In [1]:
import pandas as pd
import pandasql as ps
import numpy as np
import os
import difflib
import re
from dateutil.relativedelta import relativedelta
from collections import Counter
import collections
import time
import datetime
import timeit
from openpyxl import Workbook, load_workbook
import xlrd
import csv

# Data Import

## Quarterly reports

In [2]:
try:
    os.chdir(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\quarterlyReports-Original')
except FileNotFoundError:
    os.chdir(r'C:\Users\edwar\PH_data\data_files\quarterlyReports-Original')

os.getcwd()

'\\\\appserv\\UserShares\\dejesuse\\My Documents\\PH tables\\quarterlyReports-Original'

In [3]:
file_names = os.listdir()
file_names

['cy20q3-DHS.xlsx',
 'cy20q3-DSS.docx',
 'cy20q3-supportive.xlsx',
 'cy20q3-WJP.xlsx',
 'cy20q4-DHS.xlsx',
 'cy20q4-DSS.xlsx',
 'cy20q4-supportive.xlsx',
 'cy20q4-WJP.xlsx',
 'cy21q1-DHS.xlsx',
 'cy21q1-DSS.xlsx',
 'cy21q1-supportive.xlsx',
 'cy21q1-WJP.xlsx',
 'cy21q2-DHS.xlsx',
 'cy21q2-DSS.xlsx',
 'cy21q2-supportive.xlsx',
 'cy21q2-WJP.xlsx']

In [4]:
path = os.getcwd()

# read in Client List sheets from Excel files

sheets = {}
for file in file_names:
    file_path = f'{path}\\{file}'
    if file_path[-4:] != 'xlsx':
        continue
    else:
        sheets[file[:-5]] = pd.read_excel(file_path)

C:\Users\dejesuse\Anaconda3\lib\site-packages\openpyxl\worksheet\_reader.py:312: UserWarning: Data Validation extension is not supported and will be removed
  warn(msg)


In [5]:
# check if files follow naming convention

for sheet in sheets.keys():
    if not re.match('cy\d{2}q\d{1}-\w+', sheet):
        print(sheet, 'voilates naming convention')

In [6]:
sheet_names = {}
for file in file_names:
    file_path = f'{path}\\{file}'
    if file_path[-4:] != 'xlsx':
        continue
    else:
        xl = pd.ExcelFile(file_path)
        sheet_names[file] = xl.sheet_names

In [7]:
children_sheets = {}
for spreadsheet, sheet_name in sheet_names.items():
    for sheet in sheet_name:
        if ('children' in sheet.lower()) or ('child' in sheet.lower()):
            file_path = f'{path}\\{spreadsheet}'
            children_sheets[spreadsheet[:-5]] = pd.read_excel(file_path, sheet_name=sheet)

In [8]:
employment_sheets = {}
for spreadsheet, sheet_name in sheet_names.items():
    for sheet in sheet_name:
        if ('employment' in sheet.lower()):
            file_path = f'{path}\\{spreadsheet}'
            employment_sheets[spreadsheet[:-5]] = pd.read_excel(file_path, sheet_name=sheet)

In [9]:
medical_sheets = {}
for spreadsheet, sheet_name in sheet_names.items():
    for sheet in sheet_name:
        if ('medical' in sheet.lower()):
            file_path = f'{path}\\{spreadsheet}'
            medical_sheets[spreadsheet[:-5]] = pd.read_excel(file_path, sheet_name=sheet)

In [10]:
community_sheets = {}
for spreadsheet, sheet_name in sheet_names.items():
    for sheet in sheet_name:
        if ('community' in sheet.lower()):
            file_path = f'{path}\\{spreadsheet}'
            community_sheets[spreadsheet[:-5]] = pd.read_excel(file_path, sheet_name=sheet)

In [11]:
appt_sheets = {}
for spreadsheet, sheet_name in sheet_names.items():
    for sheet in sheet_name:
        if ('appointment' in sheet.lower()):
            file_path = f'{path}\\{spreadsheet}'
            appt_sheets[spreadsheet[:-5]] = pd.read_excel(file_path, sheet_name=sheet)

In [12]:
self_sheets = {}
for spreadsheet, sheet_name in sheet_names.items():
    for sheet in sheet_name:
        if ('sufficie' in sheet.lower()):
            file_path = f'{path}\\{spreadsheet}'
            self_sheets[spreadsheet[:-5]] = pd.read_excel(file_path, sheet_name=sheet)

C:\Users\dejesuse\Anaconda3\lib\site-packages\openpyxl\worksheet\header_footer.py:48: UserWarning: Cannot parse header or footer so it will be ignored
  warn("""Cannot parse header or footer so it will be ignored""")


### Data Cleaning

#### Adults

In [13]:
'cy20q3-supportive'[7:]

'supportive'

In [14]:
for df_name, df in sheets.items():
    
    start_year = 2019
    
    for i, column in enumerate(df.columns):
        if (df_name[7:] == 'supportive') and (re.match('mental health needs qtr \d\w{2}', str(column).lower())):
            print(df_name, i, column, column[:19]+" "+str(start_year)+" "+column[20:], sep = ' - ')
            df.rename(columns={column: column[:19]+" "+str(start_year)+" "+column[20:]},inplace=True)
            if int(column.strip()[-3]) == 4:
                start_year +=1
        elif re.match('mental health needs qtr \d\w{2}', str(column).lower()):
            year = pd.to_datetime(df_name[2:4], format = '%y').year
            df.rename(columns={column: column[:19]+" "+str(year)+" "+column[20:]},inplace=True)
        
                
            

cy20q3-supportive - 18 - Mental Health Needs QTR 1st - Mental Health Needs 2019 QTR 1st
cy20q3-supportive - 23 - Mental Health Needs QTR 2nd - Mental Health Needs 2019 QTR 2nd
cy20q3-supportive - 28 - Mental Health Needs QTR 3rd - Mental Health Needs 2019 QTR 3rd
cy20q3-supportive - 33 - Mental Health Needs QTR 4th - Mental Health Needs 2019 QTR 4th
cy20q3-supportive - 38 - Mental Health Needs QTR 1st  - Mental Health Needs 2020 QTR 1st 
cy20q3-supportive - 43 - Mental Health Needs QTR 2nd   - Mental Health Needs 2020 QTR 2nd  
cy20q3-supportive - 48 - Mental Health Needs QTR 3rd   - Mental Health Needs 2020 QTR 3rd  
cy20q4-supportive - 18 - Mental Health Needs QTR 1st - Mental Health Needs 2019 QTR 1st
cy20q4-supportive - 23 - Mental Health Needs QTR 2nd - Mental Health Needs 2019 QTR 2nd
cy20q4-supportive - 28 - Mental Health Needs QTR 3rd - Mental Health Needs 2019 QTR 3rd
cy20q4-supportive - 33 - Mental Health Needs QTR 4th - Mental Health Needs 2019 QTR 4th
cy20q4-supportive - 38

In [15]:
#check for duplicate columns

for df_name, df in sheets.items():
    for column in df.columns:
        if df.columns.to_list().count(column) > 1:
            print(df_name, column, sep=' - ')

In [16]:
for df_name, df in sheets.items():
    
    for i, column in enumerate(df.columns):
        if re.match('mental health needs qtr \d\w{2}', str(column).lower()):
            print(df_name, column, sep = ' - ')

In [17]:
for df_name, df in sheets.items():
    
    start_year = 2019
    
    for i, column in enumerate(df.columns):
        if ((df_name == 'cy20q4-supportive') or (df_name == 'cy21q1-supportive')) and ('mhp 2020 qtr 1st' in str(column).lower()):
            if i == 59:
                df.rename(columns={column: 'MHP 2021 QTR 1st' }, inplace=True)
#             print(i, column)
# #             df.rename(columns={column: column[:19]+" "+str(start_year)+" "+column[20:]},inplace=True)
# #             if int(column.strip()[-3]) == 4:
# #                 start_year +=1

In [18]:
for df_name, df in sheets.items():
    for column in df.columns:
        
        df.rename(columns={column: re.sub(r' +', ' ', column).strip()}, inplace=True)

        if str(column).strip() == 'Substance Use 202 QTR 4th':
            df.rename(columns={column: 'Substance Use 2021 QTR 4th'}, inplace=True)
        elif str(column).strip() == 'Substance Use Provider 2020 2nd QTR':
            df.rename(columns={column: 'Substance Use Provider 2020 QTR 2nd'}, inplace=True)
        elif str(column).strip() == 'Substance Use Provider 2020 3rdQTR':
            df.rename(columns={column: 'Substance Use Provider 2020 QTR 3rd'}, inplace=True)
        elif str(column).strip() == 'Substance Use Provider 2021 1st QTR':
            df.rename(columns={column: 'Substance Use Provider 2021 QTR 1st'}, inplace=True)
        elif str(column).strip() == 'Substance Use Provider 2021 2nd QTR':
            df.rename(columns={column: 'Substance Use Provider 2021 QTR 2nd'}, inplace=True)
        elif str(column).strip() == 'Substance Use Provider 2020 4th QTR':
            df.rename(columns={column: 'Substance Use Provider 2020 QTR 4th'}, inplace=True)
        elif str(column).strip() == 'PCP 2021 TR 2nd':
            df.rename(columns={column: 'PCP 2021 QTR 2nd'}, inplace=True)
        elif str(column).strip() == 'Client Name (Do not Type)':
            df.rename(columns={column: 'Client Name'}, inplace=True)
        

In [19]:
#check for duplicate columns

for df_name, df in sheets.items():
    for i, column in enumerate(df.columns):
        if df.columns.to_list().count(column) > 1:
            print(i, df_name, column, sep=' - ')

In [20]:
# changed column named MHP 2020 QTR 1st instead of MHP 2021 QTR 1st 

for df_name, df in sheets.items():
    if df_name == 'cy21q1-supportive':
        df.columns.values[59] = 'MHP 2021 QTR 1st'

In [21]:
# '02/072021' and '07.12.2021'

# PH_Master_Client_list['Quarterly_rpts_DOB'] = PH_Master_Client_list['Quarterly_rpts_DOB'].replace({"##########": pd.NaT, '11/11/19888':'11/11/1988'})

for df_name, df in sheets.items():
    for index, row in df.iterrows():
        if row['Program End Date'] == '02/072021':
            df.loc[index, 'Program End Date'] = pd.to_datetime('02/07/2021')
        elif row['Program End Date'] == '07.12.2021':
            df.loc[index, 'Program End Date'] = pd.to_datetime('07.12.2021')
        elif (str(row["Client's First Name"]).lower() == 'ashley') & (str(row["Client's Last Name"]).lower() == 'mazyck'):
            if row['Program End Date'] == pd.to_datetime('2021-12-30'):
                df.loc[index, 'Program End Date'] = pd.to_datetime('2020-12-30')
        elif row["Client's DOB"] == "##########":
            df.loc[index, "Client's DOB"] = pd.NaT
        elif row["Client's DOB"] == '11/11/19888':
            df.loc[index, "Client's DOB"] = pd.to_datetime('11/11/1988')

In [22]:
for df_name, df in sheets.items():
    for index, row in df.iterrows():
        for column in df.columns:
            if str(column) == 'Client Name (Do not Type)':          
                df.loc[index, column] = re.sub(r' +', ' ', str(row[column])).strip().title()
            elif str(column) == "Client's First Name":
                df.loc[index, column] = str(row[column]).strip().title()
            elif str(column) == "Client's Last Name":
                df.loc[index, column] = str(row[column]).strip().title()
            elif str(column) == "MHP":
                df.rename(columns={column:'MHP at intake'}, inplace=True)
            elif str(column) == 'Medical Condition':
                df.rename(columns={column: 'Medical Condition at intake'}, inplace=True)
            elif str(column) == 'Mental Health Needs':
                df.rename(columns={column: 'Mental Health Needs at intake'}, inplace=True)
            elif str(column) == 'PCP':
                df.rename(columns={column: 'PCP at intake'}, inplace=True)  
            elif str(column) == 'Substance Use Provider':
                df.rename(columns={column: 'Substance Use Provider at intake'}, inplace=True)     
            elif str(column) == 'Substance Use':
                df.rename(columns={column: 'Substance Use at intake'}, inplace=True)
            elif 'eth' in str(column).lower():
                if str(row[column]) == 'Non-Hispanic':
                    df.loc[index, column] = 'Non Hispanic'

In [23]:
for df_name, df in sheets.items():
    for index, row in df.iterrows():
        if (row["Client's First Name"].lower().strip() ==  'allana') & (row["Client's Last Name"].lower().strip() ==  'brissett'):
            df.loc[index, "Client's DOB"] = pd.to_datetime("1993-4-17", format='%Y-%m-%d')
        elif (row["Client's First Name"].lower().strip() ==  'alisia') & (row["Client's Last Name"].lower().strip() ==  'kingdom'):
            df.loc[index, "Client's DOB"] = pd.to_datetime("1992-5-22", format='%Y-%m-%d')     
        elif (row["Client's First Name"].lower().strip() ==  'shanel') & (row["Client's Last Name"].lower().strip() ==  'hugee'):
            df.loc[index, "Client's DOB"] = pd.to_datetime("1989-8-22", format='%Y-%m-%d') 
        elif (row["Client's First Name"].lower().strip() ==  'narci') & (row["Client's Last Name"].lower().strip() ==  'genoa'):
            df.loc[index, "Client's Last Name"] = 'Genao'
        elif (row["Client's First Name"].lower().strip() ==  'cindy') & (row["Client's Last Name"].lower().strip() ==  'ramikishun'):
            df.loc[index, "Client's Last Name"] = 'RAMKISHUN'.title()
        elif (row["Client's First Name"].lower().strip() ==  'donna') & (row["Client's Last Name"].lower().strip() ==  'pickersgill'):
            df.loc[index, "Client's Last Name"] = 'PICKERSGILL-BROWN'.title()
        elif (row["Client's First Name"].lower().strip() ==  'garry') & (row["Client's Last Name"].lower().strip() ==  'isaac'):
            df.loc[index, "Client's First Name"] = 'GARY'.title()
        elif (row["Client's First Name"].lower().strip() ==  'georgina') & (row["Client's Last Name"].lower().strip() ==  'deanton'):
            df.loc[index, "Client's Last Name"] = 'DEATON'.title()
        elif (row["Client's First Name"].lower().strip() ==  'irena') & (row["Client's Last Name"].lower().strip() ==  'zdrowska'):
            df.loc[index, "Client's Last Name"] = 'ZDRODOWSKA'.title()
        elif (row["Client's First Name"].lower().strip() ==  'roberto') & (row["Client's Last Name"].lower().strip() ==  'velazquez'):
            df.loc[index, "Client's Last Name"] = 'VELAZQUEZ-CABAN'.title()
        elif (row["Client's First Name"].lower().strip() ==  'tawanna') & (row["Client's Last Name"].lower().strip() ==  'horton'):
            df.loc[index, "Client's First Name"] = 'TAWANA'.title()
        elif (row["Client's First Name"].lower().strip() ==  'toniesah') & (row["Client's Last Name"].lower().strip() ==  'jackson'):
            df.loc[index, "Client's First Name"] = 'TONIESHA'.title()
        elif (row["Client's First Name"].lower().strip() ==  'wilmary') & (row["Client's Last Name"].lower().strip() ==  'pagan'):
            df.loc[index, "Client's Last Name"] = 'PAGAN GORDIAN'.title()
        elif (row["Client's First Name"].lower().strip() ==  'jenna') & (row["Client's Last Name"].lower().strip() ==  'mallet'):
            df.loc[index, "Client's Last Name"] = 'MALLETT'.title()
        elif (row["Client's First Name"].lower().strip() ==  'khilah') & (row["Client's Last Name"].lower().strip() ==  'vaughan'):
            df.loc[index, "Client's Last Name"] = 'VAUGHN'.title()
        elif (row["Client's First Name"].lower().strip() ==  'rosalba') & (row["Client's Last Name"].lower().strip() ==  'solano'):
            df.drop(index, inplace=True)
        elif (row["Client's First Name"].lower().strip() ==  'cheri') & (row["Client's Last Name"].lower().strip() ==  'la croix'):
            df.loc[index, "Client's Last Name"] = 'LACROIX'.title()
        elif (row["Client's First Name"].lower().strip() ==  'michaella') & (row["Client's Last Name"].lower().strip() ==  'doroneth'):
            df.loc[index, "Client's Last Name"] = 'DERONETH'.title()
        elif (row["Client's First Name"].lower().strip() ==  'maria zuniga') & (row["Client's Last Name"].lower().strip() ==  'miranda'):
            df.loc[index, "Client's Last Name"] = 'ZUNIGA MIRANDA'.title()  
            df.loc[index, "Client's First Name"] = 'MARIA'.title()  
        elif (row["Client's First Name"].lower().strip() ==  'lucy medina') & (row["Client's Last Name"].lower().strip() ==  'amaya'):
            df.loc[index, "Client's Last Name"] = 'MEDINA AMAYA'.title()  
            df.loc[index, "Client's First Name"] = 'LUCY'.title()
        elif (row["Client's First Name"].lower().strip() ==  'shakeym') & (row["Client's Last Name"].lower().strip() ==  'barquero'):
            df.loc[index, "Client's Last Name"] = 'BIVINS BARQUERO'.title()  
            df.loc[index, "Client's First Name"] = 'SHAKEYMA'.title()   
        elif (row["Client's First Name"].lower().strip() ==  'eugenia') & (row["Client's Last Name"].lower().strip() ==  'joseph'):
            df.loc[index, "Client's Last Name"] = 'JOSEPHS'.title()    
        elif (row["Client's First Name"].lower().strip() ==  'lennette') & (row["Client's Last Name"].lower().strip() ==  'edwards'):
            df.loc[index, "Client's First Name"] = 'LENNETT'.title()      
        elif (row["Client's First Name"].lower().strip() ==  'jennifer') & (row["Client's Last Name"].lower().strip() ==  'saint vil'):
            df.loc[index, "Client's Last Name"] = 'SAINTVIL'.title()        
        elif (row["Client's First Name"].lower().strip() ==  'adrianna') & (row["Client's Last Name"].lower().strip() ==  'overton'):
            df.loc[index, "Client's First Name"] = 'ADRIANA'.title()    
        elif (row["Client's First Name"].lower().strip() ==  'jocelyn') & (row["Client's Last Name"].lower().strip() ==  'white'):
            df.loc[index, "Client's First Name"] = 'JOCELYNN'.title()    
            df.loc[index, "Client's Last Name"] = 'FINKLEA'.title()   
        elif (row["Client's First Name"].lower().strip() ==  'roland') & (row["Client's Last Name"].lower().strip() ==  'jackson'):
            df.loc[index, "Client's First Name"] = 'ROLANDA'.title()    
        elif (row["Client's First Name"].lower().strip() == 'jully') & (row["Client's Last Name"].lower().strip() == 'harry-herrera'):
            df.loc[index, "Client's Last Name"] = 'Harry Herrera' 
            df.loc[index, "Client's DOB"] = pd.to_datetime("1997-5-29", format='%Y-%m-%d')    
        elif (row["Client's First Name"].lower().strip() == 'jully') & (row["Client's Last Name"].lower().strip() == 'harry herrera'):
            df.loc[index, "Client's DOB"] = pd.to_datetime("1997-5-29", format='%Y-%m-%d')
        elif (row["Client's First Name"].lower().strip() == 'octavia') & (row["Client's Last Name"].lower().strip() == 'elliot'):
            df.loc[index, "Client's Last Name"] = 'Elliott'    
        elif (row["Client's First Name"].lower().strip() == 'wendy') & (row["Client's Last Name"].lower().strip() == 'castilo'):
            df.loc[index, "Client's Last Name"] = 'Castillo'    
        elif (row["Client's First Name"].lower().strip() == 'loudres') & (row["Client's Last Name"].lower().strip() == 'montero'):
            df.loc[index, "Client's First Name"] = 'Lourdes'  
        elif (row["Client's First Name"].lower().strip() == 'mamasir') & (row["Client's Last Name"].lower().strip() == 'rodriguez'):
            df.loc[index, "Client's First Name"] = 'Mamasir Maria'
            df.loc[index, "Client's Last Name"] = 'Rodriquez'  

#### Children

In [24]:
for df_name, df in children_sheets.items():
    for column in df.columns:
        if 'parent' in column.lower():
            df.rename(columns={column: 'Parent_Name'}, inplace=True)

In [25]:
for df_name, df in children_sheets.items():
    for index, row in df.iterrows():
        if str(row['Parent_Name']).lower().strip() == 'marilu\xa0 santos':
            df.loc[index, 'Parent_Name'] = 'Marilu Santos'
        elif str(row['Parent_Name']).lower().strip() == 'jewel cordova':
            df.loc[index, 'Parent_Name'] = 'Jewell Cordova'
        elif str(row['Parent_Name']).lower().strip() == 'ta’Sheena johnson':
            df.loc[index, 'Parent_Name'] = 'Tasheena Johnson'         
        elif str(row['Parent_Name']).lower().strip() ==  'narci genoa':           
            df.loc[index, 'Parent_Name'] = 'narci Genao'.title()
        elif str(row['Parent_Name']).lower().strip() ==  'cindy ramikishun':
            df.loc[index, 'Parent_Name'] = 'cindy RAMKISHUN'.title()    
        elif str(row['Parent_Name']).lower().strip() ==  'donna pickersgill':
            df.loc[index, 'Parent_Name'] = 'donna PICKERSGILL-BROWN'.title()    
        elif str(row['Parent_Name']).lower().strip() ==  'garry isaac':
            df.loc[index, 'Parent_Name'] = 'GARY isaac'.title()    
        elif str(row['Parent_Name']).lower().strip() ==  'georgina deanton':
            df.loc[index, 'Parent_Name'] = 'georgina DEATON'.title()    
        elif str(row['Parent_Name']).lower().strip() ==  'irena zdrowska':
            df.loc[index, 'Parent_Name'] = 'irena ZDRODOWSKA'.title()    
        elif str(row['Parent_Name']).lower().strip() ==   'roberto velazquez':
            df.loc[index, 'Parent_Name'] = 'roberto VELAZQUEZ-CABAN'.title()    
        elif str(row['Parent_Name']).lower().strip() == 'tawanna horton':
            df.loc[index, 'Parent_Name'] = 'TAWANA horton'.title()    
        elif str(row['Parent_Name']).lower().strip() ==  'toniesah jackson':
            df.loc[index, 'Parent_Name'] = 'TONIESHA jackson'.title()
        elif str(row['Parent_Name']).lower().strip() ==  'wilmary pagan':
            df.loc[index, 'Parent_Name'] = 'wilmary PAGAN GORDIAN'.title()
        elif str(row['Parent_Name']).lower().strip() ==  'jenna mallet':
            df.loc[index, 'Parent_Name'] = 'jenna MALLETT'.title()
        elif str(row['Parent_Name']).lower().strip() ==  'khilah vaughan':
            df.loc[index, 'Parent_Name'] = 'khilah VAUGHN'.title()
        elif str(row['Parent_Name']).lower().strip() ==  'rosalba solano':
            df.loc[index, 'Parent_Name'] = 'rosalbo solano'.title()
        elif str(row['Parent_Name']).lower().strip() ==  'cheri la croix':
            df.loc[index, 'Parent_Name'] = 'cheri LACROIX'.title()
        elif str(row['Parent_Name']).lower().strip() ==  'michaella doroneth':
            df.loc[index, 'Parent_Name'] = 'michaella DERONETH'.title()
        elif str(row['Parent_Name']).lower().strip() ==  'maria zuniga miranda':
            df.loc[index, 'Parent_Name'] = 'maria ZUNIGA MIRANDA'.title()    
        elif str(row['Parent_Name']).lower().strip() ==  'lucy medina amaya':
            df.loc[index, 'Parent_Name'] = 'lucy MEDINA AMAYA'.title()  
        elif str(row['Parent_Name']).lower().strip() ==  'shakeym barquero':
            df.loc[index, 'Parent_Name'] = 'SHAKEYMA BIVINS BARQUERO'.title()     
        elif str(row['Parent_Name']).lower().strip() ==  'eugenia joseph':
            df.loc[index, 'Parent_Name'] = 'eugenia JOSEPHS'.title()    
        elif str(row['Parent_Name']).lower().strip() ==  'lennette edwards':
            df.loc[index, 'Parent_Name'] = 'LENNETT edwards'.title()      
        elif str(row['Parent_Name']).lower().strip() ==  'jennifer saint vil':
            df.loc[index, 'Parent_Name'] = 'jennifer SAINTVIL'.title()        
        elif str(row['Parent_Name']).lower().strip() ==  'adrianna overton':
            df.loc[index, 'Parent_Name'] = 'ADRIANA overton'.title()    
        elif str(row['Parent_Name']).lower().strip() ==  'jocelyn white':
            df.loc[index, 'Parent_Name'] = 'JOCELYNN FINKLEA'.title()  
        elif str(row['Parent_Name']).lower().strip() ==  'roland jackson':
            df.loc[index, 'Parent_Name'] = 'ROLANDA jackson'.title()
        elif str(row["Parent_Name"]).lower().strip() == 'jully harry-herrera':
            df.loc[index, "Parent_Name"] = 'jully Harry Herrera'.title() 
        elif str(row["Parent_Name"]).lower().strip() == 'octavia elliot':
            df.loc[index, "Parent_Name"] = 'octavia Elliott'.title()    
        elif str(row["Parent_Name"]).lower().strip() == 'wendy castilo':
            df.loc[index, "Parent_Name"] = 'wendy Castillo'.title()    
        elif str(row["Parent_Name"]).lower().strip() == 'loudres montero':
            df.loc[index, "Parent_Name"] = 'Lourdes montero'.title()  
        elif str(row["Parent_Name"]).lower().strip() == 'mamasir rodriguez':
            df.loc[index, "Parent_Name"] = 'Mamasir Maria Rodriquez' 

In [26]:
for df_name, df in children_sheets.items():
    for index, row in df.iterrows():
        if str(row['DayCare_Start_Date']).lower() == 'yes':
            df.loc[index, 'DayCare_Start_Date'] = np.nan
        elif str(row['DayCare_Start_Date']).lower() == 'no':
            df.loc[index, 'DayCare_Start_Date'] = np.nan
        elif str(row['DayCare_Start_Date']).lower() == "ct won't say":
            df.loc[index, 'DayCare_Start_Date'] = np.nan
        elif str(row['PreSchool_Start_Date']).lower() == "yes":
            df.loc[index, 'PreSchool_Start_Date'] = np.nan
        elif str(row['Primary_School_Start_Date']).lower() == "n/a":
            df.loc[index, 'Primary_School_Start_Date'] = np.nan    
            

#### Employment

In [27]:
for df_name, df in employment_sheets.items():
    for index, row in df.iterrows():
        if isinstance(row['Client Name'], datetime.datetime):
            df.drop(index, inplace=True)

In [28]:
# 'Not employed' or 'not employed ' and '5/25/2021 / 6/23/2021 for Natori Baker

for df_name, df in employment_sheets.items():
    for col in df.columns:
        if 'date' in col.lower():
            for index, row in df.iterrows():
                if str(row[col]).lower().strip() == 'not employed':
                    df.loc[index, col] = pd.NaT
                elif str(row[col]) == '5/25/2021 / 6/23/2021':
                    df.loc[index, col] = pd.to_datetime('5/25/2021')
                    df.loc[index, 'Employer Name'] = 'Metro Strategies'
                    df.loc[index, 'Position'] = 'Canvasser'

In [29]:
for df_name, df in employment_sheets.items():
    for index, row in df.iterrows():
        if pd.isna(row['Client Name']):
            continue
        else:
            df.loc[index, 'Client Name'] = re.sub(r' +', ' ', str(row['Client Name']).strip().title())

In [30]:
for df_name, df in employment_sheets.items():
    for index, row in df.iterrows():
        if str(row['Client Name']).lower().strip() == 'marilu\xa0 santos':
            df.loc[index, 'Client Name'] = 'Marilu Santos'
        elif str(row['Client Name']).lower().strip() == 'jewel cordova':
            df.loc[index, 'Client Name'] = 'Jewell Cordova'
        elif str(row['Client Name']).lower().strip() == 'ta’Sheena johnson':
            df.loc[index, 'Client Name'] = 'Tasheena Johnson'         
        elif str(row['Client Name']).lower().strip() ==  'narci genoa':           
            df.loc[index, 'Client Name'] = 'narci Genao'.title()
        elif str(row['Client Name']).lower().strip() ==  'cindy ramikishun':
            df.loc[index, 'Client Name'] = 'cindy RAMKISHUN'.title()    
        elif str(row['Client Name']).lower().strip() ==  'donna pickersgill':
            df.loc[index, 'Client Name'] = 'donna PICKERSGILL-BROWN'.title()    
        elif str(row['Client Name']).lower().strip() ==  'garry isaac':
            df.loc[index, 'Client Name'] = 'GARY isaac'.title()    
        elif str(row['Client Name']).lower().strip() ==  'georgina deanton':
            df.loc[index, 'Client Name'] = 'georgina DEATON'.title()    
        elif str(row['Client Name']).lower().strip() ==  'irena zdrowska':
            df.loc[index, 'Client Name'] = 'irena ZDRODOWSKA'.title()    
        elif str(row['Client Name']).lower().strip() ==   'roberto velazquez':
            df.loc[index, 'Client Name'] = 'roberto VELAZQUEZ-CABAN'.title()    
        elif str(row['Client Name']).lower().strip() == 'tawanna horton':
            df.loc[index, 'Client Name'] = 'TAWANA horton'.title()    
        elif str(row['Client Name']).lower().strip() ==  'toniesah jackson':
            df.loc[index, 'Client Name'] = 'TONIESHA jackson'.title()
        elif str(row['Client Name']).lower().strip() ==  'wilmary pagan':
            df.loc[index, 'Client Name'] = 'wilmary PAGAN GORDIAN'.title()
        elif str(row['Client Name']).lower().strip() ==  'jenna mallet':
            df.loc[index, 'Client Name'] = 'jenna MALLETT'.title()
        elif str(row['Client Name']).lower().strip() ==  'khilah vaughan':
            df.loc[index, 'Client Name'] = 'khilah VAUGHN'.title()
        elif str(row['Client Name']).lower().strip() ==  'rosalba solano':
            df.loc[index, 'Client Name'] = 'rosalbo solano'.title()
        elif str(row['Client Name']).lower().strip() ==  'cheri la croix':
            df.loc[index, 'Client Name'] = 'cheri LACROIX'.title()
        elif str(row['Client Name']).lower().strip() ==  'michaella doroneth':
            df.loc[index, 'Client Name'] = 'michaella DERONETH'.title()
        elif str(row['Client Name']).lower().strip() ==  'maria zuniga miranda':
            df.loc[index, 'Client Name'] = 'maria ZUNIGA MIRANDA'.title()    
        elif str(row['Client Name']).lower().strip() ==  'lucy medina amaya':
            df.loc[index, 'Client Name'] = 'lucy MEDINA AMAYA'.title()  
        elif str(row['Client Name']).lower().strip() ==  'shakeym barquero':
            df.loc[index, 'Client Name'] = 'SHAKEYMA BIVINS BARQUERO'.title()     
        elif str(row['Client Name']).lower().strip() ==  'eugenia joseph':
            df.loc[index, 'Client Name'] = 'eugenia JOSEPHS'.title()    
        elif str(row['Client Name']).lower().strip() ==  'lennette edwards':
            df.loc[index, 'Client Name'] = 'LENNETT edwards'.title()      
        elif str(row['Client Name']).lower().strip() ==  'jennifer saint vil':
            df.loc[index, 'Client Name'] = 'jennifer SAINTVIL'.title()        
        elif str(row['Client Name']).lower().strip() ==  'adrianna overton':
            df.loc[index, 'Client Name'] = 'ADRIANA overton'.title()    
        elif str(row['Client Name']).lower().strip() ==  'jocelyn white':
            df.loc[index, 'Client Name'] = 'JOCELYNN FINKLEA'.title()  
        elif str(row['Client Name']).lower().strip() ==  'roland jackson':
            df.loc[index, 'Client Name'] = 'ROLANDA jackson'.title()
        elif str(row['Client Name']).lower().strip() == 'jully harry- herrera':
            df.loc[index, 'Client Name'] = 'jully Harry Herrera'.title() 
        elif str(row['Client Name']).lower().strip() == 'octavia elliot':
            df.loc[index, 'Client Name'] = 'octavia Elliott'.title()    
        elif str(row['Client Name']).lower().strip() == 'wendy castilo':
            df.loc[index, 'Client Name'] = 'wendy Castillo'.title()    
        elif str(row['Client Name']).lower().strip() == 'loudres montero':
            df.loc[index, 'Client Name'] = 'Lourdes montero'.title()
        elif str(row["Client Name"]).lower().strip() == 'mamasir rodriguez':
            df.loc[index, "Client Name"] = 'Mamasir Maria Rodriquez' 

In [31]:
for df_name, df in employment_sheets.items():
    for column in df.columns:
        if str(column) == 'Employment   Start Date' or str(column) == 'Employment Start Date':
            df.rename(columns={column: 'Employment_StartDate'}, inplace=True)
        elif str(column) == 'Employment   End Date' or str(column) == 'Employment End Date':
            df.rename(columns={column: 'Employment_EndDate'}, inplace=True)
        elif str(column) == 'Off-The-Books ':
            df.rename(columns={column: column.strip()}, inplace=True)

In [32]:
for df_name, df in employment_sheets.items():
    for col in df.columns:
        if 'salary' in col.lower():
            for index, row in df.iterrows():
                if 'hr' in str(row[col]).lower():
                    df.loc[index, col] = float(str(row[col]).strip()[:-2].replace('$', ''))
                elif 'monthly' in str(row[col]).lower():
                    df.loc[index, col] = ((float(str((row[col]).strip()[:-7]))) * 12 / 52) / 40
                elif 'wk' in str(row[col]).lower():
                    df.loc[index, col] = float(str(row[col]).strip()[:-2].replace('$', ''))/40
                elif 'day' in str(row[col]).lower():
                    df.loc[index, col] = float(str(row[col]).strip()[:-3].replace('$', ''))/8
                elif isinstance(row[col], datetime.date):
                    if pd.isna(row[col]):
                        continue
                    else:
                        df.loc[index, col] = row[col].day

#### Medical

In [33]:
for df_name, df in medical_sheets.items():
    for index, row in df.iterrows():
        if pd.isna(row['Client Name']):
            continue
        else:
            df.loc[index, 'Client Name'] = re.sub(r' +', ' ', str(row['Client Name']).strip().title())

In [34]:
for df_name, df in medical_sheets.items():
    for index, row in df.iterrows():
        if str(row['Client Name']).lower().strip() == 'marilu\xa0 santos':
            df.loc[index, 'Client Name'] = 'Marilu Santos'
        elif str(row['Client Name']).lower().strip() == 'jewel cordova':
            df.loc[index, 'Client Name'] = 'Jewell Cordova'
        elif str(row['Client Name']).lower().strip() == 'ta’Sheena johnson':
            df.loc[index, 'Client Name'] = 'Tasheena Johnson'         
        elif str(row['Client Name']).lower().strip() ==  'narci genoa':           
            df.loc[index, 'Client Name'] = 'narci Genao'.title()
        elif str(row['Client Name']).lower().strip() ==  'cindy ramikishun':
            df.loc[index, 'Client Name'] = 'cindy RAMKISHUN'.title()    
        elif str(row['Client Name']).lower().strip() ==  'donna pickersgill':
            df.loc[index, 'Client Name'] = 'donna PICKERSGILL-BROWN'.title()    
        elif str(row['Client Name']).lower().strip() ==  'garry isaac':
            df.loc[index, 'Client Name'] = 'GARY isaac'.title()    
        elif str(row['Client Name']).lower().strip() ==  'georgina deanton':
            df.loc[index, 'Client Name'] = 'georgina DEATON'.title()    
        elif str(row['Client Name']).lower().strip() ==  'irena zdrowska':
            df.loc[index, 'Client Name'] = 'irena ZDRODOWSKA'.title()    
        elif str(row['Client Name']).lower().strip() ==   'roberto velazquez':
            df.loc[index, 'Client Name'] = 'roberto VELAZQUEZ-CABAN'.title()    
        elif str(row['Client Name']).lower().strip() == 'tawanna horton':
            df.loc[index, 'Client Name'] = 'TAWANA horton'.title()    
        elif str(row['Client Name']).lower().strip() ==  'toniesah jackson':
            df.loc[index, 'Client Name'] = 'TONIESHA jackson'.title()
        elif str(row['Client Name']).lower().strip() ==  'wilmary pagan':
            df.loc[index, 'Client Name'] = 'wilmary PAGAN GORDIAN'.title()
        elif str(row['Client Name']).lower().strip() ==  'jenna mallet':
            df.loc[index, 'Client Name'] = 'jenna MALLETT'.title()
        elif str(row['Client Name']).lower().strip() ==  'khilah vaughan':
            df.loc[index, 'Client Name'] = 'khilah VAUGHN'.title()
        elif str(row['Client Name']).lower().strip() ==  'rosalba solano':
            df.loc[index, 'Client Name'] = 'rosalbo solano'.title()
        elif str(row['Client Name']).lower().strip() ==  'cheri la croix':
            df.loc[index, 'Client Name'] = 'cheri LACROIX'.title()
        elif str(row['Client Name']).lower().strip() ==  'michaella doroneth':
            df.loc[index, 'Client Name'] = 'michaella DERONETH'.title()
        elif str(row['Client Name']).lower().strip() ==  'maria zuniga miranda':
            df.loc[index, 'Client Name'] = 'maria ZUNIGA MIRANDA'.title()    
        elif str(row['Client Name']).lower().strip() ==  'lucy medina amaya':
            df.loc[index, 'Client Name'] = 'lucy MEDINA AMAYA'.title()  
        elif str(row['Client Name']).lower().strip() ==  'shakeym barquero':
            df.loc[index, 'Client Name'] = 'SHAKEYMA BIVINS BARQUERO'.title()     
        elif str(row['Client Name']).lower().strip() ==  'eugenia joseph':
            df.loc[index, 'Client Name'] = 'eugenia JOSEPHS'.title()    
        elif str(row['Client Name']).lower().strip() ==  'lennette edwards':
            df.loc[index, 'Client Name'] = 'LENNETT edwards'.title()      
        elif str(row['Client Name']).lower().strip() ==  'jennifer saint vil':
            df.loc[index, 'Client Name'] = 'jennifer SAINTVIL'.title()        
        elif str(row['Client Name']).lower().strip() ==  'adrianna overton':
            df.loc[index, 'Client Name'] = 'ADRIANA overton'.title()    
        elif str(row['Client Name']).lower().strip() ==  'jocelyn white':
            df.loc[index, 'Client Name'] = 'JOCELYNN FINKLEA'.title()  
        elif str(row['Client Name']).lower().strip() ==  'roland jackson':
            df.loc[index, 'Client Name'] = 'ROLANDA jackson'.title()
        elif str(row['Client Name']).lower().strip() == 'jully harry-herrera':
            df.loc[index, 'Client Name'] = 'jully Harry Herrera'.title() 
        elif str(row['Client Name']).lower().strip() == 'octavia elliot':
            df.loc[index, 'Client Name'] = 'octavia Elliott'.title()    
        elif str(row['Client Name']).lower().strip() == 'wendy castilo':
            df.loc[index, 'Client Name'] = 'wendy Castillo'.title()    
        elif str(row['Client Name']).lower().strip() == 'loudres montero':
            df.loc[index, 'Client Name'] = 'Lourdes montero'.title()  
        elif str(row["Client Name"]).lower().strip() == 'mamasir rodriguez':
            df.loc[index, "Client Name"] = 'Mamasir Maria Rodriquez' 
        

#### Community

In [35]:
for df_name, df in community_sheets.items():
    for index, row in df.iterrows():
        if pd.isna(row['Client Name']):
            continue
        else:
            df.loc[index, 'Client Name'] = re.sub(r' +', ' ', str(row['Client Name']).strip().title())

In [36]:
for df_name, df in community_sheets.items():
    for index, row in df.iterrows():
        if str(row['Client Name']).lower().strip() == 'marilu\xa0 santos':
            df.loc[index, 'Client Name'] = 'Marilu Santos'
        elif str(row['Client Name']).lower().strip() == 'jewel cordova':
            df.loc[index, 'Client Name'] = 'Jewell Cordova'
        elif str(row['Client Name']).lower().strip() == 'ta’Sheena johnson':
            df.loc[index, 'Client Name'] = 'Tasheena Johnson'         
        elif str(row['Client Name']).lower().strip() ==  'narci genoa':           
            df.loc[index, 'Client Name'] = 'narci Genao'.title()
        elif str(row['Client Name']).lower().strip() ==  'cindy ramikishun':
            df.loc[index, 'Client Name'] = 'cindy RAMKISHUN'.title()    
        elif str(row['Client Name']).lower().strip() ==  'donna pickersgill':
            df.loc[index, 'Client Name'] = 'donna PICKERSGILL-BROWN'.title()    
        elif str(row['Client Name']).lower().strip() ==  'garry isaac':
            df.loc[index, 'Client Name'] = 'GARY isaac'.title()    
        elif str(row['Client Name']).lower().strip() ==  'georgina deanton':
            df.loc[index, 'Client Name'] = 'georgina DEATON'.title()    
        elif str(row['Client Name']).lower().strip() ==  'irena zdrowska':
            df.loc[index, 'Client Name'] = 'irena ZDRODOWSKA'.title()    
        elif str(row['Client Name']).lower().strip() ==   'roberto velazquez':
            df.loc[index, 'Client Name'] = 'roberto VELAZQUEZ-CABAN'.title()    
        elif str(row['Client Name']).lower().strip() == 'tawanna horton':
            df.loc[index, 'Client Name'] = 'TAWANA horton'.title()    
        elif str(row['Client Name']).lower().strip() ==  'toniesah jackson':
            df.loc[index, 'Client Name'] = 'TONIESHA jackson'.title()
        elif str(row['Client Name']).lower().strip() ==  'wilmary pagan':
            df.loc[index, 'Client Name'] = 'wilmary PAGAN GORDIAN'.title()
        elif str(row['Client Name']).lower().strip() ==  'jenna mallet':
            df.loc[index, 'Client Name'] = 'jenna MALLETT'.title()
        elif str(row['Client Name']).lower().strip() ==  'khilah vaughan':
            df.loc[index, 'Client Name'] = 'khilah VAUGHN'.title()
        elif str(row['Client Name']).lower().strip() ==  'rosalba solano':
            df.loc[index, 'Client Name'] = 'rosalbo solano'.title()
        elif str(row['Client Name']).lower().strip() ==  'cheri la croix':
            df.loc[index, 'Client Name'] = 'cheri LACROIX'.title()
        elif str(row['Client Name']).lower().strip() ==  'michaella doroneth':
            df.loc[index, 'Client Name'] = 'michaella DERONETH'.title()
        elif str(row['Client Name']).lower().strip() ==  'maria zuniga miranda':
            df.loc[index, 'Client Name'] = 'maria ZUNIGA MIRANDA'.title()    
        elif str(row['Client Name']).lower().strip() ==  'lucy medina amaya':
            df.loc[index, 'Client Name'] = 'lucy MEDINA AMAYA'.title()  
        elif str(row['Client Name']).lower().strip() ==  'shakeym barquero':
            df.loc[index, 'Client Name'] = 'SHAKEYMA BIVINS BARQUERO'.title()     
        elif str(row['Client Name']).lower().strip() ==  'eugenia joseph':
            df.loc[index, 'Client Name'] = 'eugenia JOSEPHS'.title()    
        elif str(row['Client Name']).lower().strip() ==  'lennette edwards':
            df.loc[index, 'Client Name'] = 'LENNETT edwards'.title()      
        elif str(row['Client Name']).lower().strip() ==  'jennifer saint vil':
            df.loc[index, 'Client Name'] = 'jennifer SAINTVIL'.title()        
        elif str(row['Client Name']).lower().strip() ==  'adrianna overton':
            df.loc[index, 'Client Name'] = 'ADRIANA overton'.title()    
        elif str(row['Client Name']).lower().strip() ==  'jocelyn white':
            df.loc[index, 'Client Name'] = 'JOCELYNN FINKLEA'.title()  
        elif str(row['Client Name']).lower().strip() ==  'roland jackson':
            df.loc[index, 'Client Name'] = 'ROLANDA jackson'.title()
        elif str(row['Client Name']).lower().strip() == 'jully harry-herrera':
            df.loc[index, 'Client Name'] = 'jully Harry Herrera'.title() 
        elif str(row['Client Name']).lower().strip() == 'octavia elliot':
            df.loc[index, 'Client Name'] = 'octavia Elliott'.title()    
        elif str(row['Client Name']).lower().strip() == 'wendy castilo':
            df.loc[index, 'Client Name'] = 'wendy Castillo'.title()    
        elif str(row['Client Name']).lower().strip() == 'loudres montero':
            df.loc[index, 'Client Name'] = 'Lourdes montero'.title()  
        elif str(row["Client Name"]).lower().strip() == 'mamasir rodriguez':
            df.loc[index, "Client Name"] = 'Mamasir Maria Rodriquez' 
        

#### Appointments

In [37]:
for df_name, df in appt_sheets.items():
    for index, row in df.iterrows():
        if pd.isna(row['Client Name']):
            continue
        else:
            df.loc[index, 'Client Name'] = re.sub(r' +', ' ', str(row['Client Name']).strip().title())

In [38]:
for df_name, df in appt_sheets.items():
    for index, row in df.iterrows():
        if str(row['Client Name']).lower().strip() == 'marilu\xa0 santos':
            df.loc[index, 'Client Name'] = 'Marilu Santos'
        elif str(row['Client Name']).lower().strip() == 'jewel cordova':
            df.loc[index, 'Client Name'] = 'Jewell Cordova'
        elif str(row['Client Name']).lower().strip() == 'ta’Sheena johnson':
            df.loc[index, 'Client Name'] = 'Tasheena Johnson'         
        elif str(row['Client Name']).lower().strip() ==  'narci genoa':           
            df.loc[index, 'Client Name'] = 'narci Genao'.title()
        elif str(row['Client Name']).lower().strip() ==  'cindy ramikishun':
            df.loc[index, 'Client Name'] = 'cindy RAMKISHUN'.title()    
        elif str(row['Client Name']).lower().strip() ==  'donna pickersgill':
            df.loc[index, 'Client Name'] = 'donna PICKERSGILL-BROWN'.title()    
        elif str(row['Client Name']).lower().strip() ==  'garry isaac':
            df.loc[index, 'Client Name'] = 'GARY isaac'.title()    
        elif str(row['Client Name']).lower().strip() ==  'georgina deanton':
            df.loc[index, 'Client Name'] = 'georgina DEATON'.title()    
        elif str(row['Client Name']).lower().strip() ==  'irena zdrowska':
            df.loc[index, 'Client Name'] = 'irena ZDRODOWSKA'.title()    
        elif str(row['Client Name']).lower().strip() ==   'roberto velazquez':
            df.loc[index, 'Client Name'] = 'roberto VELAZQUEZ-CABAN'.title()    
        elif str(row['Client Name']).lower().strip() == 'tawanna horton':
            df.loc[index, 'Client Name'] = 'TAWANA horton'.title()    
        elif str(row['Client Name']).lower().strip() ==  'toniesah jackson':
            df.loc[index, 'Client Name'] = 'TONIESHA jackson'.title()
        elif str(row['Client Name']).lower().strip() ==  'wilmary pagan':
            df.loc[index, 'Client Name'] = 'wilmary PAGAN GORDIAN'.title()
        elif str(row['Client Name']).lower().strip() ==  'jenna mallet':
            df.loc[index, 'Client Name'] = 'jenna MALLETT'.title()
        elif str(row['Client Name']).lower().strip() ==  'khilah vaughan':
            df.loc[index, 'Client Name'] = 'khilah VAUGHN'.title()
        elif str(row['Client Name']).lower().strip() ==  'rosalba solano':
            df.loc[index, 'Client Name'] = 'rosalbo solano'.title()
        elif str(row['Client Name']).lower().strip() ==  'cheri la croix':
            df.loc[index, 'Client Name'] = 'cheri LACROIX'.title()
        elif str(row['Client Name']).lower().strip() ==  'michaella doroneth':
            df.loc[index, 'Client Name'] = 'michaella DERONETH'.title()
        elif str(row['Client Name']).lower().strip() ==  'maria zuniga miranda':
            df.loc[index, 'Client Name'] = 'maria ZUNIGA MIRANDA'.title()    
        elif str(row['Client Name']).lower().strip() ==  'lucy medina amaya':
            df.loc[index, 'Client Name'] = 'lucy MEDINA AMAYA'.title()  
        elif str(row['Client Name']).lower().strip() ==  'shakeym barquero':
            df.loc[index, 'Client Name'] = 'SHAKEYMA BIVINS BARQUERO'.title()     
        elif str(row['Client Name']).lower().strip() ==  'eugenia joseph':
            df.loc[index, 'Client Name'] = 'eugenia JOSEPHS'.title()    
        elif str(row['Client Name']).lower().strip() ==  'lennette edwards':
            df.loc[index, 'Client Name'] = 'LENNETT edwards'.title()      
        elif str(row['Client Name']).lower().strip() ==  'jennifer saint vil':
            df.loc[index, 'Client Name'] = 'jennifer SAINTVIL'.title()        
        elif str(row['Client Name']).lower().strip() ==  'adrianna overton':
            df.loc[index, 'Client Name'] = 'ADRIANA overton'.title()    
        elif str(row['Client Name']).lower().strip() ==  'jocelyn white':
            df.loc[index, 'Client Name'] = 'JOCELYNN FINKLEA'.title()  
        elif str(row['Client Name']).lower().strip() ==  'roland jackson':
            df.loc[index, 'Client Name'] = 'ROLANDA jackson'.title()
        elif str(row['Client Name']).lower().strip() == 'jully harry-herrera':
            df.loc[index, 'Client Name'] = 'jully Harry Herrera'.title() 
        elif str(row['Client Name']).lower().strip() == 'octavia elliot':
            df.loc[index, 'Client Name'] = 'octavia Elliott'.title()    
        elif str(row['Client Name']).lower().strip() == 'wendy castilo':
            df.loc[index, 'Client Name'] = 'wendy Castillo'.title()    
        elif str(row['Client Name']).lower().strip() == 'loudres montero':
            df.loc[index, 'Client Name'] = 'Lourdes montero'.title() 
        elif str(row["Client Name"]).lower().strip() == 'mamasir rodriguez':
            df.loc[index, "Client Name"] = 'Mamasir Maria Rodriquez' 
        

#### Self sufficientcy

In [39]:
for df_name, df in self_sheets.items():
    for index, row in df.iterrows():
        if pd.isna(row['Client Name']):
            continue
        else:
            df.loc[index, 'Client Name'] = re.sub(r' +', ' ', str(row['Client Name']).strip().title())

In [40]:
for df_name, df in self_sheets.items():
    for index, row in df.iterrows():
        if str(row['Client Name']).lower().strip() == 'marilu\xa0 santos':
            df.loc[index, 'Client Name'] = 'Marilu Santos'
        elif str(row['Client Name']).lower().strip() == 'jewel cordova':
            df.loc[index, 'Client Name'] = 'Jewell Cordova'
        elif str(row['Client Name']).lower().strip() == 'ta’Sheena johnson':
            df.loc[index, 'Client Name'] = 'Tasheena Johnson'         
        elif str(row['Client Name']).lower().strip() ==  'narci genoa':           
            df.loc[index, 'Client Name'] = 'narci Genao'.title()
        elif str(row['Client Name']).lower().strip() ==  'cindy ramikishun':
            df.loc[index, 'Client Name'] = 'cindy RAMKISHUN'.title()    
        elif str(row['Client Name']).lower().strip() ==  'donna pickersgill':
            df.loc[index, 'Client Name'] = 'donna PICKERSGILL-BROWN'.title()    
        elif str(row['Client Name']).lower().strip() ==  'garry isaac':
            df.loc[index, 'Client Name'] = 'GARY isaac'.title()    
        elif str(row['Client Name']).lower().strip() ==  'georgina deanton':
            df.loc[index, 'Client Name'] = 'georgina DEATON'.title()    
        elif str(row['Client Name']).lower().strip() ==  'irena zdrowska':
            df.loc[index, 'Client Name'] = 'irena ZDRODOWSKA'.title()    
        elif str(row['Client Name']).lower().strip() ==   'roberto velazquez':
            df.loc[index, 'Client Name'] = 'roberto VELAZQUEZ-CABAN'.title()    
        elif str(row['Client Name']).lower().strip() == 'tawanna horton':
            df.loc[index, 'Client Name'] = 'TAWANA horton'.title()    
        elif str(row['Client Name']).lower().strip() ==  'toniesah jackson':
            df.loc[index, 'Client Name'] = 'TONIESHA jackson'.title()
        elif str(row['Client Name']).lower().strip() ==  'wilmary pagan':
            df.loc[index, 'Client Name'] = 'wilmary PAGAN GORDIAN'.title()
        elif str(row['Client Name']).lower().strip() ==  'jenna mallet':
            df.loc[index, 'Client Name'] = 'jenna MALLETT'.title()
        elif str(row['Client Name']).lower().strip() ==  'khilah vaughan':
            df.loc[index, 'Client Name'] = 'khilah VAUGHN'.title()
        elif str(row['Client Name']).lower().strip() ==  'rosalba solano':
            df.loc[index, 'Client Name'] = 'rosalbo solano'.title()
        elif str(row['Client Name']).lower().strip() ==  'cheri la croix':
            df.loc[index, 'Client Name'] = 'cheri LACROIX'.title()
        elif str(row['Client Name']).lower().strip() ==  'michaella doroneth':
            df.loc[index, 'Client Name'] = 'michaella DERONETH'.title()
        elif str(row['Client Name']).lower().strip() ==  'maria zuniga miranda':
            df.loc[index, 'Client Name'] = 'maria ZUNIGA MIRANDA'.title()    
        elif str(row['Client Name']).lower().strip() ==  'lucy medina amaya':
            df.loc[index, 'Client Name'] = 'lucy MEDINA AMAYA'.title()  
        elif str(row['Client Name']).lower().strip() ==  'shakeym barquero':
            df.loc[index, 'Client Name'] = 'SHAKEYMA BIVINS BARQUERO'.title()     
        elif str(row['Client Name']).lower().strip() ==  'eugenia joseph':
            df.loc[index, 'Client Name'] = 'eugenia JOSEPHS'.title()    
        elif str(row['Client Name']).lower().strip() ==  'lennette edwards':
            df.loc[index, 'Client Name'] = 'LENNETT edwards'.title()      
        elif str(row['Client Name']).lower().strip() ==  'jennifer saint vil':
            df.loc[index, 'Client Name'] = 'jennifer SAINTVIL'.title()        
        elif str(row['Client Name']).lower().strip() ==  'adrianna overton':
            df.loc[index, 'Client Name'] = 'ADRIANA overton'.title()    
        elif str(row['Client Name']).lower().strip() ==  'jocelyn white':
            df.loc[index, 'Client Name'] = 'JOCELYNN FINKLEA'.title()  
        elif str(row['Client Name']).lower().strip() ==  'roland jackson':
            df.loc[index, 'Client Name'] = 'ROLANDA jackson'.title()
        elif str(row['Client Name']).lower().strip() == 'jully harry-herrera':
            df.loc[index, 'Client Name'] = 'jully Harry Herrera'.title() 
        elif str(row['Client Name']).lower().strip() == 'octavia elliot':
            df.loc[index, 'Client Name'] = 'octavia Elliott'.title()    
        elif str(row['Client Name']).lower().strip() == 'wendy castilo':
            df.loc[index, 'Client Name'] = 'wendy Castillo'.title()    
        elif str(row['Client Name']).lower().strip() == 'loudres montero':
            df.loc[index, 'Client Name'] = 'Lourdes montero'.title()  
        elif str(row["Client Name"]).lower().strip() == 'mamasir rodriguez':
            df.loc[index, "Client Name"] = 'Mamasir Maria Rodriquez' 

## Welligent reports

In [41]:
try:
    well_census_rpt = pd.read_excel(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\welligent_reports\census_report_2021.10.28_removed_anticipated_dis_col.xlsx', skiprows=22)
except FileNotFoundError:
    well_census_rpt = pd.read_excel(r'C:\Users\edwar\PH_data\data_files\welligent_reports\census_report_2021.10.28_removed_anticipated_dis_col.xlsx', skiprows=22)

well_census_rpt.head()

#      Client Name Client ID Client Alt ID              Service Site  \
0  NaN              NaN       NaN           NaN                       NaN   
1    1   Fagan, Suzette   4903459            --                      PH 4   
2    2     Gomez, Arely   5917146            --   Lincoln Residence (Wjp)   
3    3  Henderson, Jada   5796933            --        Prospect Residence   
4    4  Henderson, Jada   5796933            --  Prospect Residence (Wjp)   

  Unit Intake Date Discharge Date  TIP    Lead Clinician Level of Care Room #  \
0  NaN         NaN            NaN  NaN               NaN           NaN    NaN   
1   --         NaN            NaN    0  Diggs, Stephanie       Missing     --   
2   --         NaN            NaN    0       Azer, Emily       Missing     --   
3   --         NaN            NaN    0       Azer, Emily       Missing     --   
4   --         NaN            NaN    0       Azer, Emily       Missing     --   

  Referring    Primary Payer Primary Payer Type Region Unnamed: 16  \
0    Agency              NaN                NaN    NaN         NaN   
1   Missing  None Identified    None Identified    NaN         NaN   
2   Missing  None Identified    None Identified    NaN         NaN   
3   Missing  None Identified    None Identified    NaN         NaN   
4   Missing  None Identified    None Identified    NaN         NaN   

   Unnamed: 17  Unnamed: 18  Unnamed: 19  
0          NaN          NaN          NaN  
1          NaN          NaN          NaN  
2          NaN          NaN          NaN  
3          NaN          NaN          NaN  
4          NaN          NaN          NaN

In [42]:
try:
    well_active_clients_rpt = pd.read_excel(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\welligent_reports\active_clients_listin_report_28102021.xlsx', skiprows=12)
except FileNotFoundError:
    well_active_clients_rpt = pd.read_excel(r'C:\Users\edwar\PH_data\data_files\welligent_reports\active_clients_listin_report_28102021.xlsx', skiprows=12)

well_active_clients_rpt.head()

#         Client Name  Client ID  Client Alt ID Client Admit Date  \
0  1  Abdurrashid, Hanif          1            NaN        2013-06-14   
1  2       Abrams, Raven    5470790            NaN        2020-11-12   
2  3    Adams, Allenasia    5385740            NaN        2020-09-25   
3  4     Alqawi, Yajaira    5785529            NaN        2021-04-01   
4  5      Aronald, Adrea    4319118            NaN        2019-03-26   

                        Program                              Service Site  \
0  D'Addario Supportive Housing  D'Addario Residence - Supportive Housing   
1                          WDSS                                      PH 4   
2                     Aftercare                  Prospect Residence (Wjp)   
3                           DHS                                  Glenmore   
4                     Aftercare                   Lincoln Residence (Wjp)   

   Unit Room #  Bed #  
0   NaN     5C  #9466  
1   NaN    NaN    NaN  
2   NaN    NaN    NaN  
3   NaN    NaN    NaN  
4   NaN    NaN    NaN

In [43]:
try:
    well_member_info_rpt = pd.read_excel(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\welligent_reports\member_info_report_28102021.xlsx', skiprows=4)
except FileNotFoundError:
    well_member_info_rpt = pd.read_excel(r'C:\Users\edwar\PH_data\data_files\welligent_reports\member_info_report_28102021.xlsx', skiprows=4)
    
well_member_info_rpt.head()

Location   Name (Full - LNF)        DOB          SSN
0  Bishop Sullivan Residence    ARRINDELL, MARIE 1964-02-26  134-66-3797
1  Bishop Sullivan Residence       BERRY, TYANNA 1990-02-03  118-76-8966
2  Bishop Sullivan Residence  CATTENHEAD, SATYRA 1962-08-24          NaN
3  Bishop Sullivan Residence        CEPEDA, LISA 1963-02-12          NaN
4  Bishop Sullivan Residence      FRANCIS, LEONA 1958-05-11  104-48-2591

In [44]:
try:
    well_demographics_rpt = pd.read_excel(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\welligent_reports\clients_demographics_2021.12.01.xlsx', skiprows=4,index_col='Client ID')
except FileNotFoundError:
    well_demographics_rpt = pd.read_excel(r'C:\Users\edwar\PH_data\data_files\welligent_reports\clients_demographics_2021.12.01.xlsx', skiprows=4, index_col='Client ID')

well_demographics_rpt.head()

Location Name (Full - LNF)        DOB  \
Client ID                                                           
10         Bishop Sullivan Residence      CEPEDA, LISA 1963-02-12   
18         Bishop Sullivan Residence    FRANCIS, LEONA 1958-05-11   
20         Bishop Sullivan Residence  HAWKINS, TABITHA 1979-09-28   
3          Bishop Sullivan Residence  ARRINDELL, MARIE 1964-02-26   
30         Bishop Sullivan Residence    KARRAS, AMELIA 1961-11-20   

           Current Grade  Gender      Race  Date of Death Date of Discharge  \
Client ID                                                                     
10                   NaN  Female  Hispanic            NaN               NaT   
18                   NaN  Female     Black            NaN               NaT   
20                   NaN  Female     Black            NaN               NaT   
3                    NaN  Female     Black            NaN               NaT   
30                   NaN  Female     White            NaN               NaT   

          Discharge Reason         Ethnicity Intake Date  \
Client ID                                                  
10                     NaN          Hispanic  2014-11-22   
18                     NaN  African-American  2014-11-04   
20                     NaN  African-American  2014-11-04   
3                      NaN      Non-Hispanic  2014-11-14   
30                     NaN      Non-Hispanic  2014-11-04   

          General_Medical_Condition Highest_Education  
Client ID                                              
10                              NaN                 E  
18                         Diabetes                 A  
20                              NaN                 D  
3                      Hypertension                 F  
30                      ChronicPain                 K

In [45]:
well_demographics_rpt['Ethnicity'].replace('Non-Hispanic', 'Non Hispanic', inplace=True)

In [46]:
well_demographics_rpt['Name (Full - LNF)'] = well_demographics_rpt['Name (Full - LNF)'].str.title()
well_demographics_rpt['Name (Full - LNF)'] = well_demographics_rpt['Name (Full - LNF)'].apply(lambda x:re.sub(' ,', ',', x))
filt = well_demographics_rpt.duplicated(subset=['Name (Full - LNF)', ], keep='last')
well_demographics_rpt.drop(well_demographics_rpt.loc[filt].index, inplace=True)

In [47]:
try:
    well_demographics_custom_fields_rpt = pd.read_excel(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\welligent_reports\well_demographics_rpt_2021.12.03.xlsx', index_col='Unique Client ID')
except FileNotFoundError:
    well_demographics_custom_fields_rpt = pd.read_excel(r'C:\Users\edwar\PH_data\data_files\welligent_reports\well_demographics_rpt_2021.12.03.xlsx', index_col='Unique Client ID')

well_demographics_custom_fields_rpt.head()

Date of Birth  Date of Death Discharge Date/Time  \
Unique Client ID                                                    
4767931             1980-01-21            NaN                 NaT   
4768322             1987-02-07            NaN                 NaT   
4763616             1991-12-10            NaN                 NaT   
4802895             1981-03-02            NaN                 NaT   
4803031             1981-02-14            NaN                 NaT   

                 Discharge Reason     Ethnicity First Name  Gender  \
Unique Client ID                                                     
4767931                       NaN      Hispanic     BRENDA  Female   
4768322                       NaN  Non-Hispanic      LAURA  Female   
4763616                       NaN  Non-Hispanic  DOMINIQUE  Female   
4802895                       NaN      Hispanic    WILMARY  Female   
4803031                       NaN  Non-Hispanic    BONNITA  Female   

                 Highest Educational Achievement Intake Date/Time  \
Unique Client ID                                                    
4767931                   No HSE/GED/High School       2019-10-15   
4768322                             Some College       2019-10-17   
4763616                   No HSE/GED/High School       2019-10-15   
4802895                   No HSE/GED/High School       2019-10-15   
4803031                             Some College       2019-10-17   

                 Intake Status  ... Location Race (Multiple) Arrested  Mhp  \
Unique Client ID                ...                                          
4767931                 Active  ...   412-11           White      NaN  Yes   
4768322                 Active  ...   412-11    Multi-Racial      NaN  Yes   
4763616                 Active  ...   412-11           Black      NaN  Yes   
4802895                 Active  ...   412-11           White      NaN   No   
4803031                 Active  ...   412-11           Black      NaN  Yes   

                 Medical Condition Mental Health Needs  Pcp  \
Unique Client ID                                              
4767931                        Yes                 Yes  Yes   
4768322                        Yes                 Yes  Yes   
4763616                        Yes                 Yes   No   
4802895                        Yes                 Yes  Yes   
4803031                        Yes                 Yes  Yes   

                 Returned To Shelter Substance Use Substance Use Provider   
Unique Client ID                                                            
4767931                          NaN            No                      No  
4768322                          NaN           Yes                      No  
4763616                          NaN           Yes                     Yes  
4802895                          NaN           Yes                     Yes  
4803031                          NaN            No                     NaN  

[5 rows x 21 columns]

In [48]:
well_demographics_custom_fields_rpt['Ethnicity'].replace('Non-Hispanic', 'Non Hispanic', inplace=True)

In [49]:
well_demographics_custom_fields_rpt['First Name'] = well_demographics_custom_fields_rpt['First Name'].str.strip()
well_demographics_custom_fields_rpt['Last Name'] = well_demographics_custom_fields_rpt['Last Name'].str.strip()
well_demographics_custom_fields_rpt['LastFirstName'] = ''
well_demographics_custom_fields_rpt['LastFirstName'] = well_demographics_custom_fields_rpt['Last Name'].str.title()+", "+well_demographics_custom_fields_rpt['First Name'].str.title()

In [50]:
filt = well_demographics_custom_fields_rpt.duplicated(subset=['LastFirstName'], keep='last')
well_demographics_custom_fields_rpt.drop(well_demographics_custom_fields_rpt.loc[filt].index, inplace=True)
well_demographics_custom_fields_rpt.head()

Date of Birth  Date of Death Discharge Date/Time  \
Unique Client ID                                                    
4767931             1980-01-21            NaN                 NaT   
4768322             1987-02-07            NaN                 NaT   
4763616             1991-12-10            NaN                 NaT   
4802895             1981-03-02            NaN                 NaT   
4803031             1981-02-14            NaN                 NaT   

                 Discharge Reason     Ethnicity First Name  Gender  \
Unique Client ID                                                     
4767931                       NaN      Hispanic     BRENDA  Female   
4768322                       NaN  Non Hispanic      LAURA  Female   
4763616                       NaN  Non Hispanic  DOMINIQUE  Female   
4802895                       NaN      Hispanic    WILMARY  Female   
4803031                       NaN  Non Hispanic    BONNITA  Female   

                 Highest Educational Achievement Intake Date/Time  \
Unique Client ID                                                    
4767931                   No HSE/GED/High School       2019-10-15   
4768322                             Some College       2019-10-17   
4763616                   No HSE/GED/High School       2019-10-15   
4802895                   No HSE/GED/High School       2019-10-15   
4803031                             Some College       2019-10-17   

                 Intake Status  ... Race (Multiple) Arrested  Mhp  \
Unique Client ID                ...                                 
4767931                 Active  ...           White      NaN  Yes   
4768322                 Active  ...    Multi-Racial      NaN  Yes   
4763616                 Active  ...           Black      NaN  Yes   
4802895                 Active  ...           White      NaN   No   
4803031                 Active  ...           Black      NaN  Yes   

                 Medical Condition Mental Health Needs  Pcp  \
Unique Client ID                                              
4767931                        Yes                 Yes  Yes   
4768322                        Yes                 Yes  Yes   
4763616                        Yes                 Yes   No   
4802895                        Yes                 Yes  Yes   
4803031                        Yes                 Yes  Yes   

                 Returned To Shelter Substance Use Substance Use Provider   \
Unique Client ID                                                             
4767931                          NaN            No                      No   
4768322                          NaN           Yes                      No   
4763616                          NaN           Yes                     Yes   
4802895                          NaN           Yes                     Yes   
4803031                          NaN            No                     NaN   

                           LastFirstName  
Unique Client ID                          
4767931                 Melendez, Brenda  
4768322                   Raymond, Laura  
4763616                Warren, Dominique  
4802895           Pagan Gordian, Wilmary  
4803031                  Junior, Bonnita  

[5 rows x 22 columns]

## Airtable reports

In [51]:
try:
    airtable_secondayRecords = pd.read_csv(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\Airtable\secondaryRecords-Grid view.csv')
except FileNotFoundError:
    airtable_secondayRecords = pd.read_csv(r'C:\Users\edwar\PH_data\data_files\Airtable\secondaryRecords-Grid view.csv')
    
airtable_secondayRecords.head()

secondaryID recordType   firstName  lastName        DOB  mainID  \
0           19      child  Emiyalisse    Lamboy  1/14/2009      60   
1           20      child       Evely  Gonzalez  7/16/2019      60   
2           21      child    Jarielle    Moyano  2/16/2014      60   
3           22      child     Jessica    Lamboy  2/26/2005      60   
4           23      child      Jordan    Lamboy  8/22/2006      60   

  fullName[calc] (from mainID) admitDate  ageAtIntake  ageForCalc  \
0               Yajaira Alqawi  4/1/2021        146.0       146.0   
1               Yajaira Alqawi  4/1/2021         20.0        20.0   
2               Yajaira Alqawi  4/1/2021         85.0        85.0   
3               Yajaira Alqawi  4/1/2021        193.0       193.0   
4               Yajaira Alqawi  4/1/2021        175.0       175.0   

   Attachments reportingPeriods(fromPrimary) program(fromPrimary)  
0          NaN                          fy21                  DHS  
1          NaN                          fy21                  DHS  
2          NaN                          fy21                  DHS  
3          NaN                          fy21                  DHS  
4          NaN                          fy21                  DHS

In [52]:
try:
    airtable_primaryRecords = pd.read_csv(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\Airtable\primaryRecords-mainView-allProg-allTime.csv')
except FileNotFoundError:
    airtable_primaryRecords = pd.read_csv(r'C:\Users\edwar\PH_data\data_files\Airtable\primaryRecords-mainView-allProg-allTime.csv')
    
airtable_primaryRecords.head()

mainID             Program        residence     lName      fullName[calc]  \
0       2  Supportive Housing  Bishop Sullivan   Whitman       Barry Whitman   
1       3  Supportive Housing  Bishop Sullivan  Williams     Debbie Williams   
2       1  Supportive Housing  Bishop Sullivan    Karras       Amelia Karras   
3     185                 DHS              PH7   Charles       Lacey Charles   
4     137  Supportive Housing       Mulholland  Harrison  Elizabeth Harrison   

          DOB  ageAtIntake  kidsInHome  otherAdultsInHome  totalAdultsInHome  \
0  12/13/1969         48.0           0                  0                  1   
1   11/8/1971         42.0           0                  0                  1   
2  11/16/1961         52.0           0                  0                  1   
3  11/16/1994         24.0           3                  0                  1   
4  10/24/1958         61.0           0                  0                  1   

   ...  medicalCondition      PCP   MHneeds MHprovider  CDhistory CDprovider  \
0  ...          no value  checked  no value    checked        yes        NaN   
1  ...               yes  checked  no value    checked   no value        NaN   
2  ...               yes  checked  no value    checked   no value        NaN   
3  ...               yes  checked  no value        NaN   no value        NaN   
4  ...               yes  checked  no value    checked        yes    checked   

  Housing Outcome (NEW) ReportingCategoryHousingExit    housingStatus(atExit)  \
0                   NaN                          NaN                      NaN   
1                   NaN                          NaN                      NaN   
2                   NaN                          NaN                      NaN   
3                   NaN         AWOL/Back to shelter  AWL/Voluntary discharge   
4                   NaN                          NaN                      NaN   

  reportingPeriods  
0             fy21  
1             fy21  
2             fy21  
3             fy21  
4             fy21  

[5 rows x 28 columns]

In [53]:
for index, row in airtable_primaryRecords.iterrows():
    if str(row['fullName[calc]']).lower().strip() == 'marilu\xa0 santos':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'Marilu Santos'
    elif str(row['fullName[calc]']).lower().strip() == 'jewel cordova':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'Jewell Cordova'
    elif str(row['fullName[calc]']).lower().strip() == 'ta’Sheena johnson':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'Tasheena Johnson'         
    elif str(row['fullName[calc]']).lower().strip() ==  'narci genoa':           
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'narci Genao'.title()
    elif str(row['fullName[calc]']).lower().strip() ==  'cindy ramikishun':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'cindy RAMKISHUN'.title()    
    elif str(row['fullName[calc]']).lower().strip() ==  'donna pickersgill':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'donna PICKERSGILL-BROWN'.title()    
    elif str(row['fullName[calc]']).lower().strip() ==  'garry isaac':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'GARY isaac'.title()    
    elif str(row['fullName[calc]']).lower().strip() ==  'georgina deanton':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'georgina DEATON'.title()    
    elif str(row['fullName[calc]']).lower().strip() ==  'irena zdrowska':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'irena ZDRODOWSKA'.title()    
    elif str(row['fullName[calc]']).lower().strip() ==   'roberto velazquez':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'roberto VELAZQUEZ-CABAN'.title()    
    elif str(row['fullName[calc]']).lower().strip() == 'tawanna horton':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'TAWANA horton'.title()    
    elif str(row['fullName[calc]']).lower().strip() ==  'toniesah jackson':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'TONIESHA jackson'.title()
    elif str(row['fullName[calc]']).lower().strip() ==  'wilmary pagan':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'wilmary PAGAN GORDIAN'.title()
    elif str(row['fullName[calc]']).lower().strip() ==  'jenna mallet':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'jenna MALLETT'.title()
    elif str(row['fullName[calc]']).lower().strip() ==  'khilah vaughan':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'khilah VAUGHN'.title()
    elif str(row['fullName[calc]']).lower().strip() ==  'rosalba solano':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'rosalbo solano'.title()
    elif str(row['fullName[calc]']).lower().strip() ==  'cheri la croix':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'cheri LACROIX'.title()
    elif str(row['fullName[calc]']).lower().strip() ==  'michaella doroneth':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'michaella DERONETH'.title()
    elif str(row['fullName[calc]']).lower().strip() ==  'maria zuniga miranda':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'maria ZUNIGA MIRANDA'.title()    
    elif str(row['fullName[calc]']).lower().strip() ==  'lucy medina amaya':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'lucy MEDINA AMAYA'.title()  
    elif str(row['fullName[calc]']).lower().strip() ==  'shakeym barquero':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'SHAKEYMA BIVINS BARQUERO'.title()     
    elif str(row['fullName[calc]']).lower().strip() ==  'eugenia joseph':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'eugenia JOSEPHS'.title()    
    elif str(row['fullName[calc]']).lower().strip() ==  'lennette edwards':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'LENNETT edwards'.title()      
    elif str(row['fullName[calc]']).lower().strip() ==  'jennifer saint vil':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'jennifer SAINTVIL'.title()        
    elif str(row['fullName[calc]']).lower().strip() ==  'adrianna overton':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'ADRIANA overton'.title()    
    elif str(row['fullName[calc]']).lower().strip() ==  'jocelyn white':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'JOCELYNN FINKLEA'.title()  
    elif str(row['fullName[calc]']).lower().strip() ==  'roland jackson':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'ROLANDA jackson'.title()
    elif str(row['fullName[calc]']).lower().strip() == 'jully harry-herrera':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'jully Harry Herrera'.title() 
    elif str(row['fullName[calc]']).lower().strip() == 'octavia elliot':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'octavia Elliott'.title()    
    elif str(row['fullName[calc]']).lower().strip() == 'wendy castilo':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'wendy Castillo'.title()    
    elif str(row['fullName[calc]']).lower().strip() == 'loudres montero':
        airtable_primaryRecords.loc[index, 'fullName[calc]'] = 'Lourdes montero'.title()  
    elif str(row["fullName[calc]"]).lower().strip() == 'mamasir rodriguez'.title():
        airtable_primaryRecords.loc[index, "fullName[calc]"] = 'Mamasir Maria Rodriquez' 

## Supportive tenants

In [54]:
try:
    supportiveHousingTenants = pd.read_excel(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\housing tenants\SUPPORTIVE HOUSING - COMMUNITY TENANT SPREADSHEET - NOVEMBER 2021.xlsx')
except FileNotFoundError:
    supportiveHousingTenants = pd.read_excel(r'C:\Users\edwar\PH_data\data_files\housing_tenants\SUPPORTIVE HOUSING - COMMUNITY TENANT SPREADSHEET - NOVEMBER 2021.xlsx')
    
supportiveHousingTenants.head()

C:\Users\dejesuse\Anaconda3\lib\site-packages\openpyxl\worksheet\_reader.py:312: UserWarning: Data Validation extension is not supported and will be removed
  warn(msg)


Residence First Name    Last Name        DOB Admission Date  Exit Date  \
0  DADDARIO   Patricia       Albert 1961-09-18     2013-03-23        NaT   
1  DADDARIO    Yolanda  Billingslea 1975-05-06     2015-08-21        NaT   
2  DADDARIO    Keianda        Henry 1993-11-30     2016-08-09 2018-12-09   
3  DADDARIO    Rosalie      Cutting 1945-03-26     2015-10-13 2021-10-01   
4  SULLIVAN       Lisa       Cepeda 1963-02-12     2014-11-22        NaT   

    Race     Ethnicity Housing Outcome (if discharged)  \
0  Black  Non-Hispanic                             NaN   
1  Black  Non-Hispanic                             NaN   
2  Black  Non-Hispanic           Involuntary Discharge   
3  White  Non-Hispanic             Independent Housing   
4  White  Non-Hispanic                             NaN   

                 Additional Information  
0                                   NaN  
1                                   NaN  
2                              Eviction  
3  Moved to purchased home in the south  
4                                   NaN

In [55]:
supportiveHousingTenants['Ethnicity'].replace('Non-Hispanic', 'Non Hispanic', inplace=True)

In [56]:
try:
    supportiveHousingTenantsRelatives = pd.read_excel(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\housing tenants\SUPPORTIVE HOUSING - COMMUNITY TENANT SPREADSHEET - NOVEMBER 2021.xlsx', sheet_name='others In Home')
except FileNotFoundError:
    supportiveHousingTenantsRelatives = pd.read_excel(r'C:\Users\edwar\PH_data\data_files\housing_tenants\SUPPORTIVE HOUSING - COMMUNITY TENANT SPREADSHEET - NOVEMBER 2021.xlsx', sheet_name='others In Home')
    
supportiveHousingTenantsRelatives.head()

Primary Resident's Name Child or Significant Other First Name Last Name  \
0          Evelyn Santana                      Child   Mai Ling      Cruz   
1          Evelyn Santana          Significant Other      Pablo      Cruz   
2           Erica Saldana                      Child    La'Miya   Johnson   
3           Erica Saldana                      Child     Nijha    Johnson   
4           Erica Saldana                      Child    Baheim     Martin   

         DOB   Detalis Exit Date  
0 2010-11-15  Daughter       NaT  
1 1977-07-14   Husband       NaT  
2 2005-06-10  Daughter       NaT  
3 2006-06-06  Daughter       NaT  
4 2011-09-20       Son       NaT

# Tables creation

## Adults

In [57]:
client_table_cols = ['Client Name',
 "Client's DOB",
 "Client's First Name",
 "Client's Last Name",
 'Education',
 'Ethnicity',
 'Race',
'MHP at intake',
'Medical Condition at intake',
'Mental Health Needs at intake',
'PCP at intake',
'Substance Use Provider at intake', 
'Substance Use at intake']

In [58]:
PH_Master_Client_list_2 = pd.DataFrame()

for df_name, df in sheets.items():
    for index, row in df.iterrows():
        PH_Master_Client_list_2 = PH_Master_Client_list_2.append({k:row[k] for k in df.columns}, ignore_index=True)
    

In [59]:
PH_Master_Client_list_2 = PH_Master_Client_list_2[PH_Master_Client_list_2.columns.intersection(client_table_cols)].copy()
PH_Master_Client_list_2 = PH_Master_Client_list_2.reindex(columns=client_table_cols)

In [60]:
PH_Master_Client_list_2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1390 entries, 0 to 1389
Data columns (total 13 columns):
 #   Column                            Non-Null Count  Dtype         
---  ------                            --------------  -----         
 0   Client Name                       1228 non-null   object        
 1   Client's DOB                      741 non-null    datetime64[ns]
 2   Client's First Name               1390 non-null   object        
 3   Client's Last Name                1390 non-null   object        
 4   Education                         732 non-null    object        
 5   Ethnicity                         739 non-null    object        
 6   Race                              737 non-null    object        
 7   MHP at intake                     633 non-null    object        
 8   Medical Condition at intake       726 non-null    object        
 9   Mental Health Needs at intake     716 non-null    object        
 10  PCP at intake                     725 non-null  

In [61]:
PH_Master_Client_list_2['AirtableIDs'] = ''
PH_Master_Client_list_2['Client Welligent ID'] = ''

In [62]:
for index, row in well_demographics_custom_fields_rpt.iterrows():
    if str(index) in list(map(str, PH_Master_Client_list_2['Client Welligent ID'])):
        continue
    elif (row['Intake Date/Time'] > pd.to_datetime('4/1/2021')):
        PH_Master_Client_list_2 = PH_Master_Client_list_2.append({'Client Name': row['First Name'].title()+" "+row['Last Name'].title(), "Client's DOB": row['Date of Birth'], "Client's First Name": row['First Name'].title(), "Client's Last Name": row['Last Name'].title(),'Education': row['Highest Educational Achievement'], 'Ethnicity': row['Ethnicity'], 'Race': row['Race (Multiple)'], 'MHP at intake': row['Mhp'],'Medical Condition at intake': row['Medical Condition'], 'Mental Health Needs at intake': row['Mental Health Needs'], 'PCP at intake': row['Pcp'], 'Substance Use Provider at intake': row[ 'Substance Use Provider '],  'Substance Use at intake': row['Substance Use'], 'ClientName_LastNameFirstName': row['Last Name'].title()+", "+row['First Name'].title(), 'Client Welligent ID': index}, ignore_index=True)

In [63]:
for index, row in supportiveHousingTenants.iterrows():
    PH_Master_Client_list_2 = PH_Master_Client_list_2.append({'Client Name': f"{row['First Name'].strip().title()} {row['Last Name'].strip().title()}","Client's DOB": row['DOB'], "Client's First Name": row['First Name'].strip().title(), "Client's Last Name": row['Last Name'].strip().title(),'Ethnicity': row['Ethnicity'], 'Race': row['Race'] }, ignore_index=True)

In [64]:
PH_Master_Client_list_2.replace({'nan': np.nan, 'Nat': np.nan, 'Nan': np.nan}, inplace=True)

In [65]:
PH_Master_Client_list_2.dropna(how='all', inplace=True)

In [66]:
PH_Master_Client_list_2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1442 entries, 0 to 1441
Data columns (total 16 columns):
 #   Column                            Non-Null Count  Dtype         
---  ------                            --------------  -----         
 0   Client Name                       1280 non-null   object        
 1   Client's DOB                      793 non-null    datetime64[ns]
 2   Client's First Name               863 non-null    object        
 3   Client's Last Name                806 non-null    object        
 4   Education                         750 non-null    object        
 5   Ethnicity                         788 non-null    object        
 6   Race                              787 non-null    object        
 7   MHP at intake                     650 non-null    object        
 8   Medical Condition at intake       747 non-null    object        
 9   Mental Health Needs at intake     736 non-null    object        
 10  PCP at intake                     743 non-null  

In [67]:
filt = pd.isna(PH_Master_Client_list_2["Client's First Name"]) & pd.isna(PH_Master_Client_list_2["Client's Last Name"])
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [68]:
filt = pd.isna(PH_Master_Client_list_2["Client's First Name"]) & pd.isna(PH_Master_Client_list_2["Client's Last Name"])
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [69]:
filt = PH_Master_Client_list_2.duplicated()
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [70]:
filt = pd.isna(PH_Master_Client_list_2["Client's Last Name"])
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [71]:
PH_Master_Client_list_2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 419 entries, 0 to 1441
Data columns (total 16 columns):
 #   Column                            Non-Null Count  Dtype         
---  ------                            --------------  -----         
 0   Client Name                       419 non-null    object        
 1   Client's DOB                      411 non-null    datetime64[ns]
 2   Client's First Name               419 non-null    object        
 3   Client's Last Name                419 non-null    object        
 4   Education                         368 non-null    object        
 5   Ethnicity                         406 non-null    object        
 6   Race                              406 non-null    object        
 7   MHP at intake                     304 non-null    object        
 8   Medical Condition at intake       362 non-null    object        
 9   Mental Health Needs at intake     352 non-null    object        
 10  PCP at intake                     358 non-null   

In [72]:

PH_Master_Client_list_2["Client Name"] = PH_Master_Client_list_2["Client's First Name"]+" "+PH_Master_Client_list_2["Client's Last Name"]

In [73]:
PH_Master_Client_list_2["ClientName_LastNameFirstName"] = PH_Master_Client_list_2["Client's Last Name"]+", "+PH_Master_Client_list_2["Client's First Name"]

In [74]:
filt = PH_Master_Client_list_2.duplicated(subset=['Client Name', "Client's DOB"], keep=False) & PH_Master_Client_list_2.loc[:,"Education": "Substance Use at intake"].isna().apply(lambda x: all(x), axis=1)
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [75]:
filt = PH_Master_Client_list_2.duplicated(subset=['Client Name'], keep=False) & pd.isna(PH_Master_Client_list_2["Client's DOB"])
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [76]:
filt = PH_Master_Client_list_2.loc[:,"Client Name":"Race"].duplicated( keep=False) & PH_Master_Client_list_2.loc[:,"MHP at intake": "Substance Use at intake"].isna().apply(lambda x: all(x), axis=1)
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [77]:
filt = (PH_Master_Client_list_2['Client Name'] == 'Anissa Delaney') & (PH_Master_Client_list_2.Education == 'GED/HSE/HSD')
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [78]:
filt = (PH_Master_Client_list_2['Client Name'] == 'Jackelyne Fernandez') & (PH_Master_Client_list_2.Education == 'GED/HSE/HSD')
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [79]:
filt = (PH_Master_Client_list_2['Client Name'] == 'Jennifer Garcia') & (PH_Master_Client_list_2.Education == 'GED/HSE/HSD')
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [80]:
filt = (PH_Master_Client_list_2['Client Name'] == 'Jessica Cabral') & (PH_Master_Client_list_2.Race == 'White')
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [81]:
filt = (PH_Master_Client_list_2['Client Name'] == 'Jolia Jacques') & (PH_Master_Client_list_2.Education == 'GED/HSE/HSD')
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [82]:
filt = (PH_Master_Client_list_2['Client Name'] == 'Jully Harry-Herrera') & (PH_Master_Client_list_2.Education == 'GED/HSE/HSD')
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [83]:
filt = (PH_Master_Client_list_2['Client Name'] == 'Kimberly Raker') & (PH_Master_Client_list_2.Ethnicity == 'Non Hispanic')
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [84]:
filt = (PH_Master_Client_list_2['Client Name'] == 'Rebecca Mosely') & (PH_Master_Client_list_2.Education == 'Some College')
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [85]:
filt = (PH_Master_Client_list_2['Client Name'] == 'Takiera Hester') & (PH_Master_Client_list_2.Race == 'White')
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [86]:
filt = (PH_Master_Client_list_2['Client Name'] == 'Tiffany Rogers') & (PH_Master_Client_list_2.Ethnicity == 'Hispanic')
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [87]:
PH_Master_Client_list_2.duplicated().sum()

1

In [88]:
filt = PH_Master_Client_list_2.duplicated(subset=['Client Name', "Client's DOB"], keep=False) & PH_Master_Client_list_2.loc[:,'MHP at intake': 'Substance Use at intake'].isna().apply(lambda x: all(x), axis=1)
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [89]:
filt = PH_Master_Client_list_2.duplicated(subset=['Client Name', "Client's DOB"], keep=False) & PH_Master_Client_list_2.loc[:,"Education":"Race" ].isna().apply(lambda x: any(x), axis=1)
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [90]:
filt = PH_Master_Client_list_2.duplicated(subset=['Client Name', "Client's DOB"], keep='last')
PH_Master_Client_list_2.drop(PH_Master_Client_list_2.loc[filt].index, inplace=True)

In [91]:
filt = PH_Master_Client_list_2.duplicated(subset=['Client Name'], keep=False)
PH_Master_Client_list_2.loc[filt].sort_values(by='Client Name')

Empty DataFrame
Columns: [Client Name, Client's DOB, Client's First Name, Client's Last Name, Education, Ethnicity, Race, MHP at intake, Medical Condition at intake, Mental Health Needs at intake, PCP at intake, Substance Use Provider at intake, Substance Use at intake, AirtableIDs, Client Welligent ID, ClientName_LastNameFirstName]
Index: []

In [92]:
PH_Master_Client_list_2.columns

Index(['Client Name', 'Client's DOB', 'Client's First Name',
       'Client's Last Name', 'Education', 'Ethnicity', 'Race', 'MHP at intake',
       'Medical Condition at intake', 'Mental Health Needs at intake',
       'PCP at intake', 'Substance Use Provider at intake',
       'Substance Use at intake', 'AirtableIDs', 'Client Welligent ID',
       'ClientName_LastNameFirstName'],
      dtype='object')

In [93]:
client_master_duplicates = []
well_demo_duplicates = []
client_names_not_on_Well = []

for index, row in PH_Master_Client_list_2.iterrows():
    if list(PH_Master_Client_list_2['ClientName_LastNameFirstName']).count(row['ClientName_LastNameFirstName']) > 1:
        client_master_duplicates.append(row['ClientName_LastNameFirstName'])
        
for index, row in PH_Master_Client_list_2.iterrows():      
    if list(well_demographics_rpt['Name (Full - LNF)']).count(row['ClientName_LastNameFirstName']) > 1:
        well_demo_duplicates.append(row['ClientName_LastNameFirstName'])
        
for index, row in PH_Master_Client_list_2.iterrows():
    if (row['ClientName_LastNameFirstName'] not in client_master_duplicates) and (row['ClientName_LastNameFirstName'] not in well_demo_duplicates):
        filt = well_demographics_rpt['Name (Full - LNF)'].str.lower().str.strip() == row['ClientName_LastNameFirstName'].lower().strip()
        value = well_demographics_rpt.loc[filt].index.values
        if value.size > 0:
            PH_Master_Client_list_2.loc[index, 'Client Welligent ID'] = value[0]
        else:
            client_names_not_on_Well.append(row['ClientName_LastNameFirstName'])
            PH_Master_Client_list_2.loc[index, 'Client Welligent ID'] = np.nan
        
print("names duplicated on master list:", set(client_master_duplicates), sep='\n')
print("names duplicated on Welligent:", set(well_demo_duplicates), sep='\n')
print("names not on Welligent:", set(client_names_not_on_Well), sep='\n')

names duplicated on master list:
set()
names duplicated on Welligent:
set()
names not on Welligent:
{'Branes, Dontashia', 'Reape, Ninlil-Iyliyya', 'Johnson, Tinesha', 'Santos, Trashella', 'Sadler, Shelby', 'Vitale, Rebecca', 'Taylor, Jennifer', 'Glover, Mariah', 'Cattenhead, Saytra', 'Mosely, Rebecca', 'Tirado, Gregoria', 'Quinsey, Arilyn', 'Haskins, Marquis', 'Santos, Marilu', 'Witherspoon, Joneisha', 'Ramos, Samantha', 'Stone, Keshauna', 'Ramnarin, Salashwar', 'Speed, Ashley', 'Labrun, Marie', 'Parron, Chevon', 'Wells, Kiana', 'Diaz, Rachel', 'Rodriquez, Mamasir Maria', 'White, Breanna', 'Noreen, Ansa', 'Anderson, Novita', 'Martinez, Isis', 'James, Yeimy', 'Peri Ovado, Dayra', 'Isbell, Uriah', 'Dreamer, Omi', 'Cruz, Gabriela', 'Cisse, Fanta', 'Wyatt, Olivia', 'Mclaughlin, Theodora', 'Durant, Malquisha', 'Logrande, Lauren', 'Powell, Tayah', 'Mohamed Abde, Fatma', 'Crisostomo, Elvia', 'Washington, Lula', 'Davis, Shianne', 'Cedono, Thalia', 'Gwee, Joseph', 'Kumah, Alanena', 'Coke, Charm

In [94]:
close_matches_names = {}
for name in client_names_not_on_Well:
    cutoff = 0.61
    if len(difflib.get_close_matches(name, list(well_demographics_rpt['Name (Full - LNF)']), cutoff=cutoff)) == 0:
        continue
    else:
        close_matches = difflib.get_close_matches(name, list(well_demographics_rpt['Name (Full - LNF)']), cutoff=cutoff)
        close_matches_names[name] = close_matches
        
print(len(close_matches_names))
close_matches_names

52


{'Barnes, Annie': ['Barnes, Desiree', 'Brame, Anaiya', 'Bines, Louise'],
 'Branes, Dontashia': ['Breedy, Montashia', 'Brame, Anaiya', 'Moore, Antasia'],
 'Fitzgerald, Latoya': ['Walker, Latoya'],
 'Washington, Lula': ['Washington, Paris',
  'Washington, Janeen',
  'Washington, Shanika'],
 'Rodriquez, Mamasir Maria': ['Rodriquez, Mamasir',
  'Rodriguez, Luvasia',
  'Rodriguez, Leticia'],
 'Mclaughlin, Theodora': ['Mclaughlin, Terrence'],
 'Justice, Melissa': ['Jimenez, Melissa'],
 'Davis, Shianne': ['Davis, Danielle', 'Diggs, Stephanie', 'Davis, Virginia'],
 'Rogers, Jamila': ['Rogers, Tiffany', 'Mccoy, Jamilah', 'Jones, Jasmine'],
 'Brown, Kimera': ['Brown, Keyreice', 'Brown, Tyesha', 'Barton, Amber'],
 'Cedono, Thalia': ['Felder, Shalima'],
 'Wells, Kiana': ['Yarrell, Kia', 'Williams, Atiffanya', 'Wilson, Kayla'],
 'Pery, Tamika': ['Frazier, Tika', 'Berry, Tyanna', 'Wright, Tanika'],
 'Santos, Trashella': ['Batts, Tahera', 'Carrington, Tracena'],
 'Mosely, Rebecca': ['Mosley, Rebecca'

In [95]:
PH_Master_Client_list_2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 376 entries, 3 to 1441
Data columns (total 16 columns):
 #   Column                            Non-Null Count  Dtype         
---  ------                            --------------  -----         
 0   Client Name                       376 non-null    object        
 1   Client's DOB                      370 non-null    datetime64[ns]
 2   Client's First Name               376 non-null    object        
 3   Client's Last Name                376 non-null    object        
 4   Education                         339 non-null    object        
 5   Ethnicity                         370 non-null    object        
 6   Race                              370 non-null    object        
 7   MHP at intake                     282 non-null    object        
 8   Medical Condition at intake       332 non-null    object        
 9   Mental Health Needs at intake     323 non-null    object        
 10  PCP at intake                     330 non-null   

In [96]:
for index, row in PH_Master_Client_list_2.iterrows():
    attr = 'Race'
    if pd.isna(row[attr]):
        filt = well_demographics_rpt.index == row['Client Welligent ID']
        value = well_demographics_rpt.loc[filt,attr].values
        if value.size > 0:
            PH_Master_Client_list_2.loc[index, attr] = value[0]
#         if value.size > 0:
#             PH_Master_Client_list_2.loc[index, attr] = value[0]

In [97]:
airtable_duplicates = []
client_names_not_on_airtable = []

for index, row in PH_Master_Client_list_2.iterrows():      
    if list(airtable_primaryRecords['fullName[calc]']).count(row['Client Name']) > 1:
        airtable_duplicates.append(row['ClientName_LastNameFirstName'])
        
for index, row in PH_Master_Client_list_2.iterrows():
    if (row['ClientName_LastNameFirstName'] not in airtable_duplicates):
        filt = airtable_primaryRecords['fullName[calc]'].str.lower().str.strip() == row['Client Name'].lower().strip()
        value = airtable_primaryRecords.loc[filt, 'mainID'].values
        if value.size > 0:
            PH_Master_Client_list_2.loc[index, 'AirtableIDs'] = value[0]
        else:
            client_names_not_on_airtable.append(row['ClientName_LastNameFirstName'])
            PH_Master_Client_list_2.loc[index, 'AirtableIDs'] = np.nan
        
print("names duplicated on Airtable:", set(airtable_duplicates), sep='\n')
print("names not on Airtable:", set(client_names_not_on_airtable), sep='\n')

names duplicated on Airtable:
{'Deroneth, Michaella', 'Cabral, Jessica', 'Jacques, Jolia', 'Portelli, Rosa', 'Rizzo, Gabriella'}
names not on Airtable:
{'James, Tonya', 'Hunte, Pauline', 'Vasquez, Tais', 'Green, Latifa', 'Cattenhead, Saytra', 'Tavarez, Jisset', 'Cardona Bayon, Kaina', 'Fluker, Sherial', "Jones, T'Nia", 'Whetts, Tyana', 'Cutting, Rosalie', 'Robinson, Shawanda', 'Rodriquez, Mamasir Maria', 'Faria, Leah', 'Kidd, Shanna', 'Mcadoo, Katrina', 'Williams, Larissa', 'Small, Tyje', 'Washington, Shanika', 'Owens, Alexandria', 'Liverpool, Sharon', 'Williams, Sharanda', 'Kimble, Erica', 'Henry, Keianda', 'Arroyo, Raymond', 'Hugee, Shanel', 'Cepeda, Lisa', 'Walker, Delores', 'Ramos, Betsy', 'Frazier, Tika', 'Hernandez, Jamie', 'Edgardo, Isaac', 'Saldana, Erica', 'Thompson, Stacey', 'Martinez, Tahasia', 'Willingham, Tanisha', 'Billingslea, Yolanda', 'Santana, Evelyn', 'Nicholson, Antone', 'Matisi, Alissa', 'Hernandez, Maria', 'James, Charla', 'Jefferies, Kechia', 'Herrera-Gonzalez, H

In [98]:
for index, row in PH_Master_Client_list_2.iterrows():
    attr = 'DOB'
    if pd.isna(row["Client's DOB"]):
        filt = airtable_primaryRecords['mainID'] == row['AirtableIDs']
        value = airtable_primaryRecords.loc[filt,attr].values
        if value.size > 0:
            print(value)
#             PH_Master_Client_list_2.loc[index, attr] = value[0]

[nan]
[nan]
[nan]
[nan]
[nan]


## Employment

In [99]:
emp_cols = """Client Name	Eligible to Work	Employment_StartDate	Employer Name	Position	Employment Status	Starting Salary (per hour)	Current/Ending Salary (per hour)	Employment_EndDate	Employment End Reason	Off-The-Books	Notes:""".split('\t')


In [100]:
PH_employment_master_df_2 = pd.DataFrame()

for df_name,  df in employment_sheets.items():
    for index, row in df.iterrows():
        PH_employment_master_df_2 = PH_employment_master_df_2.append({k:row[k] for k in df.columns}, ignore_index=True)

In [101]:
PH_employment_master_df_2 = PH_employment_master_df_2[PH_employment_master_df_2.columns.intersection(emp_cols)].copy()

In [102]:
PH_employment_master_df_2 = PH_employment_master_df_2.reindex(columns=emp_cols)
PH_employment_master_df_2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 860 entries, 0 to 859
Data columns (total 12 columns):
 #   Column                            Non-Null Count  Dtype  
---  ------                            --------------  -----  
 0   Client Name                       827 non-null    object 
 1   Eligible to Work                  833 non-null    object 
 2   Employment_StartDate              290 non-null    object 
 3   Employer Name                     297 non-null    object 
 4   Position                          283 non-null    object 
 5   Employment Status                 293 non-null    object 
 6   Starting Salary (per hour)        279 non-null    float64
 7   Current/Ending Salary (per hour)  255 non-null    float64
 8   Employment_EndDate                172 non-null    object 
 9   Employment End Reason             172 non-null    object 
 10  Off-The-Books                     200 non-null    object 
 11  Notes:                            94 non-null     object 
dtypes: float

In [103]:
filt = PH_employment_master_df_2.duplicated()
PH_employment_master_df_2.drop(PH_employment_master_df_2.loc[filt].index, inplace=True)
PH_employment_master_df_2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 342 entries, 0 to 854
Data columns (total 12 columns):
 #   Column                            Non-Null Count  Dtype  
---  ------                            --------------  -----  
 0   Client Name                       338 non-null    object 
 1   Eligible to Work                  333 non-null    object 
 2   Employment_StartDate              115 non-null    object 
 3   Employer Name                     120 non-null    object 
 4   Position                          112 non-null    object 
 5   Employment Status                 117 non-null    object 
 6   Starting Salary (per hour)        110 non-null    float64
 7   Current/Ending Salary (per hour)  98 non-null     float64
 8   Employment_EndDate                54 non-null     object 
 9   Employment End Reason             55 non-null     object 
 10  Off-The-Books                     69 non-null     object 
 11  Notes:                            52 non-null     object 
dtypes: float

In [104]:
PH_employment_master_df_2['Employment_StartDate'].replace(np.nan, pd.NaT, inplace=True)
PH_employment_master_df_2['Employment_EndDate'].replace(np.nan, pd.NaT, inplace=True)
PH_employment_master_df_2['Eligible to Work'] = PH_employment_master_df_2['Eligible to Work'].str.title().str.strip()
PH_employment_master_df_2['Off-The-Books'] = PH_employment_master_df_2['Off-The-Books'].str.title().str.strip()

In [105]:
for col in PH_employment_master_df_2.columns:
    if 'date' in col.lower():
        PH_employment_master_df_2[col] = pd.to_datetime(PH_employment_master_df_2[col], errors='coerce')

In [106]:
filt = PH_employment_master_df_2['Client Name'].isna()
PH_employment_master_df_2.drop(PH_employment_master_df_2.loc[filt].index, inplace=True)

In [107]:
filt = PH_employment_master_df_2.duplicated(subset=['Client Name', 'Employment_StartDate'], keep='last')
PH_employment_master_df_2.drop(PH_employment_master_df_2.loc[filt].index, inplace=True)

In [108]:
pd.set_option('display.max_rows', None)
filt = PH_employment_master_df_2.duplicated(subset=['Client Name', 'Eligible to Work'],keep=False)
dup_clients_df = PH_employment_master_df_2.loc[filt].sort_values(by='Client Name')
dup_clients_df

Client Name Eligible to Work Employment_StartDate  \
8            Allana Brissett              Yes           2019-06-01   
331          Allana Brissett              Yes                  NaT   
14             Ashley Mazyck              Yes           2018-10-01   
15             Ashley Mazyck              Yes           2020-03-01   
37             Barry Whitman              Yes           2020-09-14   
36             Barry Whitman              Yes           2018-02-01   
139            Charmika King              Yes                  NaT   
547            Charmika King              Yes           2021-04-20   
12          Danielle Johnson              Yes           2019-11-04   
13          Danielle Johnson              Yes           2020-02-10   
48            Deira Figueroa               No           2018-06-02   
47            Deira Figueroa               No           2018-01-10   
214           Deira Figueroa               No           2020-10-10   
215           Deira Figueroa               No           2021-01-25   
754           Deira Figueroa               No           2021-05-17   
213           Deira Figueroa               No           2019-03-15   
405          Desiree Roberts              Yes           2020-06-01   
164          Desiree Roberts              Yes                  NaT   
51          Dominique Warren              Yes                  NaT   
216         Dominique Warren              Yes           2020-08-24   
52               Donald Hart              Yes           2018-10-18   
53               Donald Hart              Yes           2019-01-18   
54   Donna Pickersgill-Brown              Yes           2011-07-05   
55   Donna Pickersgill-Brown              Yes           2018-10-29   
3            Fatasia Petties              Yes           2019-09-01   
2            Fatasia Petties              Yes           2020-06-06   
58                Gary Isaac               No           2017-09-15   
59                Gary Isaac               No           2016-02-04   
60                Gary Isaac               No           2018-03-06   
0        Jackelyne Fernandez              Yes           2017-09-01   
1        Jackelyne Fernandez              Yes           2020-09-16   
233             Kadian Whyte               No           2020-10-17   
67              Kadian Whyte               No           2018-10-02   
78       Latoya Herndon-Ford              Yes                  NaT   
77       Latoya Herndon-Ford              Yes           2019-10-01   
76       Latoya Herndon-Ford              Yes           2019-01-22   
71       Latoya Herndon-Ford              Yes           2017-05-20   
72       Latoya Herndon-Ford              Yes           2016-10-30   
73       Latoya Herndon-Ford              Yes           2017-06-21   
75       Latoya Herndon-Ford              Yes           2018-11-19   
74       Latoya Herndon-Ford              Yes           2018-09-10   
174           Lawanda Stroud              Yes           2017-11-01   
173           Lawanda Stroud              Yes                  NaT   
16         Leticia Navarrete              Yes           2020-05-30   
17         Leticia Navarrete              Yes           2019-10-01   
9               Louise Bines              Yes           2019-11-01   
10              Louise Bines              Yes           2017-12-01   
833             Natori Baker              Yes           2021-05-25   
150             Natori Baker              Yes                  NaT   
147            Nicole Hudson              Yes                  NaT   
551            Nicole Hudson              Yes           2021-02-17   
606           Rashima Wilson              Yes           2021-05-25   
365           Rashima Wilson              Yes           2018-04-01   
5             Rebecca Mosely              Yes           2020-05-15   
6             Rebecca Mosely              Yes           2019-07-15   
96             Robert Frager              Yes           2020-01-27   
95             Robert Frage

In [109]:
dup_clients_dic = {}
for index, row in dup_clients_df.iterrows():
    if row['Client Name'] in dup_clients_dic.keys():
        dup_clients_dic[row['Client Name']].append(index)
    else:
        dup_clients_dic[row['Client Name']] = [index]

In [110]:
for k, v in dup_clients_dic.items():
    for i, ind in enumerate(v):
        if pd.isna(dup_clients_df.loc[ind, 'Employment_StartDate': 'Notes:']).all():
            if not pd.isna(dup_clients_df.loc[v[1], 'Employment_EndDate']) or not pd.isna(dup_clients_df.loc[v[-1], 'Employment_EndDate']):
                continue
            else:
                PH_employment_master_df_2.drop(ind, inplace=True)
        

In [111]:
pd.set_option('display.max_rows', None)
filt = PH_employment_master_df_2.duplicated(subset=['Client Name'],keep=False) & pd.isna(PH_employment_master_df_2['Eligible to Work'])
PH_employment_master_df_2.drop(PH_employment_master_df_2.loc[filt].index, inplace=True)

In [269]:
filt = PH_employment_master_df_2['Client Name'] == 'Tinesha Johnson'
PH_employment_master_df_2.loc[filt, 'Eligible to Work'] = 'Yes'

In [112]:
pd.set_option('display.max_rows', None)
filt = PH_employment_master_df_2.duplicated(subset=['Client Name'],keep=False)
PH_employment_master_df_2.loc[filt].sort_values(by='Client Name')

Client Name Eligible to Work Employment_StartDate  \
14             Ashley Mazyck              Yes           2018-10-01   
15             Ashley Mazyck              Yes           2020-03-01   
37             Barry Whitman              Yes           2020-09-14   
36             Barry Whitman              Yes           2018-02-01   
13          Danielle Johnson              Yes           2020-02-10   
12          Danielle Johnson              Yes           2019-11-04   
48            Deira Figueroa               No           2018-06-02   
47            Deira Figueroa               No           2018-01-10   
754           Deira Figueroa               No           2021-05-17   
213           Deira Figueroa               No           2019-03-15   
214           Deira Figueroa               No           2020-10-10   
215           Deira Figueroa               No           2021-01-25   
216         Dominique Warren              Yes           2020-08-24   
51          Dominique Warren              Yes                  NaT   
52               Donald Hart              Yes           2018-10-18   
53               Donald Hart              Yes           2019-01-18   
55   Donna Pickersgill-Brown              Yes           2018-10-29   
54   Donna Pickersgill-Brown              Yes           2011-07-05   
3            Fatasia Petties              Yes           2019-09-01   
2            Fatasia Petties              Yes           2020-06-06   
58                Gary Isaac               No           2017-09-15   
59                Gary Isaac               No           2016-02-04   
60                Gary Isaac               No           2018-03-06   
0        Jackelyne Fernandez              Yes           2017-09-01   
1        Jackelyne Fernandez              Yes           2020-09-16   
352      Jully Harry Herrera               No                  NaT   
21       Jully Harry Herrera              Yes           2020-08-12   
233             Kadian Whyte               No           2020-10-17   
67              Kadian Whyte               No           2018-10-02   
71       Latoya Herndon-Ford              Yes           2017-05-20   
72       Latoya Herndon-Ford              Yes           2016-10-30   
73       Latoya Herndon-Ford              Yes           2017-06-21   
74       Latoya Herndon-Ford              Yes           2018-09-10   
75       Latoya Herndon-Ford              Yes           2018-11-19   
76       Latoya Herndon-Ford              Yes           2019-01-22   
77       Latoya Herndon-Ford              Yes           2019-10-01   
78       Latoya Herndon-Ford              Yes                  NaT   
17         Leticia Navarrete              Yes           2019-10-01   
16         Leticia Navarrete              Yes           2020-05-30   
9               Louise Bines              Yes           2019-11-01   
10              Louise Bines              Yes           2017-12-01   
606           Rashima Wilson              Yes           2021-05-25   
365           Rashima Wilson              Yes           2018-04-01   
6             Rebecca Mosely              Yes           2019-07-15   
5             Rebecca Mosely              Yes           2020-05-15   
261            Robert Frager              Yes           2020-04-06   
95             Robert Frager              Yes           2019-10-23   
96             Robert Frager              Yes           2020-01-27   
100             Shakeia Dean              Yes           2017-01-16   
101             Shakeia Dean              Yes           2018-11-01   
266             Shakeia Dean              Yes           2019-03-25   
109            Tawana Horton              Yes           2018-07-08   
110            Tawana Horton              Yes           2019-07-14   

                    Employer Name                        Position  \
14                 Elina Williams                      Babysitter   
15                 Deandra Saleis                      Babysitter   
37        Gunder Home Renovat

## Programs

In [113]:
PH_clients_pograms_2 = pd.DataFrame()

for df_name, df in sheets.items():
    for index, row in df.iterrows():
        PH_clients_pograms_2 = PH_clients_pograms_2.append({k:row[k] for k in df.columns}, ignore_index=True)
        PH_clients_pograms_2.loc[PH_clients_pograms_2.tail(1).index.item(), 'program'] = df_name[7:]

In [114]:
cols = ["Client's First Name", "Client's Last Name", 'Client Name','welligent_id', 'airtable_id','Admission Date',  'Program End Date','Housing Status (at exit)', 'program', 'Location', 'client_type']

In [115]:
PH_clients_pograms_2 = PH_clients_pograms_2[PH_clients_pograms_2.columns.intersection(cols)].copy()

In [116]:
PH_clients_pograms_2 = PH_clients_pograms_2.reindex(columns=cols)

In [117]:
PH_clients_pograms_2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1390 entries, 0 to 1389
Data columns (total 11 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   Client's First Name       1390 non-null   object        
 1   Client's Last Name        1390 non-null   object        
 2   Client Name               1228 non-null   object        
 3   welligent_id              0 non-null      float64       
 4   airtable_id               0 non-null      float64       
 5   Admission Date            754 non-null    datetime64[ns]
 6   Program End Date          308 non-null    object        
 7   Housing Status (at exit)  301 non-null    object        
 8   program                   1390 non-null   object        
 9   Location                  767 non-null    object        
 10  client_type               0 non-null      float64       
dtypes: datetime64[ns](1), float64(3), object(7)
memory usage: 119.6+ KB


In [118]:
for index, row in supportiveHousingTenants.iterrows():
    program='supportive'
    client_type = 'tenant'
    PH_clients_pograms_2 = PH_clients_pograms_2.append({"Client's First Name":row['First Name'].strip().title(), "Client's Last Name":row['Last Name'].strip().title(), 'Client Name': f"{row['First Name'].strip().title()} {row['Last Name'].strip().title()}", 'Admission Date': row['Admission Date'], 'Program End Date': row['Exit Date'],'Housing Status (at exit)': row['Housing Outcome (if discharged)'], 'program': program, 'Location': row['Residence'], 'client_type': client_type },ignore_index=True)

In [119]:
PH_clients_pograms_2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1414 entries, 0 to 1413
Data columns (total 11 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   Client's First Name       1414 non-null   object        
 1   Client's Last Name        1414 non-null   object        
 2   Client Name               1252 non-null   object        
 3   welligent_id              0 non-null      float64       
 4   airtable_id               0 non-null      float64       
 5   Admission Date            778 non-null    datetime64[ns]
 6   Program End Date          315 non-null    object        
 7   Housing Status (at exit)  308 non-null    object        
 8   program                   1414 non-null   object        
 9   Location                  791 non-null    object        
 10  client_type               24 non-null     object        
dtypes: datetime64[ns](1), float64(2), object(8)
memory usage: 121.6+ KB


In [120]:
filt = PH_clients_pograms_2.duplicated()
PH_clients_pograms_2.drop(PH_clients_pograms_2.loc[filt].index, inplace=True)

In [121]:
for index, row in PH_clients_pograms_2.iterrows():
    filt = PH_Master_Client_list_2['Client Name'] == row['Client Name']
    welligent_id = PH_Master_Client_list_2.loc[filt, 'Client Welligent ID'].values
    airtable_id = PH_Master_Client_list_2.loc[filt, 'AirtableIDs'].values
    if (welligent_id.size > 0) or (airtable_id.size > 0):
        PH_clients_pograms_2.loc[index, 'welligent_id'] = welligent_id[0]
        PH_clients_pograms_2.loc[index, 'airtable_id'] = airtable_id[0]
    elif (welligent_id.size > 1) or (airtable_id.size > 1):
        PH_clients_pograms_2.loc[index, 'welligent_id'] = welligent_id[1]
        PH_clients_pograms_2.loc[index, 'airtable_id'] = airtable_id[1]

In [122]:
for index, row in well_demographics_custom_fields_rpt.iterrows():
    if str(index) in list(map(str, PH_clients_pograms_2['welligent_id'])):
        continue
    elif (row['Intake Date/Time'] > pd.to_datetime('4/1/2021')):
        PH_clients_pograms_2 = PH_clients_pograms_2.append({"Client's First Name": row['First Name'].title().strip(), "Client's Last Name": row['Last Name'].title().strip(), 'Client Name': row['First Name'].title().strip()+" "+row['Last Name'].title().strip(),'welligent_id': index, 'Admission Date': row['Intake Date/Time'], 'Program End Date': row['Discharge Date/Time'],'Housing Status (at exit)': row['Discharge Reason'], 'Location': row['Location'], }, ignore_index=True)

In [123]:
programs_locs_dic = {'DHS': ['Glenmore ', 'PH2/7', 'PH3', 'PH7'],
 'DSS': ['PH4'],
 'WJP': ['PH2', 'PH5'],
 'supportive': ['Bishop Sullivan', "D'Addario", 'McKinney', 'Mulholland']}

In [124]:
for index, row in PH_clients_pograms_2.iterrows():
    if re.match('\d{3}-\d+', str(row['Location'])):
        filt = well_demographics_rpt['Name (Full - LNF)'] == row["Client's Last Name"]+", "+row["Client's First Name"]
        value = well_demographics_rpt.loc[filt, 'Location'].values
        if value.size < 1:
            continue
        else:
            PH_clients_pograms_2.loc[index, 'Location'] = value[0]
            for k, v in programs_locs_dic.items():
                for loc in v:
                    if value[0].split()[0].lower() in str(loc).lower():
                        PH_clients_pograms_2.loc[index, 'program'] = k
                    elif str(k).lower() in value[0].lower():
                        PH_clients_pograms_2.loc[index, 'program'] = k
                
#                 print(value[0].split()[0])
#                 PH_clients_pograms_2.loc[index, 'program'] = k
#             elif value[0].split()[0].lower() not in map(str.lower, v):
#                 print(value[0].split()[0].lower())
        

In [125]:
PH_clients_pograms_2.replace('Nan', np.nan, inplace=True)

In [126]:
filt = PH_clients_pograms_2.duplicated()
PH_clients_pograms_2.drop(PH_clients_pograms_2.loc[filt].index, inplace=True)

In [127]:
filt  = pd.isna(PH_clients_pograms_2['client_type'])
PH_clients_pograms_2.loc[filt, 'client_type'] = 'client'

In [128]:
PH_clients_pograms_2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 485 entries, 0 to 484
Data columns (total 11 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   Client's First Name       484 non-null    object        
 1   Client's Last Name        466 non-null    object        
 2   Client Name               462 non-null    object        
 3   welligent_id              280 non-null    float64       
 4   airtable_id               255 non-null    object        
 5   Admission Date            460 non-null    datetime64[ns]
 6   Program End Date          203 non-null    object        
 7   Housing Status (at exit)  197 non-null    object        
 8   program                   485 non-null    object        
 9   Location                  464 non-null    object        
 10  client_type               485 non-null    object        
dtypes: datetime64[ns](1), float64(1), object(9)
memory usage: 45.5+ KB


In [129]:
PH_clients_pograms_2['Client Name'] = PH_clients_pograms_2["Client's First Name"]+" "+PH_clients_pograms_2["Client's Last Name"]

In [130]:
PH_clients_pograms_2['Program End Date'].replace(np.nan, pd.NaT, inplace=True)

In [131]:
for index, row in PH_clients_pograms_2.iterrows():
    if re.match('\d+\.0+', str(row['airtable_id'])):
        PH_clients_pograms_2.loc[index, 'airtable_id'] = int(row['airtable_id'])

In [132]:
filt = PH_clients_pograms_2['Client Name'].isna()
PH_clients_pograms_2.drop(PH_clients_pograms_2.loc[filt].index, inplace=True)

In [133]:
filt = PH_clients_pograms_2['Client Name'] == ' '
PH_clients_pograms_2.drop(PH_clients_pograms_2.loc[filt].index, inplace=True)

In [134]:
filt = PH_clients_pograms_2.loc[:,"Client's First Name":"program"].duplicated(keep='last') & pd.isna(PH_clients_pograms_2['Program End Date'])
PH_clients_pograms_2.drop(PH_clients_pograms_2.loc[filt].index, inplace=True)

In [135]:
filt = PH_clients_pograms_2.loc[:,"Client's First Name":"Program End Date"].duplicated(keep='last')
PH_clients_pograms_2.drop(PH_clients_pograms_2.loc[filt].index, inplace=True)

In [136]:
filt = PH_clients_pograms_2.loc[:,"Client's First Name":"Admission Date"].duplicated(keep=False) & pd.isna(PH_clients_pograms_2['Program End Date'])
PH_clients_pograms_2.drop(PH_clients_pograms_2.loc[filt].index, inplace=True)

In [137]:
for index, row in PH_clients_pograms_2.iterrows():
    if 'Addario'.lower() in str(row['Location']).lower():
        PH_clients_pograms_2.loc[index, 'Location'] = "D'Addario"
    elif 'Glenmore '.strip().lower() in str(row['Location']).strip().lower():
        PH_clients_pograms_2.loc[index, 'Location'] = 'Glenmore'
    elif 'Lincoln Residence'.lower() in str(row['Location']).lower():
        PH_clients_pograms_2.loc[index, 'Location'] = 'PH5'
    elif 'Ph4' in str(row['Location']):
        PH_clients_pograms_2.loc[index, 'Location'] = 'PH4'
    elif 'Ph7' in str(row['Location']):
        PH_clients_pograms_2.loc[index, 'Location'] = 'PH7'
    elif 'Prospect Residence' in str(row['Location']):
        PH_clients_pograms_2.loc[index, 'Location'] = 'PH2'
    elif 'sullivan' in str(row['Location']).lower():
        PH_clients_pograms_2.loc[index, 'Location'] = 'Bishop Sullivan'

In [138]:
filt = PH_clients_pograms_2['Client Name'].str.contains('Mileivi')
PH_clients_pograms_2.loc[filt]

Client's First Name Client's Last Name    Client Name  welligent_id  \
308               Munoz            Mileivi  Munoz Mileivi           NaN   
459               Munoz            Mileivi  Munoz Mileivi     5829622.0   

    airtable_id Admission Date Program End Date Housing Status (at exit)  \
308         NaN     2021-04-20       2021-04-22                 Transfer   
459         NaN     2021-04-20              NaT                      NaN   

    program  Location client_type  
308     DHS  Glenmore      client  
459     DHS  Glenmore      client

In [139]:
filt = PH_clients_pograms_2.duplicated(subset=['Client Name', 'Admission Date'], keep='last') & pd.isna(PH_clients_pograms_2['Program End Date'])
PH_clients_pograms_2.drop(PH_clients_pograms_2.loc[filt].index, inplace=True)

In [140]:
filt = PH_clients_pograms_2.duplicated(subset=['Client Name', 'Admission Date'], keep=False) & pd.isna(PH_clients_pograms_2['Program End Date'])
PH_clients_pograms_2.drop(PH_clients_pograms_2.loc[filt].index, inplace=True)

In [141]:
for index, row in PH_clients_pograms_2.iterrows():
    filt = PH_Master_Client_list_2['Client Name'] == row['Client Name']
    welligent_id = PH_Master_Client_list_2.loc[filt, 'Client Welligent ID'].values
    airtable_id = PH_Master_Client_list_2.loc[filt, 'AirtableIDs'].values
    if (welligent_id.size > 0) or (airtable_id.size > 0):
        PH_clients_pograms_2.loc[index, 'welligent_id'] = welligent_id[0]
        PH_clients_pograms_2.loc[index, 'airtable_id'] = airtable_id[0]
    elif (welligent_id.size > 1) or (airtable_id.size > 1):
        PH_clients_pograms_2.loc[index, 'welligent_id'] = welligent_id[1]
        PH_clients_pograms_2.loc[index, 'airtable_id'] = airtable_id[1]
        

In [142]:
filt = PH_clients_pograms_2.duplicated(subset=['Client Name','Program End Date','Housing Status (at exit)', 'program', 'Location', 'client_type'], keep='last')
PH_clients_pograms_2.drop(PH_clients_pograms_2.loc[filt].index, inplace=True)

In [143]:
filt = PH_clients_pograms_2.duplicated(subset='Client Name', keep=False) 
dup_cliens_df = PH_clients_pograms_2.loc[filt].sort_values(by=['Client Name', 'Admission Date']) #duplicate clients with different admission dates
dup_cliens_df

Client's First Name Client's Last Name          Client Name  welligent_id  \
314               Abbie              Scott          Abbie Scott     5839972.0   
484               Abbie              Scott          Abbie Scott     5839972.0   
228              Ashley             Mazyck        Ashley Mazyck     4178029.0   
282              Ashley             Mazyck        Ashley Mazyck     4178029.0   
247              Ashley             Mazyck        Ashley Mazyck     4178029.0   
290           Jackelyne          Fernandez  Jackelyne Fernandez     4120199.0   
217           Jackelyne          Fernandez  Jackelyne Fernandez     4120199.0   
9              Jennifer             Garcia      Jennifer Garcia     4943758.0   
215            Jennifer             Garcia      Jennifer Garcia     4943758.0   
10              Jessica             Cabral       Jessica Cabral     4720115.0   
203             Jessica             Cabral       Jessica Cabral     4720115.0   
224             Jessica             Cabral       Jessica Cabral     4720115.0   
229               Jully      Harry Herrera  Jully Harry Herrera     4736639.0   
12                Jully      Harry Herrera  Jully Harry Herrera     4736639.0   
161            Kimberly              Raker       Kimberly Raker     3944563.0   
61             Kimberly              Raker       Kimberly Raker     3944563.0   
225              Louise              Bines         Louise Bines     5055089.0   
15               Louise              Bines         Louise Bines     5055089.0   
317             Orladia             Rosado       Orladia Rosado     5839983.0   
482             Orladia             Rosado       Orladia Rosado     5839983.0   
378             Ruquana             Blyden       Ruquana Blyden     5777108.0   
483             Ruquana             Blyden       Ruquana Blyden     5777108.0   
269            Savannah             Howard      Savannah Howard     5479471.0   
454            Savannah             Howard      Savannah Howard     5479471.0   
172             Takiera             Hester       Takiera Hester     4379978.0   
187             Takiera             Hester       Takiera Hester     4379978.0   

    airtable_id Admission Date Program End Date      Housing Status (at exit)  \
314         197     2021-04-21              NaT                           NaN   
484         197     2021-05-06              NaT                           NaN   
228         194     2018-09-26              NaT                           NaN   
282         194     2018-12-10       2020-12-30  Independent living/permanent   
247         194     2019-11-15              NaT                      Transfer   
290         188     2018-12-08       2020-12-02         Involuntary discharge   
217         188     2018-12-27              NaT                           NaN   
9           370     2019-11-15       2020-01-08  Independent living/permanent   
215         370     2019-12-04       2019-12-30       AWL/Voluntary discharge   
10                  2019-05-04       2020-04-06  Independent living/permanent   
203                 2019-05-14       2019-09-11                           NaN   
224                 2019-09-19              NaT                           NaN   
229         186     2019-02-09              NaT                           NaN   
12          186     2019-02-10              NaT                           NaN   
161          38     2018-09-27       2019-03-18  Independent living/permanent   
61           38     2019-03-18              NaT                           NaN   
225         182     2019-10-10              NaT                           NaN   
15          182     2019-10-13       2020-05-01  Independent living/permanent   
317         179     2021-04-22              NaT                           NaN   
482         179     2021-05-06              NaT                           NaN   
378         177     2021-03-23       2021-06-14  Independent living/permanent   
483         177     2021-04-14    

In [144]:
dup_cliens_dic = {}


for index, row in dup_cliens_df.iterrows():
    if row['Client Name'] in dup_cliens_dic.keys():
        dup_cliens_dic[row['Client Name']].append(index)
    else:
        dup_cliens_dic[row['Client Name']] = [index]

In [145]:
filt = PH_clients_pograms_2.duplicated(subset='Client Name', keep=False) & pd.isna(PH_clients_pograms_2['Program End Date'])
PH_clients_pograms_2.loc[filt].sort_values(by='Client Name')

Client's First Name Client's Last Name          Client Name  welligent_id  \
314               Abbie              Scott          Abbie Scott     5839972.0   
484               Abbie              Scott          Abbie Scott     5839972.0   
228              Ashley             Mazyck        Ashley Mazyck     4178029.0   
247              Ashley             Mazyck        Ashley Mazyck     4178029.0   
217           Jackelyne          Fernandez  Jackelyne Fernandez     4120199.0   
224             Jessica             Cabral       Jessica Cabral     4720115.0   
12                Jully      Harry Herrera  Jully Harry Herrera     4736639.0   
229               Jully      Harry Herrera  Jully Harry Herrera     4736639.0   
61             Kimberly              Raker       Kimberly Raker     3944563.0   
225              Louise              Bines         Louise Bines     5055089.0   
317             Orladia             Rosado       Orladia Rosado     5839983.0   
482             Orladia             Rosado       Orladia Rosado     5839983.0   
483             Ruquana             Blyden       Ruquana Blyden     5777108.0   
269            Savannah             Howard      Savannah Howard     5479471.0   
454            Savannah             Howard      Savannah Howard     5479471.0   

    airtable_id Admission Date Program End Date Housing Status (at exit)  \
314         197     2021-04-21              NaT                      NaN   
484         197     2021-05-06              NaT                      NaN   
228         194     2018-09-26              NaT                      NaN   
247         194     2019-11-15              NaT                 Transfer   
217         188     2018-12-27              NaT                      NaN   
224                 2019-09-19              NaT                      NaN   
12          186     2019-02-10              NaT                      NaN   
229         186     2019-02-09              NaT                      NaN   
61           38     2019-03-18              NaT                      NaN   
225         182     2019-10-10              NaT                      NaN   
317         179     2021-04-22              NaT                      NaN   
482         179     2021-05-06              NaT                      NaN   
483         177     2021-04-14              NaT                      NaN   
269         300     2020-11-09              NaT                      NaN   
454         300     2021-10-22              NaT                      NaN   

        program         Location client_type  
314         DHS            PH2/7      client  
484         DHS              PH7      client  
228         DHS              PH3      client  
247         DHS              PH7      client  
217         DHS              PH7      client  
224         DHS              PH7      client  
12          DHS            PH2/7      client  
229         DHS              PH3      client  
61   supportive        D'Addario      client  
225         DHS              PH7      client  
317         DHS            PH2/7      client  
482         DHS              PH7      client  
483         DHS              PH7      client  
269         WJP              PH5      client  
454  supportive  Bishop Sullivan      tenant

In [146]:
filt = PH_clients_pograms_2.duplicated(subset='Client Name', keep=False)
PH_clients_pograms_2.loc[filt].sort_values(by=['Client Name', 'Admission Date'])

Client's First Name Client's Last Name          Client Name  welligent_id  \
314               Abbie              Scott          Abbie Scott     5839972.0   
484               Abbie              Scott          Abbie Scott     5839972.0   
228              Ashley             Mazyck        Ashley Mazyck     4178029.0   
282              Ashley             Mazyck        Ashley Mazyck     4178029.0   
247              Ashley             Mazyck        Ashley Mazyck     4178029.0   
290           Jackelyne          Fernandez  Jackelyne Fernandez     4120199.0   
217           Jackelyne          Fernandez  Jackelyne Fernandez     4120199.0   
9              Jennifer             Garcia      Jennifer Garcia     4943758.0   
215            Jennifer             Garcia      Jennifer Garcia     4943758.0   
10              Jessica             Cabral       Jessica Cabral     4720115.0   
203             Jessica             Cabral       Jessica Cabral     4720115.0   
224             Jessica             Cabral       Jessica Cabral     4720115.0   
229               Jully      Harry Herrera  Jully Harry Herrera     4736639.0   
12                Jully      Harry Herrera  Jully Harry Herrera     4736639.0   
161            Kimberly              Raker       Kimberly Raker     3944563.0   
61             Kimberly              Raker       Kimberly Raker     3944563.0   
225              Louise              Bines         Louise Bines     5055089.0   
15               Louise              Bines         Louise Bines     5055089.0   
317             Orladia             Rosado       Orladia Rosado     5839983.0   
482             Orladia             Rosado       Orladia Rosado     5839983.0   
378             Ruquana             Blyden       Ruquana Blyden     5777108.0   
483             Ruquana             Blyden       Ruquana Blyden     5777108.0   
269            Savannah             Howard      Savannah Howard     5479471.0   
454            Savannah             Howard      Savannah Howard     5479471.0   
172             Takiera             Hester       Takiera Hester     4379978.0   
187             Takiera             Hester       Takiera Hester     4379978.0   

    airtable_id Admission Date Program End Date      Housing Status (at exit)  \
314         197     2021-04-21              NaT                           NaN   
484         197     2021-05-06              NaT                           NaN   
228         194     2018-09-26              NaT                           NaN   
282         194     2018-12-10       2020-12-30  Independent living/permanent   
247         194     2019-11-15              NaT                      Transfer   
290         188     2018-12-08       2020-12-02         Involuntary discharge   
217         188     2018-12-27              NaT                           NaN   
9           370     2019-11-15       2020-01-08  Independent living/permanent   
215         370     2019-12-04       2019-12-30       AWL/Voluntary discharge   
10                  2019-05-04       2020-04-06  Independent living/permanent   
203                 2019-05-14       2019-09-11                           NaN   
224                 2019-09-19              NaT                           NaN   
229         186     2019-02-09              NaT                           NaN   
12          186     2019-02-10              NaT                           NaN   
161          38     2018-09-27       2019-03-18  Independent living/permanent   
61           38     2019-03-18              NaT                           NaN   
225         182     2019-10-10              NaT                           NaN   
15          182     2019-10-13       2020-05-01  Independent living/permanent   
317         179     2021-04-22              NaT                           NaN   
482         179     2021-05-06              NaT                           NaN   
378         177     2021-03-23       2021-06-14  Independent living/permanent   
483         177     2021-04-14    

In [147]:
filt = pd.isna(PH_clients_pograms_2['Admission Date'])
PH_clients_pograms_2.drop(PH_clients_pograms_2.loc[filt].index, inplace=True)

In [148]:
filt = PH_clients_pograms_2.client_type.isna()
PH_clients_pograms_2.loc[filt]

Empty DataFrame
Columns: [Client's First Name, Client's Last Name, Client Name, welligent_id, airtable_id, Admission Date, Program End Date, Housing Status (at exit), program, Location, client_type]
Index: []

In [149]:
PH_clients_pograms_2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 390 entries, 0 to 484
Data columns (total 11 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   Client's First Name       390 non-null    object        
 1   Client's Last Name        390 non-null    object        
 2   Client Name               390 non-null    object        
 3   welligent_id              318 non-null    float64       
 4   airtable_id               340 non-null    object        
 5   Admission Date            390 non-null    datetime64[ns]
 6   Program End Date          202 non-null    datetime64[ns]
 7   Housing Status (at exit)  197 non-null    object        
 8   program                   390 non-null    object        
 9   Location                  390 non-null    object        
 10  client_type               390 non-null    object        
dtypes: datetime64[ns](2), float64(1), object(8)
memory usage: 36.6+ KB


In [150]:
[x for x in map(str, PH_Master_Client_list_2['Client Name']) if str(x) not in map(str, PH_clients_pograms_2['Client Name'])]

[]

## Children

In [151]:
PH_children_master_list_2 = pd.DataFrame()

for df_name, df in children_sheets.items():
    for index, row in df.iterrows():
        PH_children_master_list_2 = PH_children_master_list_2.append({k:row[k] for k in df.columns}, ignore_index=True)

In [152]:
children_cols = """Parent_Name	Child_FirstName	Child_LastName	Children's_Name	DOB	DayCare_Start_Date	PreSchool_Start_Date	Primary_School_Start_Date	Data Entry Date""".split('\t')

In [153]:
PH_children_master_list_2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 770 entries, 0 to 769
Data columns (total 31 columns):
 #   Column                     Non-Null Count  Dtype         
---  ------                     --------------  -----         
 0   Child_FirstName            675 non-null    object        
 1   Child_LastName             630 non-null    object        
 2   Children's_Name            654 non-null    object        
 3   DOB                        627 non-null    object        
 4   Data Entry Date            521 non-null    object        
 5   DayCare_Start_Date         58 non-null     datetime64[ns]
 6   Notes:                     338 non-null    object        
 7   Parent_Name                643 non-null    object        
 8   PreSchool_Start_Date       20 non-null     datetime64[ns]
 9   Primary_School_Start_Date  251 non-null    object        
 10  Unnamed: 10                2 non-null      object        
 11  Unnamed: 11                8 non-null      object        
 12  Unnamed:

In [154]:
PH_children_master_list_2 = PH_children_master_list_2[PH_children_master_list_2.columns.intersection(children_cols)].copy()

In [155]:
PH_children_master_list_2 = PH_children_master_list_2.reindex(columns=children_cols)

In [156]:
PH_children_master_list_2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 770 entries, 0 to 769
Data columns (total 9 columns):
 #   Column                     Non-Null Count  Dtype         
---  ------                     --------------  -----         
 0   Parent_Name                643 non-null    object        
 1   Child_FirstName            675 non-null    object        
 2   Child_LastName             630 non-null    object        
 3   Children's_Name            654 non-null    object        
 4   DOB                        627 non-null    object        
 5   DayCare_Start_Date         58 non-null     datetime64[ns]
 6   PreSchool_Start_Date       20 non-null     datetime64[ns]
 7   Primary_School_Start_Date  251 non-null    object        
 8   Data Entry Date            521 non-null    object        
dtypes: datetime64[ns](2), object(7)
memory usage: 54.3+ KB


In [157]:
for col in PH_children_master_list_2.columns:
    if 'date' in col.lower() or 'dob' in col.lower():
        PH_children_master_list_2[col] = pd.to_datetime(PH_children_master_list_2[col], errors='coerce')

In [158]:
PH_children_master_list_2["Children's_Name"] = PH_children_master_list_2['Child_FirstName'].str.strip().str.title()+" "+PH_children_master_list_2['Child_LastName'].str.strip().str.title()
PH_children_master_list_2['Child_FirstName'] = PH_children_master_list_2['Child_FirstName'].str.strip().str.title()
PH_children_master_list_2['Child_LastName'] = PH_children_master_list_2['Child_LastName'].str.strip().str.title()
PH_children_master_list_2['Parent_Name'] = PH_children_master_list_2['Parent_Name'].str.strip().str.title().apply(lambda x: re.sub(' +', ' ',str(x)))

In [159]:
PH_children_master_list_2.replace('nan', np.nan, inplace=True)

In [160]:
filt = PH_children_master_list_2.duplicated()
PH_children_master_list_2.drop(PH_children_master_list_2.loc[filt].index, inplace=True)

In [161]:
filt = PH_children_master_list_2["Children's_Name"].isna()
PH_children_master_list_2.drop(PH_children_master_list_2.loc[filt].index, inplace=True)

In [162]:
filt = PH_children_master_list_2.duplicated(subset=["Children's_Name",'DOB' ], keep='last') & pd.isna(PH_children_master_list_2['Primary_School_Start_Date'])
PH_children_master_list_2.drop(PH_children_master_list_2.loc[filt].index, inplace=True)

In [163]:
filt = PH_children_master_list_2.duplicated(subset=["Children's_Name",'DOB' ], keep='last')
PH_children_master_list_2.drop(PH_children_master_list_2.loc[filt].index, inplace=True)

In [164]:
filt = PH_children_master_list_2.duplicated(subset="Children's_Name", keep=False) & PH_children_master_list_2.loc[:, 'DOB':'Data Entry Date'].isna().apply(lambda x:all(x), axis=1)
PH_children_master_list_2.drop(PH_children_master_list_2.loc[filt].index, inplace=True)

In [165]:
children_cols = """admitDate exitDate intakeAge""".split()

In [166]:
PH_children_master_list_2[children_cols] = np.nan

In [167]:
for index, row in PH_children_master_list_2.iterrows():
    filt = PH_clients_pograms_2['Client Name'].str.lower().str.strip() == str(row['Parent_Name']).lower().strip()
    adminDate = PH_clients_pograms_2.loc[filt, 'Admission Date'].values
    exitDate = PH_clients_pograms_2.loc[filt, 'Program End Date'].values
    if adminDate.size == 0:
        PH_children_master_list_2.loc[index, 'admitDate'] = pd.NaT
    elif adminDate.size == 1:
        PH_children_master_list_2.loc[index, 'admitDate'] = adminDate[0]
    else:
        PH_children_master_list_2.loc[index, 'admitDate'] = adminDate[-1]
        
    if exitDate.size == 0:
        PH_children_master_list_2.loc[index, 'exitDate'] = pd.NaT
    elif exitDate.size == 1:
        PH_children_master_list_2.loc[index, 'exitDate'] = exitDate[0]
    else:
        PH_children_master_list_2.loc[index, 'exitDate'] = exitDate[-1]
    

In [168]:
PH_children_master_list_2['admitDate'] = pd.to_datetime(PH_children_master_list_2['admitDate'])
PH_children_master_list_2['exitDate'].replace(np.nan, pd.NaT, inplace=True)
PH_children_master_list_2['exitDate'] = pd.to_datetime(PH_children_master_list_2['exitDate'])

In [169]:
for index, row in PH_children_master_list_2.iterrows():
    if pd.isna(row['DOB']) | pd.isna(row['admitDate']):
        PH_children_master_list_2.loc[index, 'intakeAge'] = np.nan
        
    else:
        if (row['admitDate'] - row['DOB']).days/365 < 0:
            continue
        else:
            PH_children_master_list_2.loc[index, 'intakeAge'] = int((row['admitDate'] - row['DOB']).days/365)

In [170]:
PH_children_master_list_2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 383 entries, 0 to 764
Data columns (total 12 columns):
 #   Column                     Non-Null Count  Dtype         
---  ------                     --------------  -----         
 0   Parent_Name                380 non-null    object        
 1   Child_FirstName            383 non-null    object        
 2   Child_LastName             383 non-null    object        
 3   Children's_Name            383 non-null    object        
 4   DOB                        376 non-null    datetime64[ns]
 5   DayCare_Start_Date         41 non-null     datetime64[ns]
 6   PreSchool_Start_Date       7 non-null      datetime64[ns]
 7   Primary_School_Start_Date  139 non-null    datetime64[ns]
 8   Data Entry Date            300 non-null    datetime64[ns]
 9   admitDate                  323 non-null    datetime64[ns]
 10  exitDate                   163 non-null    datetime64[ns]
 11  intakeAge                  298 non-null    float64       
dtypes: datet

In [171]:
filt = PH_children_master_list_2['admitDate'].isna()
PH_children_master_list_2.loc[filt]

Parent_Name Child_FirstName   Child_LastName  \
112          Betty Henry         Messiah            Henry   
113       Brianna Lebron          Camryn         Ferguson   
116      Cherokee Holden          Pharon           Holden   
118         Deja Venture          Tashae           Mosley   
119       Denisha Howard          Audrey           Howard   
120      Destiny Snowden             Ava            Lucas   
121       Destiny Thomas           Amara           Thomas   
127       Equasia Savage        Sailheen          Wigwall   
138           Jasmin Day            Teri          Griffin   
139        Jasmine Adams         Zaniynh            Adams   
147        Leeana Robles          Olivia           Robles   
154     Robemny Bautista        Isabella    Bautista Roma   
156           Sacha Daye          Josiah           Duclas   
157           Sacha Daye        Jeremiah           Duclas   
159         Shaday Tripp          Skylar            Tripp   
161       Sharon Goggans         Shannah          Goggans   
163        Shazma Nelson         Graycen           Nelson   
164    Shellyann Polanco             Mia          Polanco   
165      Sushana Parsley         Riquane             Wade   
185         Anaiya Brame         Melanie           Miller   
186        Alexis Warnic         Royalty            Sewer   
187     Breanna Crawford          Apphia         Crawford   
190       Chelsea Thomas         Cyncere         Mckellar   
191      Cheyenne Lyerly         Brielle            Logan   
192        Emily Camacho          Elijah          Camacho   
193        Devonna Quinn         Akeelah           Brewer   
194      Desiree Roberts          Autumn          Roberts   
196     Jacqulynn Robles           Aidah           Wilson   
197     Jacqulynn Robles        Skarlett           Graham   
198        Jessica Reyes        Anamarie            Reyes   
199        Jessica Reyes         Analisa            Reyes   
202       Katrina Harris          Justin            Kirby   
203         Kayla Wilson        Jeremiah          Bigelow   
205         Khady Ndiaye          Emilie            Gomis   
206      Ladelia Cureton      Brook-Lynn        Blackwell   
208       Lawanda Stroud          Josiah            Myers   
210           Mia Moorer           Spady             King   
213       Porsha Shelton         Zopyros        Heckstall   
214    Raquel Washington          Denver       Washington   
215        Regina Carter         Kharter           Segree   
216        Rihab Karrout           Layla          Gardner   
217      Saisaiah Mcfall           Chase           Bascoe   
219         Shanika Lyde        Kylieann           Holmes   
220   Shaniqua Blackwood         Na'Zier           Mcneil   
221         Sobnia Yizar           Aidan            Yizar   
222    Stephanie Jimenez            Amir          Nichols   
226    Ta’Sheena Johnson        Ja'Layah          Johnson   
227      Tarhonda Mcgill        Blessing           Mcgill   
228       Tatiana Tacuri           Janet             Diaz   
229      Tayael Mccollop        Jhon-Tay          Coghiel   
230          Terri Hines          Jaliah            Hines   
231        Ursula Stokes            Kash           Brooks   
232       Violeta Jaquez           Angel           Jaquez   
233        Zeronia Henry        Ze-Karly            Henry   
364     Shakeym Barquero        Kharisma         Barquero   
365     Shakeym Barquero         Jayceon         Barquero   
487  Meaghen Goodermoote          Amirah  Morbillo-Torres   
528                  NaN          Safari      Cabral Cruz   
664                  NaN      Dae'Vionna          Stewart   
742                  NaN          Aurora            Hugee   

            Children's_Name        DOB DayCare_Start_Date  \
112           Messiah Henry 2017-06-13                NaT   
113         Camryn Ferguson 2015-02-27         2018-05-30   
116           Pharon Holden 2016-09-17                NaT   
118           Tashae Mosley 2016-01-22         

# Summary table

In [172]:
columns = """Client Name
DOB
Admission_dates
Program End Date
Adults served
Children served
Average age of adult intake
Average age of child intake
Households eligible to work in period
Households with employment in period
Adults with mental health needs
Number of above connected with mental health service provider
Adults with active substance abuse
Adults in recovery
Average length of stay (intake to discharge) in days
Ethnicity: Hispanic
Ethnicity: Non-Hispanic
Race: Black
Race: White
Race: Asian/Pacific Islander
Race: Multi-Racial
Education at intake: GED/HSE/HSD
Education at intake: Some College
Education at intake: No HSE/GED/High School
Education at intake: Bachelor's Degree
Education at intake: Associate's Degree
Education at intake: Post-graduate Degree 
Housing outcome at discharge: AWOL/Back to shelter
Housing outcome at discharge: Deceased
Housing outcome at discharge: Eviction
Housing outcome at discharge: Independent living/permanent
Housing outcome at discharge: Ineligible
Housing outcome at discharge: Involuntary discharge
Housing outcome at discharge: Voluntary Discharge
Housing outcome at discharge: Transfer
Residents connected with medical provider in period
Period_start_date
Period_end_date
program
Location""".split('\n')


In [173]:
PH_qrtly_summary_df = pd.DataFrame(columns=columns)

In [174]:
start= '12/10/2017'
start = pd.to_datetime(start)
currQuater = int((start.month-1)/3+1)
dtfirstDay = datetime.datetime(start.year, 3* currQuater - 2, 1)
dtfirstDay

datetime.datetime(2017, 10, 1, 0, 0)

In [175]:
PH_clients_pograms_2.columns

Index(['Client's First Name', 'Client's Last Name', 'Client Name',
       'welligent_id', 'airtable_id', 'Admission Date', 'Program End Date',
       'Housing Status (at exit)', 'program', 'Location', 'client_type'],
      dtype='object')

In [176]:
PH_clients_pograms_2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 390 entries, 0 to 484
Data columns (total 11 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   Client's First Name       390 non-null    object        
 1   Client's Last Name        390 non-null    object        
 2   Client Name               390 non-null    object        
 3   welligent_id              318 non-null    float64       
 4   airtable_id               340 non-null    object        
 5   Admission Date            390 non-null    datetime64[ns]
 6   Program End Date          202 non-null    datetime64[ns]
 7   Housing Status (at exit)  197 non-null    object        
 8   program                   390 non-null    object        
 9   Location                  390 non-null    object        
 10  client_type               390 non-null    object        
dtypes: datetime64[ns](2), float64(1), object(8)
memory usage: 36.6+ KB


In [177]:
for index, row in PH_clients_pograms_2.iterrows():
    admit_date = row['Admission Date']
    if pd.isna(row['Program End Date']):
        exit_date = datetime.date.today()
    else:
        exit_date = row['Program End Date']
    currQuarter = int((admit_date.month-1)/3+1)
    dtfirstDay = datetime.datetime(admit_date.year, 3 * currQuarter - 2, 1)
    quarters = pd.date_range(dtfirstDay, exit_date, freq='QS')
    
    for quarter_start in quarters:
        quarter_end = quarter_start + relativedelta(months=3, days=-1)
        
        PH_qrtly_summary_df = PH_qrtly_summary_df.append({'Client Name': row['Client Name'], 'Period_start_date': quarter_start,  'Period_end_date': quarter_end, 'program': row['program'], 'Location': row['Location'],  'Program End Date': row['Program End Date'], 'Admission_dates': row['Admission Date']}, ignore_index=True)

In [178]:
PH_qrtly_summary_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3297 entries, 0 to 3296
Data columns (total 40 columns):
 #   Column                                                         Non-Null Count  Dtype         
---  ------                                                         --------------  -----         
 0   Client Name                                                    3297 non-null   object        
 1   DOB                                                            0 non-null      object        
 2   Admission_dates                                                3297 non-null   datetime64[ns]
 3   Program End Date                                               1033 non-null   datetime64[ns]
 4   Adults served                                                  0 non-null      object        
 5   Children served                                                0 non-null      object        
 6   Average age of adult intake                                    0 non-null      object        
 7

In [179]:
PH_Master_Client_list_2.columns

Index(['Client Name', 'Client's DOB', 'Client's First Name',
       'Client's Last Name', 'Education', 'Ethnicity', 'Race', 'MHP at intake',
       'Medical Condition at intake', 'Mental Health Needs at intake',
       'PCP at intake', 'Substance Use Provider at intake',
       'Substance Use at intake', 'AirtableIDs', 'Client Welligent ID',
       'ClientName_LastNameFirstName'],
      dtype='object')

In [180]:
for index, row in PH_qrtly_summary_df.iterrows():
    filt = PH_Master_Client_list_2['Client Name'] == row['Client Name']
    DOB = PH_Master_Client_list_2.loc[filt, "Client's DOB"].values
    race = PH_Master_Client_list_2.loc[filt, "Race"].values
    edu = PH_Master_Client_list_2.loc[filt, "Education"].values
    eth = PH_Master_Client_list_2.loc[filt, 'Ethnicity'].values
    if DOB.size == 0:
        PH_qrtly_summary_df.loc[index,'DOB'] = pd.NaT
    else:
        PH_qrtly_summary_df.loc[index,'DOB'] = pd.to_datetime(DOB[0], format='%Y-%m-%d')
    
    if race.size == 0:
        PH_qrtly_summary_df.loc[index,'Race'] = np.nan
    else:
        PH_qrtly_summary_df.loc[index,'Race'] = race[0]
    
    if edu.size == 0:
        PH_qrtly_summary_df.loc[index,"Education"] = np.nan
    else:
        PH_qrtly_summary_df.loc[index,"Education"] = edu[0]
    
    if eth.size == 0:
        PH_qrtly_summary_df.loc[index,'Ethnicity'] = np.nan
    else:
        PH_qrtly_summary_df.loc[index,'Ethnicity'] = eth[0]    
        

In [181]:
all_clients_info_df = pd.DataFrame()

for df_name, df in sheets.items():
    period = df_name[:6]
    program = df_name[7:] 
    for index, row in df.iterrows():
        all_clients_info_df = all_clients_info_df.append({k:row[k] for k in df.columns}, ignore_index=True)
        all_clients_info_df.loc[all_clients_info_df.tail(1).index.item(), 'program'] = program
        all_clients_info_df.loc[all_clients_info_df.tail(1).index.item(), 'period'] = period

In [182]:
for column in all_clients_info_df.columns:
        if re.match('mental health needs \d{4} qtr \d\w{2}', str(column).lower()):
            print(column)

Mental Health Needs 2020 QTR 1st
Mental Health Needs 2020 QTR 2nd
Mental Health Needs 2020 QTR 3rd
Mental Health Needs 2020 QTR 4th
Mental Health Needs 2019 QTR 1st
Mental Health Needs 2019 QTR 2nd
Mental Health Needs 2019 QTR 3rd
Mental Health Needs 2019 QTR 4th
Mental Health Needs 2021 QTR 1st
Mental Health Needs 2021 QTR 2nd
Mental Health Needs 2021 QTR 3rd
Mental Health Needs 2021 QTR 4th


In [183]:
# check for duplicated columns

for column in all_clients_info_df.columns:
    if all_clients_info_df.columns.to_list().count(column) > 1:
        print(column)

In [184]:
for col in all_clients_info_df.columns:
    if 'unnamed' in col.lower():
        all_clients_info_df.drop(columns=col, inplace=True)
 

In [185]:
all_clients_info_df.isna().apply(lambda x:all(x), axis=1).sum()

0

In [186]:
filt = PH_qrtly_summary_df.duplicated(subset=['Client Name', 'Period_start_date'],keep=False)
PH_qrtly_summary_df.loc[filt].sort_values(by=['Client Name', 'Period_start_date'])

Client Name                  DOB Admission_dates  \
2371          Abbie Scott  1990-12-28 00:00:00      2021-04-21   
3294          Abbie Scott  1990-12-28 00:00:00      2021-05-06   
2372          Abbie Scott  1990-12-28 00:00:00      2021-04-21   
3295          Abbie Scott  1990-12-28 00:00:00      2021-05-06   
2373          Abbie Scott  1990-12-28 00:00:00      2021-04-21   
3296          Abbie Scott  1990-12-28 00:00:00      2021-05-06   
1943        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2256        Ashley Mazyck  1984-03-26 00:00:00      2018-12-10   
1944        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2257        Ashley Mazyck  1984-03-26 00:00:00      2018-12-10   
1945        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2258        Ashley Mazyck  1984-03-26 00:00:00      2018-12-10   
1946        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2259        Ashley Mazyck  1984-03-26 00:00:00      2018-12-10   
1947        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2116        Ashley Mazyck  1984-03-26 00:00:00      2019-11-15   
2260        Ashley Mazyck  1984-03-26 00:00:00      2018-12-10   
1948        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2117        Ashley Mazyck  1984-03-26 00:00:00      2019-11-15   
2261        Ashley Mazyck  1984-03-26 00:00:00      2018-12-10   
1949        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2118        Ashley Mazyck  1984-03-26 00:00:00      2019-11-15   
2262        Ashley Mazyck  1984-03-26 00:00:00      2018-12-10   
1950        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2119        Ashley Mazyck  1984-03-26 00:00:00      2019-11-15   
2263        Ashley Mazyck  1984-03-26 00:00:00      2018-12-10   
1951        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2120        Ashley Mazyck  1984-03-26 00:00:00      2019-11-15   
2264        Ashley Mazyck  1984-03-26 00:00:00      2018-12-10   
1952        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2121        Ashley Mazyck  1984-03-26 00:00:00      2019-11-15   
1953        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2122        Ashley Mazyck  1984-03-26 00:00:00      2019-11-15   
1954        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2123        Ashley Mazyck  1984-03-26 00:00:00      2019-11-15   
1955        Ashley Mazyck  1984-03-26 00:00:00      2018-09-26   
2124        Ashley Mazyck  1984-03-26 00:00:00      2019-11-15   
1867  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-27   
2284  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-08   
1868  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-27   
2285  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-08   
1869  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-27   
2286  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-08   
1870  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-27   
2287  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-08   
1871  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-27   
2288  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-08   
1872  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-27   
2289  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-08   
1873  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-27   
2290  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-08   
1874  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-27   
2291  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-08   
1875  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-27   
2292  Jackelyne Fernandez  1991-05-02 00:00:00      2018-12-08   
21        Jennifer Garcia  1997-05-19 00:00:00      2019-11-15   
1866      Jennifer Garcia  1997-05-19 00:00:00      2019-12-04   
23         Jessica Cabral  1995-08-28 00:00:00      2019-05-04   
1842       Jessica Cabral  1995-08-28 00:00:00      2019-05-14   
24         Jessica Cabral  1995-08-28 00:00:00      20

In [187]:
filt = PH_clients_pograms_2['client_type'] == 'tenant'
PH_clients_pograms_2.loc[filt]

Client's First Name Client's Last Name          Client Name  welligent_id  \
433            Patricia             Albert      Patricia Albert           2.0   
434             Yolanda        Billingslea  Yolanda Billingslea           6.0   
435             Keianda              Henry        Keianda Henry          21.0   
436             Rosalie            Cutting      Rosalie Cutting          12.0   
437                Lisa             Cepeda          Lisa Cepeda          10.0   
438              Saytra         Cattenhead    Saytra Cattenhead           NaN   
440               Jamie          Hernandez      Jamie Hernandez          22.0   
441              Kechia          Jefferies     Kechia Jefferies           NaN   
442              Luther                Lee           Luther Lee          34.0   
443             Katrina             Mcadoo       Katrina Mcadoo          37.0   
444              Antone          Nicholson     Antone Nicholson           NaN   
445               Erica            Saldana        Erica Saldana          48.0   
446              Evelyn            Santana       Evelyn Santana          49.0   
447              Jisset            Tavarez       Jisset Tavarez          53.0   
448             Pauline              Hunte        Pauline Hunte          25.0   
449             Raymond             Arroyo       Raymond Arroyo           4.0   
450              Stacey           Thompson      Stacey Thompson          54.0   
451             Delores             Walker       Delores Walker          56.0   
452              Janeen         Washington    Janeen Washington          58.0   
453               Isaac            Edgardo        Isaac Edgardo           NaN   
454            Savannah             Howard      Savannah Howard     5479471.0   
456             Tanisha         Willingham   Tanisha Willingham          62.0   

    airtable_id Admission Date Program End Date Housing Status (at exit)  \
433         NaN     2013-03-23              NaT                      NaN   
434         NaN     2015-08-21              NaT                      NaN   
435         NaN     2016-08-09       2018-12-09    Involuntary Discharge   
436         NaN     2015-10-13       2021-10-01      Independent Housing   
437         NaN     2014-11-22              NaT                      NaN   
438         NaN     2014-12-24       2020-04-05                    Death   
440         NaN     2013-06-14              NaT                      NaN   
441         NaN     2016-09-06              NaT                      NaN   
442         NaN     2013-05-10              NaT                      NaN   
443         NaN     2013-03-21              NaT                      NaN   
444         NaN     2013-07-03              NaT                      NaN   
445         NaN     2014-11-25              NaT                      NaN   
446         NaN     2014-11-26              NaT                      NaN   
447         NaN     2014-05-16       2021-04-30      Independent Housing   
448         NaN     2013-04-18       2018-06-01     Family Reunification   
449         NaN     2013-03-30       2020-05-16      Independent Housing   
450         NaN     2013-06-10              NaT                      NaN   
451         NaN     2013-06-12              NaT                      NaN   
452         NaN     2013-03-21              NaT                      NaN   
453         NaN     2018-11-01       2020-02-01                    Death   
454         300     2021-10-22              NaT                      NaN   
456         NaN     2016-09-01              NaT                      NaN   

        program         Location client_type  
433  supportive        D'Addario      tenant  
434  supportive        D'Addario      tenant  
435  supportive        D'Addario      tenant  
436  supportive        D'Addario      tenant  
437  supportive  Bishop Sullivan      tenant  
438  supportive  Bishop Sullivan      tenant  
440  supportive        D'Addario      tenant  
441  supportive

In [188]:
all_clients_info_df["Client's First Name"] = all_clients_info_df["Client's First Name"].str.strip().str.title()
all_clients_info_df["Client's Last Name"] = all_clients_info_df["Client's Last Name"].str.strip().str.title()
all_clients_info_df['Client Name'] = all_clients_info_df["Client's First Name"]+" "+all_clients_info_df["Client's Last Name"]

In [189]:
all_clients_info_df.replace('nan', np.nan, inplace=True)

In [190]:
all_clients_info_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1390 entries, 0 to 1389
Data columns (total 99 columns):
 #   Column                                              Non-Null Count  Dtype         
---  ------                                              --------------  -----         
 0   # of Children Living w/Client                       741 non-null    float64       
 1   # of Children NOT Living w/Client                   693 non-null    float64       
 2   Admission Date                                      754 non-null    datetime64[ns]
 3   Client Name                                         1390 non-null   object        
 4   Client's DOB                                        741 non-null    datetime64[ns]
 5   Client's First Name                                 1390 non-null   object        
 6   Client's Last Name                                  1390 non-null   object        
 7   Education                                           732 non-null    object        
 8   Ethnicit

In [191]:
all_clients_info_df.head()

# of Children Living w/Client  # of Children NOT Living w/Client  \
0                            1.0                                0.0   
1                            2.0                                0.0   
2                            1.0                                0.0   
3                            2.0                                0.0   
4                            1.0                                0.0   

  Admission Date       Client Name Client's DOB Client's First Name  \
0     2019-07-17  Aimahlia Newsome   1992-03-04            Aimahlia   
1     2019-04-16   Allana Brissett   1993-04-17              Allana   
2     2019-02-14    Anissa Delaney   1993-09-09              Anissa   
3     2020-06-08     Antasia Moore   1995-03-07             Antasia   
4     2018-12-10     Ashley Mazyck   1984-03-26              Ashley   

  Client's Last Name               Education     Ethnicity  \
0            Newsome  No HSE/GED/High School  Non Hispanic   
1           Brissett            Some College  Non Hispanic   
2            Delaney             GED/HSE/HSD  Non Hispanic   
3              Moore            Some College  Non Hispanic   
4             Mazyck            Some College  Non Hispanic   

  Housing Status (Current;  If changed from at exit)  ... PCP 2021 QTR 3rd  \
0                                                NaN  ...              NaN   
1                                                NaN  ...              NaN   
2                                                NaN  ...              NaN   
3                                                NaN  ...              NaN   
4                                                NaN  ...              NaN   

  PCP 2021 QTR 4th Substance Use 2021 QTR 2nd Substance Use 2021 QTR 3rd  \
0              NaN                        NaN                        NaN   
1              NaN                        NaN                        NaN   
2              NaN                        NaN                        NaN   
3              NaN                        NaN                        NaN   
4              NaN                        NaN                        NaN   

  Substance Use 2021 QTR 4th Substance Use Provider 2021 QTR 1st  \
0                        NaN                                 NaN   
1                        NaN                                 NaN   
2                        NaN                                 NaN   
3                        NaN                                 NaN   
4                        NaN                                 NaN   

  Substance Use Provider 2021 QTR 2nd Substance Use Provider 2021 QTR 3rd  \
0                                 NaN                                 NaN   
1                                 NaN                                 NaN   
2                                 NaN                                 NaN   
3                                 NaN                                 NaN   
4                                 NaN                                 NaN   

  Substance Use Provider 2021 QTR 4th Substance Use Provider 2021 2nd QTR  
0                                 NaN                                 NaN  
1                                 NaN                                 NaN  
2                                 NaN                                 NaN  
3                                 NaN                                 NaN  
4                                 NaN                                 NaN  

[5 rows x 99 columns]

In [192]:
all_clients_info_df['period']

0       cy20q3
1       cy20q3
2       cy20q3
3       cy20q3
4       cy20q3
5       cy20q3
6       cy20q3
7       cy20q3
8       cy20q3
9       cy20q3
10      cy20q3
11      cy20q3
12      cy20q3
13      cy20q3
14      cy20q3
15      cy20q3
16      cy20q3
17      cy20q3
18      cy20q3
19      cy20q3
20      cy20q3
21      cy20q3
22      cy20q3
23      cy20q3
24      cy20q3
25      cy20q3
26      cy20q3
27      cy20q3
28      cy20q3
29      cy20q3
30      cy20q3
31      cy20q3
32      cy20q3
33      cy20q3
34      cy20q3
35      cy20q3
36      cy20q3
37      cy20q3
38      cy20q3
39      cy20q3
40      cy20q3
41      cy20q3
42      cy20q3
43      cy20q3
44      cy20q3
45      cy20q3
46      cy20q3
47      cy20q3
48      cy20q3
49      cy20q3
50      cy20q3
51      cy20q3
52      cy20q3
53      cy20q3
54      cy20q3
55      cy20q3
56      cy20q3
57      cy20q3
58      cy20q3
59      cy20q3
60      cy20q3
61      cy20q3
62      cy20q3
63      cy20q3
64      cy20q3
65      cy20q3
66      cy

In [193]:
int('cy20q3'[-1])

3

In [194]:
pd.to_datetime('cy20q3'[2:4], format='%y').year

2020

In [195]:
pd.to_datetime([x[2:4] for x in all_clients_info_df['period']], format='%y').year

Int64Index([2020, 2020, 2020, 2020, 2020, 2020, 2020, 2020, 2020, 2020,
            ...
            2021, 2021, 2021, 2021, 2021, 2021, 2021, 2021, 2021, 2021],
           dtype='int64', length=1390)

In [196]:
[x[-1] for x in all_clients_info_df['period']]

['3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3',
 '3'

In [197]:
for index, row in all_clients_info_df.iterrows():
    quarter = int(row['period'][-1])
    dtfirstDay = datetime.datetime(pd.to_datetime(row['period'][2:4], format='%y').year, 3 * quarter - 2, 1)
    all_clients_info_df.loc[index, 'Period_start_date'] = dtfirstDay


In [198]:
all_clients_info_df['Period_start_date'] = pd.to_datetime(all_clients_info_df['Period_start_date'])

In [199]:
currQuarter = int((admit_date.month-1)/3+1)
dtfirstDay = datetime.datetime(admit_date.year, 3 * currQuarter - 2, 1)

In [200]:
PH_qrtly_summary_df = pd.merge(PH_qrtly_summary_df, all_clients_info_df, how='left', left_on=['Client Name', 'Period_start_date', 'program'], right_on=['Client Name', 'Period_start_date', 'program'], )

In [201]:
PH_qrtly_summary_df.columns

Index(['Client Name', 'DOB', 'Admission_dates', 'Program End Date_x',
       'Adults served', 'Children served', 'Average age of adult intake',
       'Average age of child intake', 'Households eligible to work in period',
       'Households with employment in period',
       ...
       'PCP 2021 QTR 3rd', 'PCP 2021 QTR 4th', 'Substance Use 2021 QTR 2nd',
       'Substance Use 2021 QTR 3rd', 'Substance Use 2021 QTR 4th',
       'Substance Use Provider 2021 QTR 1st',
       'Substance Use Provider 2021 QTR 2nd',
       'Substance Use Provider 2021 QTR 3rd',
       'Substance Use Provider 2021 QTR 4th',
       'Substance Use Provider 2021 2nd QTR'],
      dtype='object', length=140)

In [202]:
np.where(pd.isna(PH_qrtly_summary_df['DOB']), 'Yes', 'No')

array(['No', 'No', 'No', ..., 'No', 'No', 'No'], dtype='<U3')

In [203]:
for index, row in PH_qrtly_summary_df.iterrows():
    if pd.isna(row['DOB']):
        continue
    else:
        if (row['Period_start_date'] <= row['Admission_dates'] <=row['Period_end_date']):
            PH_qrtly_summary_df.loc[index, 'Average age of adult intake'] = int((row['Admission_dates'] - row['DOB']).days/365)
        else:
            PH_qrtly_summary_df.loc[index, 'Average age of adult intake'] = pd.NaT

In [204]:
PH_qrtly_summary_df.columns

Index(['Client Name', 'DOB', 'Admission_dates', 'Program End Date_x',
       'Adults served', 'Children served', 'Average age of adult intake',
       'Average age of child intake', 'Households eligible to work in period',
       'Households with employment in period',
       ...
       'PCP 2021 QTR 3rd', 'PCP 2021 QTR 4th', 'Substance Use 2021 QTR 2nd',
       'Substance Use 2021 QTR 3rd', 'Substance Use 2021 QTR 4th',
       'Substance Use Provider 2021 QTR 1st',
       'Substance Use Provider 2021 QTR 2nd',
       'Substance Use Provider 2021 QTR 3rd',
       'Substance Use Provider 2021 QTR 4th',
       'Substance Use Provider 2021 2nd QTR'],
      dtype='object', length=140)

In [205]:
start = timeit.default_timer()

for index, row in PH_qrtly_summary_df.iterrows():
    start_date = row['Period_start_date']
    end_date = row['Period_end_date']
    adm_date = row['Admission_dates']
    dis_date = row['Program End Date_x']
    if pd.isna(dis_date):
        if adm_date > end_date:
            continue
        elif adm_date < start_date:
            PH_qrtly_summary_df.loc[index, 'Average length of stay in days - for all clients within period'] = (end_date - start_date).days
        elif start_date <= adm_date <= end_date:
            PH_qrtly_summary_df.loc[index, 'Average length of stay in days - for all clients within period'] = (end_date - adm_date).days
    elif ((adm_date < start_date) & (dis_date < start_date)) | ((adm_date > end_date) & (dis_date > end_date)):
        continue
    else:
        if (start_date <= adm_date <= end_date) & (start_date <= dis_date <= end_date):
            PH_qrtly_summary_df.loc[index, 'Average length of stay in days - for all clients within period'] = (dis_date - adm_date).days
        elif (adm_date < start_date) & (dis_date > end_date):
            PH_qrtly_summary_df.loc[index, 'Average length of stay in days - for all clients within period'] = (end_date - start_date).days
        elif (adm_date > start_date) & (dis_date > end_date):
            PH_qrtly_summary_df.loc[index, 'Average length of stay in days - for all clients within period'] = (end_date - adm_date).days
        elif (adm_date < start_date) & (dis_date < end_date):
            PH_qrtly_summary_df.loc[index, 'Average length of stay in days - for all clients within period'] = (dis_date - start_date).days
            
stop = timeit.default_timer()
    
print("Time: ", stop-start)

Time:  1.3526980000000037


In [206]:
start = timeit.default_timer()

for index, row in PH_qrtly_summary_df.iterrows():
    start_date = row['Period_start_date']
    end_date = row['Period_end_date']
    adm_date = row['Admission_dates']
    dis_date = row['Program End Date_x']
    if pd.isna(dis_date):
        continue
    elif start_date<=dis_date<=end_date:
        PH_qrtly_summary_df.loc[index, 'Average length of stay in days - from intake to discharge (dischared clients only)'] = (adm_date - dis_date).days
    else:
        PH_qrtly_summary_df.loc[index, 'Average length of stay in days - from intake to discharge (dischared clients only)'] = pd.NaT
stop = timeit.default_timer()
        
print("Time: ", stop-start)

Time:  0.8443790999999976


In [207]:
start = timeit.default_timer()

for index, row in PH_qrtly_summary_df.iterrows():
    start_date = row['Period_start_date']
    end_date = row['Period_end_date']
    adm_date = row['Admission_dates']
    dis_date = row['Program End Date_x']
    if pd.isna(dis_date):
        if adm_date > end_date:
            continue
        elif adm_date < start_date:
            PH_qrtly_summary_df.loc[index, 'Average length of stay in days - for all clients within period'] = (end_date - adm_date).days
        elif start_date <= adm_date <= end_date:
            PH_qrtly_summary_df.loc[index, 'Average length of stay in days - for all clients within period'] = (end_date - adm_date).days
    elif ((adm_date < start_date) & (dis_date < start_date)) | ((adm_date > end_date) & (dis_date > end_date)):
        continue
    else:
        if (start_date <= adm_date <= end_date) & (start_date <= dis_date <= end_date):
            PH_qrtly_summary_df.loc[index, 'Average length of stay in days - for all clients within period'] = (dis_date - adm_date).days
        elif (adm_date < start_date) & (dis_date > end_date):
            PH_qrtly_summary_df.loc[index, 'Average length of stay in days - for all clients within period'] = (end_date - adm_date).days
        elif (adm_date > start_date) & (dis_date > end_date):
            PH_qrtly_summary_df.loc[index, 'Average length of stay in days - for all clients within period'] = (end_date - adm_date).days
        elif (adm_date < start_date) & (dis_date < end_date):
            PH_qrtly_summary_df.loc[index, 'Average length of stay in days - for all clients within period'] = (dis_date - adm_date).days
            
stop = timeit.default_timer()
        
print("Time: ", stop-start)

Time:  1.2990716999999847


In [208]:
start = timeit.default_timer()

for index, row in PH_qrtly_summary_df.iterrows():
    start_date = row['Period_start_date']
    end_date = row['Period_end_date']
    adm_date = row['Admission_dates']
    dis_date = row['Program End Date_x']
    if pd.isna(dis_date):
        if adm_date > end_date:
            continue
        elif adm_date < start_date:
            PH_qrtly_summary_df.loc[index, 'Adults served'] = 1
        elif start_date <= adm_date <= end_date:
            PH_qrtly_summary_df.loc[index, 'Adults served'] = 1
    elif ((adm_date < start_date) & (dis_date < start_date)) | ((adm_date > end_date) & (dis_date > end_date)):
        continue
    else:
        if (start_date <= adm_date <= end_date) & (start_date <= dis_date <= end_date):
            PH_qrtly_summary_df.loc[index, 'Adults served'] = 1
        elif (adm_date < start_date) & (dis_date > end_date):
            PH_qrtly_summary_df.loc[index, 'Adults served'] = 1
        elif (adm_date >= start_date) & (dis_date > end_date):
            PH_qrtly_summary_df.loc[index, 'Adults served'] = 1
        elif (adm_date < start_date) & (dis_date <= end_date):
            PH_qrtly_summary_df.loc[index, 'Adults served'] = 1
            
stop = timeit.default_timer()

print('Time: ', stop-start)

Time:  1.346747999999991


In [261]:
for index, row in PH_qrtly_summary_df.iterrows():
    print(row['Client Name'])

Aimahlia Newsome
Aimahlia Newsome
Aimahlia Newsome
Aimahlia Newsome
Aimahlia Newsome
Anissa Delaney
Anissa Delaney
Anissa Delaney
Anissa Delaney
Anissa Delaney
Anissa Delaney
Anissa Delaney
Candyce Ward
Candyce Ward
Candyce Ward
Candyce Ward
Danielle Johnson
Danielle Johnson
Danielle Johnson
Danielle Johnson
Danielle Johnson
Jennifer Garcia
Jennifer Garcia
Jessica Cabral
Jessica Cabral
Jessica Cabral
Jessica Cabral
Jessica Cabral
Jully Harry Herrera
Jully Harry Herrera
Jully Harry Herrera
Jully Harry Herrera
Jully Harry Herrera
Jully Harry Herrera
Jully Harry Herrera
Jully Harry Herrera
Jully Harry Herrera
Jully Harry Herrera
Jully Harry Herrera
Jully Harry Herrera
Lacey Charles
Lacey Charles
Lacey Charles
Lacey Charles
Lacey Charles
Lacey Charles
Louise Bines
Louise Bines
Louise Bines
Narci Genao
Narci Genao
Cindy Ramkishun
Shadea Smith
Shadea Smith
Shadea Smith
Shadea Smith
Shadea Smith
Shadea Smith
Tiffany Rogers
Tiffany Rogers
Tiffany Rogers
Tiffany Rogers
Tiffany Rogers
Margaret G

Simonia Doyle
Simonia Doyle
Simonia Doyle
Simonia Doyle
Simonia Doyle
Simonia Doyle
Stephanie Demesa
Stephanie Demesa
Stephanie Demesa
Stephanie Demesa
Stephanie Demesa
Stephanie Demesa
Stephanie Demesa
Stephanie Demesa
Stephanie Demesa
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tabitha Hawkins
Tanika Wright
Tanika Wright
Tanika Wright
Tanika Wright
Tanika Wright
Tanika Wright
Tanika Wright
Tanika Wright
Tanika Wright
Tanika Wright
Tanika Wright
Tanika Wright
Tanika Wright
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Tawana Horton
Terrence 

Lennett Edwards
Raven Abrams
Raven Abrams
Raven Abrams
Raven Abrams
Raven Abrams
Suzette Fagan
Suzette Fagan
Suzette Fagan
Suzette Fagan
Suzette Fagan
Suzette Fagan
Suzette Fagan
Suzette Fagan
Suzette Fagan
Tinea Edwards
Tinea Edwards
Tinea Edwards
Tinea Edwards
Tinea Edwards
Carmen Rivera
Carmen Rivera
Carmen Rivera
Carmen Rivera
Jenna Mallett
Jenna Mallett
Jenna Mallett
Nicole Hudson
Nicole Hudson
Nicole Hudson
Nicole Hudson
Nicole Hudson
Trisha Housen
Trisha Housen
Trisha Housen
Lashawn Ford
Lashawn Ford
Jennifer Saintvil
Shamara Fields
Shamara Fields
Rosa Portelli
Lovely Petit
Lovely Petit
Lovely Petit
Lovely Petit
Jada Henderson
Jada Henderson
Jada Henderson
Jada Henderson
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsay
Denasia King Lindsa

In [209]:
PH_children_master_list_2.columns

Index(['Parent_Name', 'Child_FirstName', 'Child_LastName', 'Children's_Name',
       'DOB', 'DayCare_Start_Date', 'PreSchool_Start_Date',
       'Primary_School_Start_Date', 'Data Entry Date', 'admitDate', 'exitDate',
       'intakeAge'],
      dtype='object')

In [210]:
start = timeit.default_timer()

for index, row in PH_qrtly_summary_df.iterrows():
    filt = PH_children_master_list_2['Parent_Name'] == row['Client Name']
    child_intakeAge = PH_children_master_list_2.loc[filt, 'intakeAge']
    admitDate = PH_children_master_list_2.loc[filt, 'admitDate']

    for admitDate, child_intakeAge in zip(admitDate, child_intakeAge):
        
        if pd.isna(admitDate) | pd.isna(child_intakeAge):
            continue
        else:
            if row['Period_start_date'] <= admitDate <= row['Period_end_date']:
                PH_qrtly_summary_df.loc[index, 'Average age of child intake'] = child_intakeAge
                
stop = timeit.default_timer()

print('Time: ', stop - start)

Time:  1.8648593000000062


In [211]:
PH_qrtly_summary_df.head()

Client Name                  DOB Admission_dates Program End Date_x  \
0  Aimahlia Newsome  1992-03-04 00:00:00      2019-07-17         2020-07-08   
1  Aimahlia Newsome  1992-03-04 00:00:00      2019-07-17         2020-07-08   
2  Aimahlia Newsome  1992-03-04 00:00:00      2019-07-17         2020-07-08   
3  Aimahlia Newsome  1992-03-04 00:00:00      2019-07-17         2020-07-08   
4  Aimahlia Newsome  1992-03-04 00:00:00      2019-07-17         2020-07-08   

  Adults served Children served Average age of adult intake  \
0             1             NaN                          27   
1             1             NaN                         NaT   
2             1             NaN                         NaT   
3             1             NaN                         NaT   
4             1             NaN                         NaT   

  Average age of child intake Households eligible to work in period  \
0                         0.0                                   NaN   
1                         NaN                                   NaN   
2                         NaN                                   NaN   
3                         NaN                                   NaN   
4                         NaN                                   NaN   

  Households with employment in period  ... Substance Use 2021 QTR 2nd  \
0                                  NaN  ...                        NaN   
1                                  NaN  ...                        NaN   
2                                  NaN  ...                        NaN   
3                                  NaN  ...                        NaN   
4                                  NaN  ...                        NaN   

  Substance Use 2021 QTR 3rd Substance Use 2021 QTR 4th  \
0                        NaN                        NaN   
1                        NaN                        NaN   
2                        NaN                        NaN   
3                        NaN                        NaN   
4                        NaN                        NaN   

  Substance Use Provider 2021 QTR 1st Substance Use Provider 2021 QTR 2nd  \
0                                 NaN                                 NaN   
1                                 NaN                                 NaN   
2                                 NaN                                 NaN   
3                                 NaN                                 NaN   
4                                 NaN                                 NaN   

  Substance Use Provider 2021 QTR 3rd Substance Use Provider 2021 QTR 4th  \
0                                 NaN                                 NaN   
1                                 NaN                                 NaN   
2                                 NaN                                 NaN   
3                                 NaN                                 NaN   
4                                 NaN                                 NaN   

  Substance Use Provider 2021 2nd QTR  \
0                                 NaN   
1                                 NaN   
2                                 NaN   
3                                 NaN   
4                                 NaN   

  Average length of stay in days - for all clients within period  \
0                                               75.0               
1                                              167.0               
2                                              258.0               
3                                              349.0               
4                                              357.0               

  Average length of stay in days - from intake to discharge (dischared clients only)  
0                                                NaT                                  
1                                                NaT                                  
2                                                NaT                                

In [212]:
races = ['Asian/Pacific Islander', 'Black', 'Multi-Racial', 'White']
educations = ['No HSE/GED/High School', 'Some College', 'GED/HSE/HSD',
       'Post Graduate Degree', 'Bachelor’s Degree', 'Associates',
       "Bachelor's Degree"]
ethnicities = ['Non Hispanic', 'Hispanic']

In [213]:
start = timeit.default_timer()

for race in races:
    PH_qrtly_summary_df[f"Race: {race}"] = np.where((PH_qrtly_summary_df['Adults served']) == 1 & (PH_qrtly_summary_df['Race_x'] == race), 1, 0 )
    
for education in educations:
    PH_qrtly_summary_df[f"Education at intake: {education}"] = np.where((PH_qrtly_summary_df['Adults served']) == 1 & (PH_qrtly_summary_df['Education_x'] == education), 1, 0 )
for eth in ethnicities:
    if eth == 'Non Hispanic':
        PH_qrtly_summary_df[f"Ethnicity: {eth[:3]+'-'+eth[4:]}"] = np.where((PH_qrtly_summary_df['Adults served']) == 1 & (PH_qrtly_summary_df['Ethnicity_x'] == eth), 1, 0 )
    else:
         PH_qrtly_summary_df[f"Ethnicity: {eth}"] = np.where((PH_qrtly_summary_df['Adults served']) == 1 & (PH_qrtly_summary_df['Ethnicity_x'] == eth), 1, 0 )
    
stop = timeit.default_timer()

print('Time: ', stop - start)

Time:  0.050465500000001384


In [259]:
PH_qrtly_summary_df['Race: Black'].sum()

2058

In [214]:
PH_qrtly_summary_df['Program End Date_x'].all()

True

In [215]:
PH_qrtly_summary_df['Period_start_date'].isna().sum()

0

In [216]:
for col in PH_qrtly_summary_df.columns:
    if 'work' in col.lower():
        print(col)

Households eligible to work in period


In [217]:
housing_outcomes = ['AWL/Voluntary discharge', 'Independent living/permanent',
       'Independent', 'Death', 'Transfer', 'Involuntary discharge',
       'Voluntary Discharge', 'Ineligible']

In [218]:
PH_qrtly_summary_df['Housing outcome at discharge: Deceased'] = np.where(PH_qrtly_summary_df['Housing Status (at exit)'].isnull(), 0, 
         np.where(((PH_qrtly_summary_df['Housing Status (at exit)'] == 'Death') | (PH_qrtly_summary_df['Housing Status (at exit)'] == 'Deceased')), 1, 0))

PH_qrtly_summary_df['Housing outcome at discharge: AWOL/Back to shelter'] = np.where(PH_qrtly_summary_df['Housing Status (at exit)'].isnull(), 0, 
         np.where(((PH_qrtly_summary_df['Housing Status (at exit)'] == 'AWL/Voluntary discharge') | (PH_qrtly_summary_df['Housing Status (at exit)'] == 'AWOL')), 1, 0))

PH_qrtly_summary_df['Housing outcome at discharge: Independent living/permanent'] = np.where(PH_qrtly_summary_df['Housing Status (at exit)'].isnull(), 0, 
         np.where(((PH_qrtly_summary_df['Housing Status (at exit)'] == 'Independent living/permanent') | (PH_qrtly_summary_df['Housing Status (at exit)'] == 'Independent Living') | (PH_qrtly_summary_df['Housing Status (at exit)'] == 'Independent')), 1, 0))

PH_qrtly_summary_df['Housing outcome at discharge: Ineligible'] = np.where(PH_qrtly_summary_df['Housing Status (at exit)'].isnull(), 0, 
         np.where(((PH_qrtly_summary_df['Housing Status (at exit)'] =='Ineligible')), 1, 0))

PH_qrtly_summary_df['Housing outcome at discharge: Involuntary discharge'] = np.where(PH_qrtly_summary_df['Housing Status (at exit)'].isnull(), 0, 
         np.where(((PH_qrtly_summary_df['Housing Status (at exit)'] =='Transfer')), 1, 0))

PH_qrtly_summary_df['Housing outcome at discharge: Voluntary Discharge'] = np.where(PH_qrtly_summary_df['Housing Status (at exit)'].isnull(), 0, 
         np.where(((PH_qrtly_summary_df['Housing Status (at exit)'] =='Voluntary Discharge')), 1, 0))


In [219]:
PH_qrtly_summary_df['Housing outcome at discharge: AWOL/Back to shelter'] .sum()

21

In [220]:
PH_employment_master_df_2.columns

Index(['Client Name', 'Eligible to Work', 'Employment_StartDate',
       'Employer Name', 'Position', 'Employment Status',
       'Starting Salary (per hour)', 'Current/Ending Salary (per hour)',
       'Employment_EndDate', 'Employment End Reason', 'Off-The-Books',
       'Notes:'],
      dtype='object')

In [221]:
start = timeit.default_timer()


for index, row in PH_qrtly_summary_df.iterrows():
    filt = PH_employment_master_df_2['Client Name'] == row['Client Name']
    value = PH_employment_master_df_2.loc[filt, 'Eligible to Work'].values
    if value.size == 0:
        continue
    else:
        if (row['Adults served'] == 1) & (str(value[0]).lower() == 'yes'):
            PH_qrtly_summary_df.loc[index, 'Households eligible to work in period'] = 1

In [222]:
PH_qrtly_summary_df['Substance Use 2019 QTR 4th']

0                  NaN
1                  NaN
2                  NaN
3                  NaN
4                  NaN
5                  NaN
6                  NaN
7                  NaN
8                  NaN
9                  NaN
10                 NaN
11                 NaN
12                 NaN
13                 NaN
14                 NaN
15                 NaN
16                 NaN
17                 NaN
18                 NaN
19                 NaN
20                 NaN
21                 NaN
22                 NaN
23                 NaN
24                 NaN
25                 NaN
26                 NaN
27                 NaN
28                 NaN
29                 NaN
30                 NaN
31                 NaN
32                 NaN
33                 NaN
34                 NaN
35                 NaN
36                 NaN
37                 NaN
38                 NaN
39                 NaN
40                 NaN
41                 NaN
42                 NaN
43         

In [223]:
# start = timeit.default_timer()

# arr = []

# for i, column in enumerate(PH_qrtly_summary_df.columns):
#     if re.match('Substance Use \d{4} QTR \d\w{2}', str(column)):
        
# #         PH_qrtly_summary_df['Adults with active substance abuse 2'] = PH_qrtly_summary_df[column].apply(lambda x: 1 if str(x).lower() == 'yes - active' else 0)
#         try:
#             arr.append(np.where(PH_qrtly_summary_df[column].str.lower() == 'yes - active', 1, np.where(PH_qrtly_summary_df[PH_qrtly_summary_df.columns[i+1]].str.lower() == 'yes - active', 1, 0)))
#         except AttributeError:
#             arr.append(np.where(PH_qrtly_summary_df[column].astype(str).str.lower() == 'yes - active', 1, np.where(PH_qrtly_summary_df[PH_qrtly_summary_df.columns[i+1]].astype(str).str.lower() == 'yes - active', 1, 0)))
        
# stop = timeit.default_timer()

# print('Time: ', stop - start)

In [224]:
PH_qrtly_summary_df.loc[96]

Client Name                                                                               Adalberto Santiago
DOB                                                                                      1968-05-24 00:00:00
Admission_dates                                                                          2013-06-07 00:00:00
Program End Date_x                                                                                       NaT
Adults served                                                                                              1
Children served                                                                                          NaN
Average age of adult intake                                                                              NaT
Average age of child intake                                                                              NaN
Households eligible to work in period                                                                    NaN
Households with emp

In [225]:
PH_qrtly_summary_df.loc[3300]

Client Name                                                                                   Abbie Scott
DOB                                                                                   1990-12-28 00:00:00
Admission_dates                                                                       2021-05-06 00:00:00
Program End Date_x                                                                                    NaT
Adults served                                                                                           1
Children served                                                                                       NaN
Average age of adult intake                                                                           NaT
Average age of child intake                                                                           NaN
Households eligible to work in period                                                                 NaN
Households with employment in period          

In [226]:
currQuarter = int((admit_date.month-1)/3+1)
dtfirstDay = datetime.datetime(admit_date.year, 3 * currQuarter - 2, 1)

In [227]:
PH_qrtly_summary_df.iloc[:,[1,2,10]]

DOB Admission_dates Adults with mental health needs
0     1992-03-04 00:00:00      2019-07-17                             NaN
1     1992-03-04 00:00:00      2019-07-17                             NaN
2     1992-03-04 00:00:00      2019-07-17                             NaN
3     1992-03-04 00:00:00      2019-07-17                             NaN
4     1992-03-04 00:00:00      2019-07-17                             NaN
5     1993-09-09 00:00:00      2019-02-14                             NaN
6     1993-09-09 00:00:00      2019-02-14                             NaN
7     1993-09-09 00:00:00      2019-02-14                             NaN
8     1993-09-09 00:00:00      2019-02-14                             NaN
9     1993-09-09 00:00:00      2019-02-14                             NaN
10    1993-09-09 00:00:00      2019-02-14                             NaN
11    1993-09-09 00:00:00      2019-02-14                             NaN
12    1986-08-14 00:00:00      2019-07-05                             NaN
13    1986-08-14 00:00:00      2019-07-05                             NaN
14    1986-08-14 00:00:00      2019-07-05                             NaN
15    1986-08-14 00:00:00      2019-07-05                             NaN
16    1981-05-21 00:00:00      2019-07-15                             NaN
17    1981-05-21 00:00:00      2019-07-15                             NaN
18    1981-05-21 00:00:00      2019-07-15                             NaN
19    1981-05-21 00:00:00      2019-07-15                             NaN
20    1981-05-21 00:00:00      2019-07-15                             NaN
21    1997-05-19 00:00:00      2019-11-15                             NaN
22    1997-05-19 00:00:00      2019-11-15                             NaN
23    1995-08-28 00:00:00      2019-05-04                             NaN
24    1995-08-28 00:00:00      2019-05-04                             NaN
25    1995-08-28 00:00:00      2019-05-04                             NaN
26    1995-08-28 00:00:00      2019-05-04                             NaN
27    1995-08-28 00:00:00      2019-05-04                             NaN
28    1997-05-29 00:00:00      2019-02-10                             NaN
29    1997-05-29 00:00:00      2019-02-10                             NaN
30    1997-05-29 00:00:00      2019-02-10                             NaN
31    1997-05-29 00:00:00      2019-02-10                             NaN
32    1997-05-29 00:00:00      2019-02-10                             NaN
33    1997-05-29 00:00:00      2019-02-10                             NaN
34    1997-05-29 00:00:00      2019-02-10                             NaN
35    1997-05-29 00:00:00      2019-02-10                             NaN
36    1997-05-29 00:00:00      2019-02-10                             NaN
37    1997-05-29 00:00:00      2019-02-10                             NaN
38    1997-05-29 00:00:00      2019-02-10                             NaN
39    1997-05-29 00:00:00      2019-02-10                             NaN
40    1994-11-16 00:00:00      2019-04-15                             NaN
41    1994-11-16 00:00:00      2019-04-15                             NaN
42    1994-11-16 00:00:00      2019-04-15                             NaN
43    1994-11-16 00:00:00      2019-04-15                             NaN
44    1994-11-16 00:00:00      2019-04-15                             NaN
45    1994-11-16 00:00:00      2019-04-15                             NaN
46    1995-01-27 00:00:00      2019-10-13                             NaN
47    1995-01-27 00:00:00      2019-10-13                             NaN
48    1995-01-27 00:00:00      2019-10-13                             NaN
49    1994-03-29 00:00:00      2020-05-28                             NaN
50    1994-03-29 00:00:00      2020-05-28                             NaN
51    1994-11-11 00:00:00      2020-08-21                             NaN
52    1997-03-31 00:00:00      2020-07-22                             NaN
53    1997-03-31 00:00:00 

In [228]:
indx = [col for col in PH_qrtly_summary_df.columns if  re.match('substance use \d{4} qtr \d\w{2}', str(col).lower())]
indx.insert(0,'Period_start_date')

In [229]:
indx

['Period_start_date',
 'Substance Use 2020 QTR 1st',
 'Substance Use 2020 QTR 2nd',
 'Substance Use 2020 QTR 3rd',
 'Substance Use 2020 QTR 4th',
 'Substance Use 2019 QTR 1st',
 'Substance Use 2019 QTR 2nd',
 'Substance Use 2019 QTR 3rd',
 'Substance Use 2019 QTR 4th',
 'Substance Use 2021 QTR 1st',
 'Substance Use 2021 QTR 2nd',
 'Substance Use 2021 QTR 3rd',
 'Substance Use 2021 QTR 4th']

In [230]:
PH_qrtly_summary_df.loc[:,indx]

Period_start_date Substance Use 2020 QTR 1st Substance Use 2020 QTR 2nd  \
0           2019-07-01                        NaN                        NaN   
1           2019-10-01                        NaN                        NaN   
2           2020-01-01                        NaN                        NaN   
3           2020-04-01                        NaN                        NaN   
4           2020-07-01                         No                         No   
5           2019-01-01                        NaN                        NaN   
6           2019-04-01                        NaN                        NaN   
7           2019-07-01                        NaN                        NaN   
8           2019-10-01                        NaN                        NaN   
9           2020-01-01                        NaN                        NaN   
10          2020-04-01                        NaN                        NaN   
11          2020-07-01                         No                         No   
12          2019-07-01                        NaN                        NaN   
13          2019-10-01                        NaN                        NaN   
14          2020-01-01                        NaN                        NaN   
15          2020-04-01                        NaN                        NaN   
16          2019-07-01                        NaN                        NaN   
17          2019-10-01                        NaN                        NaN   
18          2020-01-01                        NaN                        NaN   
19          2020-04-01                        NaN                        NaN   
20          2020-07-01                         No                         No   
21          2019-10-01                        NaN                        NaN   
22          2020-01-01                        NaN                        NaN   
23          2019-04-01                        NaN                        NaN   
24          2019-07-01                        NaN                        NaN   
25          2019-10-01                        NaN                        NaN   
26          2020-01-01                        NaN                        NaN   
27          2020-04-01                        NaN                        NaN   
28          2019-01-01                        NaN                        NaN   
29          2019-04-01                        NaN                        NaN   
30          2019-07-01                        NaN                        NaN   
31          2019-10-01                        NaN                        NaN   
32          2020-01-01                        NaN                        NaN   
33          2020-04-01                        NaN                        NaN   
34          2020-07-01                         No                         No   
35          2020-10-01                        NaN                        NaN   
36          2021-01-01                        NaN                        NaN   
37          2021-04-01                        NaN                        NaN   
38          2021-07-01                        NaN                        NaN   
39          2021-10-01                        NaN                        NaN   
40          2019-04-01                        NaN                        NaN   
41          2019-07-01                        NaN                        NaN   
42          2019-10-01                        NaN                        NaN   
43          2020-01-01                        NaN                        NaN   
44          2020-04-01                        NaN                        NaN   
45          2020-07-01                         No                         No   
46          2019-10-01                        NaN                        NaN   
47          2020-01-01                        NaN                        NaN   
48          2020-04-01                        NaN                        NaN   
49   

In [231]:
# start = timeit.default_timer()

# cols = [col for col in PH_qrtly_summary_df.columns if  re.match('Substance Use \d{4} QTR \d\w{2}', str(col))]
# cols.append('Period_start_date')




# [PH_qrtly_summary_df.columns.get_loc(col) for col in PH_qrtly_summary_df.columns]

# for column in PH_qrtly_summary_df.columns:
#     if re.match('Substance Use \d{4} QTR \d\w{2}', str(column)):
#         PH_qrtly_summary_df.columns.get_loc(col)


# arr = []


# for column in PH_qrtly_summary_df.columns:
#     if re.match('substance use \d{4} qtr \d\w{2}', str(column).lower()):
#         year = int(column[14:18])
#         quarter = int(column[-3])
#         dtfirstDay = datetime.datetime(year, 3 * quarter - 2, 1)
#         if np.where((PH_qrtly_summary_df[column].astype(str).str.lower() == 'yes - active') & (PH_qrtly_summary_df['Period_start_date'] == dtfirstDay), 1, 0) == 1
        
#         PH_qrtly_summary_df['Adults with active substance abuse 2'] = np.where((PH_qrtly_summary_df[column].astype(str).str.lower() == 'yes - active') & (PH_qrtly_summary_df['Period_start_date'] == dtfirstDay), 1, 0)

        
# stop = timeit.default_timer()

# print('Time: ', stop - start)


In [232]:
PH_qrtly_summary_df.loc[258]

Client Name                                                                                Calvin Johnson
DOB                                                                                   1969-12-28 00:00:00
Admission_dates                                                                       2019-12-31 00:00:00
Program End Date_x                                                                                    NaT
Adults served                                                                                           1
Children served                                                                                       NaN
Average age of adult intake                                                                           NaT
Average age of child intake                                                                           NaN
Households eligible to work in period                                                                 NaN
Households with employment in period          

In [233]:
'Substance Use 2021 QTR 1st'[-3]

'1'

In [234]:
type(pd.to_datetime('Substance Use 2021 QTR 1st'[14:18], format='%Y').year)

int

In [235]:
test2 = np.where((PH_qrtly_summary_df['Substance Use 2021 QTR 1st'].str.lower() == 'yes - active'), 1, 0) 

In [236]:
test2.sum()

98

In [237]:
PH_qrtly_summary_df['Adults with active substance abuse'] = np.where((PH_qrtly_summary_df['Substance Use 2020 QTR 1st'].str.lower() == 'yes - active') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2020')), 1, 
                np.where((PH_qrtly_summary_df['Substance Use 2020 QTR 2nd'].str.lower() == 'yes - active')& (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2020')), 1,
                         np.where((PH_qrtly_summary_df['Substance Use 2020 QTR 3rd'].str.lower() == 'yes - active') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2020')), 1,
                                 np.where((PH_qrtly_summary_df['Substance Use 2020 QTR 4th'].str.lower() == 'yes - active') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2020')), 1, 
                                          np.where((PH_qrtly_summary_df['Substance Use 2019 QTR 1st'].str.lower() == 'yes - active') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2019')), 1,
                                                  np.where((PH_qrtly_summary_df['Substance Use 2019 QTR 2nd'].str.lower() == 'yes - active') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2019')), 1,
                                                          np.where((PH_qrtly_summary_df['Substance Use 2019 QTR 3rd'].str.lower() == 'yes - active') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2019')), 1,
                                                                  np.where((PH_qrtly_summary_df['Substance Use 2019 QTR 4th'].str.lower() == 'yes - active') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2019')), 1,
                                                                           np.where((PH_qrtly_summary_df['Substance Use 2021 QTR 1st'].str.lower() == 'yes - active')& (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2021')), 1,
                                                                                    np.where((PH_qrtly_summary_df['Substance Use 2021 QTR 2nd'].str.lower() == 'yes - active') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2021')), 1,
                                                                                             np.where((PH_qrtly_summary_df['Substance Use 2021 QTR 3rd'].astype(str).str.lower() == 'yes - active') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2021')), 1,
                                                                                                      np.where((PH_qrtly_summary_df['Substance Use 2021 QTR 4th'].astype(str).str.lower() == 'yes - active') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2021')), 1,0))))))))))))


In [256]:
PH_qrtly_summary_df['Adults with active substance abuse'].sum()

136

In [239]:
PH_qrtly_summary_df['Adults in recovery'] = np.where((PH_qrtly_summary_df['Substance Use 2020 QTR 1st'].str.lower() == 'yes - recovery') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2020')), 1, 
                np.where((PH_qrtly_summary_df['Substance Use 2020 QTR 2nd'].str.lower() == 'yes - recovery') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2020')), 1,
                         np.where((PH_qrtly_summary_df['Substance Use 2020 QTR 3rd'].str.lower() == 'yes - recovery') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2020')), 1,
                                 np.where((PH_qrtly_summary_df['Substance Use 2020 QTR 4th'].str.lower() == 'yes - recovery') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2020')), 1, 
                                          np.where((PH_qrtly_summary_df['Substance Use 2019 QTR 1st'].str.lower() == 'yes - recovery') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2019')), 1,
                                                  np.where((PH_qrtly_summary_df['Substance Use 2019 QTR 2nd'].str.lower() == 'yes - recovery') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2019')), 1,
                                                          np.where((PH_qrtly_summary_df['Substance Use 2019 QTR 3rd'].str.lower() == 'yes - recovery') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2019')), 1,
                                                                  np.where((PH_qrtly_summary_df['Substance Use 2019 QTR 4th'].str.lower() == 'yes - recovery') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2019')), 1,
                                                                           np.where((PH_qrtly_summary_df['Substance Use 2021 QTR 1st'].str.lower() == 'yes - recovery') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2021')), 1,
                                                                                    np.where((PH_qrtly_summary_df['Substance Use 2021 QTR 2nd'].str.lower() == 'yes - recovery')  & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2021')), 1,
                                                                                             np.where((PH_qrtly_summary_df['Substance Use 2021 QTR 3rd'].astype(str).str.lower() == 'yes - recovery') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2021')), 1,
                                                                                                      np.where((PH_qrtly_summary_df['Substance Use 2021 QTR 4th'].astype(str).str.lower() == 'yes - recovery') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2021')), 1,0))))))))))))

In [240]:
PH_qrtly_summary_df['Adults in recovery'].sum()

73

In [241]:
filt = PH_qrtly_summary_df['Adults with active substance abuse'] == 1
PH_qrtly_summary_df.loc[filt]

Client Name                  DOB Admission_dates  \
93         Adalberto Santiago  1968-05-24 00:00:00      2013-06-07   
94         Adalberto Santiago  1968-05-24 00:00:00      2013-06-07   
95         Adalberto Santiago  1968-05-24 00:00:00      2013-06-07   
96         Adalberto Santiago  1968-05-24 00:00:00      2013-06-07   
139              Alice Joseph  1963-05-29 00:00:00      2013-07-31   
140              Alice Joseph  1963-05-29 00:00:00      2013-07-31   
141              Alice Joseph  1963-05-29 00:00:00      2013-07-31   
142              Alice Joseph  1963-05-29 00:00:00      2013-07-31   
180           Ashley Nimchick  1984-06-05 00:00:00      2019-10-15   
181           Ashley Nimchick  1984-06-05 00:00:00      2019-10-15   
182           Ashley Nimchick  1984-06-05 00:00:00      2019-10-15   
183           Ashley Nimchick  1984-06-05 00:00:00      2019-10-15   
194             Barry Whitman  1969-12-13 00:00:00      2018-09-21   
195             Barry Whitman  1969-12-13 00:00:00      2018-09-21   
196             Barry Whitman  1969-12-13 00:00:00      2018-09-21   
197             Barry Whitman  1969-12-13 00:00:00      2018-09-21   
241           Brenda Melendez  1980-01-21 00:00:00      2019-10-15   
256            Calvin Johnson  1969-12-28 00:00:00      2019-12-31   
277              Darryl James  1990-04-20 00:00:00      2019-12-31   
278              Darryl James  1990-04-20 00:00:00      2019-12-31   
279              Darryl James  1990-04-20 00:00:00      2019-12-31   
280              Darryl James  1990-04-20 00:00:00      2019-12-31   
342              Deborah Ross  1975-04-24 00:00:00      2013-06-11   
344              Deborah Ross  1975-04-24 00:00:00      2013-06-11   
377            Deira Figueroa  1978-10-24 00:00:00      2013-06-18   
378            Deira Figueroa  1978-10-24 00:00:00      2013-06-18   
379            Deira Figueroa  1978-10-24 00:00:00      2013-06-18   
385          Dominique Warren  1991-12-10 00:00:00      2019-10-15   
386          Dominique Warren  1991-12-10 00:00:00      2019-10-15   
387          Dominique Warren  1991-12-10 00:00:00      2019-10-15   
442        Elizabeth Harrison  1958-10-24 00:00:00      2019-12-31   
443        Elizabeth Harrison  1958-10-24 00:00:00      2019-12-31   
444        Elizabeth Harrison  1958-10-24 00:00:00      2019-12-31   
445        Elizabeth Harrison  1958-10-24 00:00:00      2019-12-31   
476                Ethan Ward  1962-09-01 00:00:00      2013-07-31   
477                Ethan Ward  1962-09-01 00:00:00      2013-07-31   
478                Ethan Ward  1962-09-01 00:00:00      2013-07-31   
479                Ethan Ward  1962-09-01 00:00:00      2013-07-31   
501                Gary Isaac  1961-12-31 00:00:00      2015-11-09   
502                Gary Isaac  1961-12-31 00:00:00      2015-11-09   
503                Gary Isaac  1961-12-31 00:00:00      2015-11-09   
504                Gary Isaac  1961-12-31 00:00:00      2015-11-09   
537           Georgina Deaton  1953-11-03 00:00:00      2013-06-13   
538           Georgina Deaton  1953-11-03 00:00:00      2013-06-13   
571         Hanif Abdurrashid  1966-03-03 00:00:00      2013-06-14   
595          Irena Zdrodowska  1947-03-10 00:00:00      2014-11-07   
596          Irena Zdrodowska  1947-03-10 00:00:00      2014-11-07   
597          Irena Zdrodowska  1947-03-10 00:00:00      2014-11-07   
598          Irena Zdrodowska  1947-03-10 00:00:00      2014-11-07   
604          Jeanette Covollo  1977-10-28 00:00:00      2019-10-17   
605          Jeanette Covollo  1977-10-28 00:00:00      2019-10-17   
606          Jeanette Covollo  1977-10-28 00:00:00      2019-10-17   
607          Jeanette Covollo  1977-10-28 00:00:00      2019-10-17   
613           Jessica Leonard  1989-05-31 00:00:00      2019-12-31   
614           Jessica Leonard  1989-05-31 00:00:00      2019-12-31   
615           Jessica Leonard  1989-05-31 00:00:00      2019-12-31   
616           Jessica Leonar

In [242]:
pd.to_datetime('10/1/2021').strftime('%m%d')

'1001'

In [243]:
for col in PH_qrtly_summary_df.columns:
    if 'mental health needs' in col.lower():
        print(col)

Adults with mental health needs
Mental Health Needs 2020 QTR 1st
Mental Health Needs 2020 QTR 2nd
Mental Health Needs 2020 QTR 3rd
Mental Health Needs 2020 QTR 4th
Mental Health Needs at intake
Mental Health Needs 2019 QTR 1st
Mental Health Needs 2019 QTR 2nd
Mental Health Needs 2019 QTR 3rd
Mental Health Needs 2019 QTR 4th
Mental Health Needs 2021 QTR 1st
Mental Health Needs 2021 QTR 2nd
Mental Health Needs 2021 QTR 3rd
Mental Health Needs 2021 QTR 4th


In [244]:
PH_qrtly_summary_df['Adults with mental health needs'] = np.where((PH_qrtly_summary_df['Mental Health Needs 2020 QTR 1st'].str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2020')), 1,
                np.where((PH_qrtly_summary_df['Mental Health Needs 2020 QTR 2nd'].str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2020')), 1,
                     np.where((PH_qrtly_summary_df['Mental Health Needs 2020 QTR 3rd'].str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2020')), 1,
                          np.where((PH_qrtly_summary_df['Mental Health Needs 2020 QTR 4th'].str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2020')), 1,
                                 np.where((PH_qrtly_summary_df['Mental Health Needs 2019 QTR 1st'].str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2019')), 1,
                                         np.where((PH_qrtly_summary_df['Mental Health Needs 2019 QTR 1st'].str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2019')), 1,
                                             np.where((PH_qrtly_summary_df['Mental Health Needs 2019 QTR 2nd'].str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2019')), 1,                                                                                    
                                                 np.where((PH_qrtly_summary_df['Mental Health Needs 2019 QTR 3rd'].str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2019')), 1, 
                                                     np.where((PH_qrtly_summary_df['Mental Health Needs 2019 QTR 4th'].str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2019')), 1,                                                                                           
                                                         np.where((PH_qrtly_summary_df['Mental Health Needs 2021 QTR 1st'].str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2021')), 1,   
                                                            np.where((PH_qrtly_summary_df['Mental Health Needs 2021 QTR 2nd'].str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2021')), 1,
                                                                 np.where((PH_qrtly_summary_df['Mental Health Needs 2021 QTR 3rd'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2021')), 1,                                                                                   
                                                                     np.where((PH_qrtly_summary_df['Mental Health Needs 2021 QTR 4th'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2021')), 1, 0)))))))))))))                                                                              
                                                                                                                                                    
                                                                                                                                                    

In [257]:
PH_qrtly_summary_df['Adults with mental health needs'].sum()

352

In [246]:
cols

["Client's First Name",
 "Client's Last Name",
 'Client Name',
 'welligent_id',
 'airtable_id',
 'Admission Date',
 'Program End Date',
 'Housing Status (at exit)',
 'program',
 'Location',
 'client_type']

In [247]:
indx = [col for col in PH_qrtly_summary_df.columns if  re.match('mental health needs qtr \d\w{2}', str(col).lower())]
indx.insert(0,'Period_start_date')

In [248]:
filt = PH_qrtly_summary_df['Client Name'] == 'Aimahlia Newsome'
PH_qrtly_summary_df.loc[filt, indx]

Period_start_date
0        2019-07-01
1        2019-10-01
2        2020-01-01
3        2020-04-01
4        2020-07-01

In [249]:
PH_qrtly_summary_df.loc[94]

Client Name                                                                               Adalberto Santiago
DOB                                                                                      1968-05-24 00:00:00
Admission_dates                                                                          2013-06-07 00:00:00
Program End Date_x                                                                                       NaT
Adults served                                                                                              1
Children served                                                                                          NaN
Average age of adult intake                                                                              NaT
Average age of child intake                                                                              NaN
Households eligible to work in period                                                                    NaN
Households with emp

In [250]:
PH_qrtly_summary_df.loc[:, indx]

Period_start_date
0           2019-07-01
1           2019-10-01
2           2020-01-01
3           2020-04-01
4           2020-07-01
5           2019-01-01
6           2019-04-01
7           2019-07-01
8           2019-10-01
9           2020-01-01
10          2020-04-01
11          2020-07-01
12          2019-07-01
13          2019-10-01
14          2020-01-01
15          2020-04-01
16          2019-07-01
17          2019-10-01
18          2020-01-01
19          2020-04-01
20          2020-07-01
21          2019-10-01
22          2020-01-01
23          2019-04-01
24          2019-07-01
25          2019-10-01
26          2020-01-01
27          2020-04-01
28          2019-01-01
29          2019-04-01
30          2019-07-01
31          2019-10-01
32          2020-01-01
33          2020-04-01
34          2020-07-01
35          2020-10-01
36          2021-01-01
37          2021-04-01
38          2021-07-01
39          2021-10-01
40          2019-04-01
41          2019-07-01
42          2019-10-01
43          2020-01-01
44          2020-04-01
45          2020-07-01
46          2019-10-01
47          2020-01-01
48          2020-04-01
49          2020-04-01
50          2020-07-01
51          2020-07-01
52          2020-07-01
53          2020-10-01
54          2021-01-01
55          2021-04-01
56          2021-07-01
57          2021-10-01
58          2020-10-01
59          2021-01-01
60          2021-04-01
61          2021-07-01
62          2021-10-01
63          2020-10-01
64          2013-04-01
65          2013-07-01
66          2013-10-01
67          2014-01-01
68          2014-04-01
69          2014-07-01
70          2014-10-01
71          2015-01-01
72          2015-04-01
73          2015-07-01
74          2015-10-01
75          2016-01-01
76          2016-04-01
77          2016-07-01
78          2016-10-01
79          2017-01-01
80          2017-04-01
81          2017-07-01
82          2017-10-01
83          2018-01-01
84          2018-04-01
85          2018-07-01
86          2018-10-01
87          2019-01-01
88          2019-04-01
89          2019-07-01
90          2019-10-01
91          2020-01-01
92          2020-04-01
93          2020-07-01
94          2020-10-01
95          2021-01-01
96          2021-04-01
97          2021-07-01
98          2021-10-01
99          2013-07-01
100         2013-10-01
101         2014-01-01
102         2014-04-01
103         2014-07-01
104         2014-10-01
105         2015-01-01
106         2015-04-01
107         2015-07-01
108         2015-10-01
109         2016-01-01
110         2016-04-01
111         2013-07-01
112         2013-10-01
113         2014-01-01
114         2014-04-01
115         2014-07-01
116         2014-10-01
117         2015-01-01
118         2015-04-01
119         2015-07-01
120         2015-10-01
121         2016-01-01
122         2016-04-01
123         2016-07-01
124         2016-10-01
125         2017-01-01
126         2017-04-01
127         2017-07-01
128         2017-10-01
129         2018-01-01
130         2018-04-01
131         2018-07-01
132         2018-10-01
133         2019-01-01
134         2019-04-01
135         2019-07-01
136         2019-10-01
137         2020-01-01
138         2020-04-01
139         2020-07-01
140         2020-10-01
141         2021-01-01
142         2021-04-01
143         2021-07-01
144         2021-10-01
145         2014-10-01
146         2015-01-01
147         2015-04-01
148         2015-07-01
149         2015-10-01
150         2016-01-01
151         2016-04-01
152         2016-07-01
153         2016-10-01
154         2017-01-01
155         2017-04-01
156         2017-07-01
157         2017-10-01
158         2018-01-01
159         2018-04-01
160         2018-07-01
161         2018-10-01
162         2019-01-01
163         2019-04-01
164         2019-07-01
165         2019-10-01
166         2020-01-01
167         2020-04-01
168         2020-07-01
169         2020-10-01
170         2021-01-01
171         2021-04-01
172         2021-07-01
173

In [251]:
PH_qrtly_summary_df['Number of above connected with mental health service provider'] = np.where((PH_qrtly_summary_df['MHP 2020 QTR 1st'].str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2020')), 1, 
                np.where((PH_qrtly_summary_df['MHP 2020 QTR 2nd'].str.lower() == 'yes')& (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2020')), 1,
                         np.where((PH_qrtly_summary_df['MHP 2020 QTR 3rd'].str.lower() == 'yes')& (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2020')), 1,
                                 np.where((PH_qrtly_summary_df['MHP 2020 QTR 4th'].str.lower() == 'yes')& (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2020')), 1, 
                                          np.where((PH_qrtly_summary_df['MHP 2019 QTR 1st'].str.lower() == 'yes')& (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2019')), 1,
                                                  np.where((PH_qrtly_summary_df['MHP 2019 QTR 2nd'].str.lower() == 'yes')& (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2019')), 1,
                                                          np.where((PH_qrtly_summary_df['MHP 2019 QTR 3rd'].str.lower() == 'yes')& (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2019')), 1,
                                                                  np.where((PH_qrtly_summary_df['MHP 2019 QTR 4th'].str.lower() == 'yes') &(PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2019')), 1,
                                                                           np.where((PH_qrtly_summary_df['MHP 2021 QTR 1st'].str.lower() == 'yes')& (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2021')), 1,
                                                                                    np.where((PH_qrtly_summary_df['MHP 2021 QTR 2nd'].str.lower() == 'yes')& (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2021')), 1,
                                                                                             np.where((PH_qrtly_summary_df['MHP 2021 QTR 3rd'].astype(str).str.lower() == 'yes') &(PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2021')), 1,
                                                                                                      np.where((PH_qrtly_summary_df['MHP 2021 QTR 4th'].astype(str).str.lower() == 'yes') &(PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2021')), 1,0))))))))))))

In [252]:
PH_qrtly_summary_df['Number of above connected with mental health service provider'].sum()

261

In [253]:
PH_qrtly_summary_df['Residents connected with medical provider in period'] = np.where((PH_qrtly_summary_df['PCP 2020 QTR 1st'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2020')), 1, 
                np.where((PH_qrtly_summary_df['PCP 2020 QTR 2nd'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2020')), 1,
                         np.where((PH_qrtly_summary_df['PCP 2020 QTR 3rd'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2020')), 1,
                                 np.where((PH_qrtly_summary_df['PCP 2020 QTR 4th'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2020')), 1, 
                                          np.where((PH_qrtly_summary_df['PCP 2019 QTR 1st'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2019')), 1,
                                                  np.where((PH_qrtly_summary_df['PCP 2019 QTR 2nd'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2019')), 1,
                                                          np.where((PH_qrtly_summary_df['PCP 2019 QTR 3rd'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2019')), 1,
                                                                  np.where((PH_qrtly_summary_df['PCP 2019 QTR 4th'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2019')), 1,
                                                                           np.where((PH_qrtly_summary_df['PCP 2021 QTR 1st'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('1/1/2021')), 1,
                                                                                    np.where((PH_qrtly_summary_df['PCP 2021 QTR 2nd'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('4/1/2021')), 1,
                                                                                             np.where((PH_qrtly_summary_df['PCP 2021 QTR 3rd'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('7/1/2021')), 1,
                                                                                                      np.where((PH_qrtly_summary_df['PCP 2021 QTR 4th'].astype(str).str.lower() == 'yes') & (PH_qrtly_summary_df['Period_start_date'] == pd.to_datetime('10/1/2021')), 1,0))))))))))))

In [254]:
PH_qrtly_summary_df['Residents connected with medical provider in period'].sum()

352

In [255]:
for col in PH_qrtly_summary_df.columns:
    if 'pcp' in col.lower() and 'provider' not in col.lower():
        print(col)

PCP 2020 QTR 1st
PCP 2020 QTR 2nd
PCP 2020 QTR 3rd
PCP 2020 QTR 4th
PCP Upon Leaving
PCP at intake
PCP 2019 QTR 1st
PCP 2019 QTR 2nd
PCP 2019 QTR 3rd
PCP 2019 QTR 4th
PCP 2021 QTR 1st
PCP 2021 QTR 2nd
PCP 2021 QTR 3rd
PCP 2021 QTR 4th


In [263]:
PH_employment_master_df_2.columns

Index(['Client Name', 'Eligible to Work', 'Employment_StartDate',
       'Employer Name', 'Position', 'Employment Status',
       'Starting Salary (per hour)', 'Current/Ending Salary (per hour)',
       'Employment_EndDate', 'Employment End Reason', 'Off-The-Books',
       'Notes:'],
      dtype='object')

In [274]:
dup_names = []

for index, row in PH_qrtly_summary_df.iterrows():
    name = row['Client Name']
    if PH_employment_master_df_2['Client Name'].to_list().count(name) > 1:
        dup_names.append(name)
    else:
        filt = PH_employment_master_df_2['Client Name'] == row['Client Name']
        value = PH_employment_master_df_2.loc[filt, 'Eligible to Work'].values
        if value.size == 0:
            continue
        else:
            if str(value[0]).lower() == 'yes':
                PH_qrtly_summary_df.loc[index, 'Households eligible to work in period'] = 1
print('Duplicated names on employment master df:', set(dup_names), sep = '\n')            

Duplicated names on employment master df
{'Shakeia Dean', 'Kadian Whyte', 'Dominique Warren', 'Gary Isaac', 'Tawana Horton', 'Donald Hart', 'Rebecca Mosely', 'Donna Pickersgill-Brown', 'Deira Figueroa', 'Latoya Herndon-Ford', 'Ashley Mazyck', 'Jackelyne Fernandez', 'Rashima Wilson', 'Barry Whitman', 'Robert Frager', 'Danielle Johnson', 'Louise Bines', 'Jully Harry Herrera', 'Fatasia Petties', 'Leticia Navarrete'}


In [ ]:
# number of children

# Reports export

In [ ]:
try:
    PH_Master_Client_list_2.to_csv(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\reports\PH_Master_Client_list_2.csv')
except FileNotFoundError:
    PH_Master_Client_list_2.to_csv(r'C:\Users\edwar\PH_data\reports\PH_Master_Client_list_2.csv')

In [ ]:
try:
    PH_clients_pograms_2.to_csv(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\reports\PH_clients_pograms_2.csv')
except FileNotFoundError:
    PH_clients_pograms_2.to_csv(r'C:\Users\edwar\PH_data\reports\PH_clients_pograms_2.csv')

In [ ]:
try:
    PH_children_master_list_2.to_csv(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\reports\PH_children_master_list_2.csv')
except FileNotFoundError:
    PH_children_master_list_2.to_csv(r'C:\Users\edwar\PH_data\reports\PH_children_master_list_2.csv')

In [ ]:
try:
    PH_employment_master_df_2.to_csv(r'\\appserv\UserShares\dejesuse\My Documents\PH tables\reports\PH_employment_master_df_2.csv')
except FileNotFoundError:
    PH_employment_master_df_2.to_csv(r'C:\Users\edwar\PH_data\reports\PH_employment_master_df_2.csv')